# Preparing Data for Machine Learning
The asthma emergency department visit data for California is loaded, transformed to separate by demographics, and cleaned. The correspondings air quality summaries for the location and time of each row are pulled from the EPA AQS API and attached to the asthma data. The combined data is written to a SQL database for later use in training a ML model.

## EXTRACT

## 1. Load asthma data from the data lake.

In [0]:
storageAccount = "gen10datafund2111"
storageContainer = "jadr-health-insights"
clientSecret = dbutils.secrets.get(scope = "jadr_blob", key = "clientSecret")
clientid = dbutils.secrets.get(scope = "jadr_blob", key = "clientid")
mount_point = "/mnt/darrellgerber/jadr"


configs = {"fs.azure.account.auth.type": "OAuth",
       "fs.azure.account.oauth.provider.type": "org.apache.hadoop.fs.azurebfs.oauth2.ClientCredsTokenProvider",
       "fs.azure.account.oauth2.client.id": clientid,
       "fs.azure.account.oauth2.client.secret": clientSecret,
       "fs.azure.account.oauth2.client.endpoint": "https://login.microsoftonline.com/d46b54b2-a652-420b-aa5a-2ef7f8fc706e/oauth2/token",
       "fs.azure.createRemoteFileSystemDuringInitialization": "true"}

try: 
    dbutils.fs.unmount(mount_point)
except:
    pass

dbutils.fs.mount(
    source = "abfss://"+storageContainer+"@"+storageAccount+".dfs.core.windows.net/",
    mount_point = mount_point,
    extra_configs = configs)
display(dbutils.fs.ls(mount_point))

/mnt/darrellgerber/jadr has been unmounted.

path name size modificationTime dbfs:/mnt/darrellgerber/jadr/Data/ Data/ 0 1643742636000 dbfs:/mnt/darrellgerber/jadr/ML-Models/ ML-Models/ 0 1643906451000 dbfs:/mnt/darrellgerber/jadr/deleteme.txt deleteme.txt 8 1643742578000

## TRANSFORM

In [0]:
asthmaDF = spark.read.options(inferSchema = 'True', delimiter=',', header='True').csv('/mnt/darrellgerber/jadr/Data/asthma-emergency-department-visit-rates-fbyr_b/asthma-ed-visit-rates-by-county.csv')
display(asthmaDF)
print(asthmaDF.printSchema())
print(asthmaDF.count())
from pyspark.sql.functions import isnan, when, count, col
# Count of missing values in each column
asthmaDF.select([count(when(isnan(c), c)).alias(c) for c in asthmaDF.columns]).show()
# Count of null values in each column
asthmaDF.select([count(when(col(c).isNull(), c)).alias(c) for c in asthmaDF.columns]).show()
# Count of zero values in each column
asthmaDF.select([count(when(col(c)=="0", c)).alias(c) for c in asthmaDF.columns]).show()

COUNTY YEAR STRATA STRATA NAME AGE GROUP NUMBER OF ED VISITS AGE-ADJUSTED ED VISIT RATE COMMENT California 2015 Total population All ages All ages 191,904 50.4 null Alameda 2015 Total population All ages All ages 9,939 64.3 null Alpine 2015 Total population All ages All ages 0 0.0 null Amador 2015 Total population All ages All ages 196 58.4 null Butte 2015 Total population All ages All ages 1,044 50.2 null Calaveras 2015 Total population All ages All ages 185 48.0 null Colusa 2015 Total population All ages All ages 97 41.4 null Contra Costa 2015 Total population All ages All ages 6,858 65.2 null Del Norte 2015 Total population All ages All ages 140 53.0 null El Dorado 2015 Total population All ages All ages 592 36.4 null Fresno 2015 Total population All ages All ages 7,936 77.0 null Glenn 2015 Total population All ages All ages 122 42.6 null Humboldt 2015 Total population All ages All ages 835 63.4 null Imperial 2015 Total population All ages All ages 1,388 71.2 null Inyo 2015 Total population All ages All ages 88 53.5 null Kern 2015 Total population All ages All ages 5,859 62.3 null Kings 2015 Total population All ages All ages 1,250 78.6 null Lake 2015 Total population All ages All ages 478 80.4 null Lassen 2015 Total population All ages All ages 148 45.3 null Los Angeles 2015 Total population All ages All ages 52,227 53.1 null Madera 2015 Total population All ages All ages 1,031 62.3 null Marin 2015 Total population All ages All ages 541 22.2 null Mariposa 2015 Total population All ages All ages 79 47.4 null Mendocino 2015 Total population All ages All ages 479 57.4 null Merced 2015 Total population All ages All ages 2,425 87.4 null Modoc 2015 Total population All ages All ages 53 67.9 null Mono 2015 Total population All ages All ages 43 32.0 null Monterey 2015 Total population All ages All ages 2,194 50.2 null Napa 2015 Total population All ages All ages 572 41.9 null Nevada 2015 Total population All ages All ages 351 42.8 null Orange 2015 Total population All ages All ages 10,275 33.9 null Placer 2015 Total population All ages All ages 1,125 31.4 null Plumas 2015 Total population All ages All ages 99 56.3 null Riverside 2015 Total population All ages All ages 10,111 43.2 null Sacramento 2015 Total population All ages All ages 10,109 69.2 null San Benito 2015 Total population All ages All ages 285 50.1 null San Bernardino 2015 Total population All ages All ages 12,761 59.3 null San Diego 2015 Total population All ages All ages 11,646 37.0 null San Francisco 2015 Total population All ages All ages 3,141 41.3 null San Joaquin 2015 Total population All ages All ages 4,802 66.2 null San Luis Obispo 2015 Total population All ages All ages 950 40.1 null San Mateo 2015 Total population All ages All ages 2,695 36.4 null Santa Barbara 2015 Total population All ages All ages 1,734 40.7 null Santa Clara 2015 Total population All ages All ages 6,521 35.1 null Santa Cruz 2015 Total population All ages All ages 910 36.5 null Shasta 2015 Total population All ages All ages 1,015 60.5 null Sierra 2015 Total population All ages All ages 9 null Rate not available due to statistical instability Siskiyou 2015 Total population All ages All ages 176 47.0 null Solano 2015 Total population All ages All ages 3,415 83.2 null Sonoma 2015 Total population All ages All ages 1,936 40.2 null Stanislaus 2015 Total population All ages All ages 3,281 60.7 null Sutter 2015 Total population All ages All ages 337 34.1 null Tehama 2015 Total population All ages All ages 323 52.7 null Trinity 2015 Total population All ages All ages 67 60.5 null Tulare 2015 Total population All ages All ages 2,542 51.3 null Tuolumne 2015 Total population All ages All ages 257 53.1 null Ventura 2015 Total population All ages All ages 2,933 35.3 null Yolo 2015 Total population All ages All ages 852 44.1 null Yuba 2015 Total population All ages All ages 346 45.4 null California 2015 Child vs. adult 0�17 years 0�17 years 74,050 80.6 null Alameda 2015 Child vs. adult 0�17 years 0�17 y

root
-- COUNTY: string (nullable = true)
-- YEAR: integer (nullable = true)
-- STRATA: string (nullable = true)
-- STRATA NAME: string (nullable = true)
-- AGE GROUP: string (nullable = true)
-- NUMBER OF ED VISITS: string (nullable = true)
-- AGE-ADJUSTED ED VISIT RATE: double (nullable = true)
-- COMMENT: string (nullable = true)

None
3658
+------+----+------+-----------+---------+-------------------+--------------------------+-------+
COUNTY|YEAR|STRATA|STRATA NAME|AGE GROUP|NUMBER OF ED VISITS|AGE-ADJUSTED ED VISIT RATE|COMMENT|
+------+----+------+-----------+---------+-------------------+--------------------------+-------+
 0| 0| 0| 0| 0| 0| 0| 0|
+------+----+------+-----------+---------+-------------------+--------------------------+-------+

+------+----+------+-----------+---------+-------------------+--------------------------+-------+
COUNTY|YEAR|STRATA|STRATA NAME|AGE GROUP|NUMBER OF ED VISITS|AGE-ADJUSTED ED VISIT RATE|COMMENT|
+------+----+------+-----------+---------+-------------------+--------------------------+-------+
 0| 0| 0| 0| 0| 513| 541| 3117|
+------+----+------+-----------+---------+-------------------+--------------------------+-------+

+------+----+------+-----------+---------+-------------------+--------------------------+-------+
COUNTY|YEAR|STRATA|STRATA NAME|AGE GROUP|NUMBER OF ED VISITS|AGE-ADJUSTED ED VISIT RATE|COMMENT|
+------+----+------+-----------+---------+-------------------+--------------------------+-------+
 0| 0| 0| 0| 0| 197| 197| 0|
+------+----+------+-----------+---------+-------------------+--------------------------+-------+

Cleanup that is needed from this quick look:
1. Remove numeric data that is zero or null
2. Change the type of numeric columns to int or float

In [0]:
asthmaDF = asthmaDF.filter((asthmaDF['NUMBER OF ED VISITS'] != "0") & (asthmaDF['NUMBER OF ED VISITS'].isNotNull()))
asthmaDF = asthmaDF.filter((asthmaDF['AGE-ADJUSTED ED VISIT RATE'] != "0") & (asthmaDF['AGE-ADJUSTED ED VISIT RATE'].isNotNull()))
print(asthmaDF.count())
from pyspark.sql.functions import isnan, when, count, col
# Count of missing values in each column
asthmaDF.select([count(when(isnan(c), c)).alias(c) for c in asthmaDF.columns]).show()
# Count of null values in each column
asthmaDF.select([count(when(col(c).isNull(), c)).alias(c) for c in asthmaDF.columns]).show()
# Count of zero values in each column
asthmaDF.select([count(when(col(c)=="0", c)).alias(c) for c in asthmaDF.columns]).show()

2920
+------+----+------+-----------+---------+-------------------+--------------------------+-------+
COUNTY|YEAR|STRATA|STRATA NAME|AGE GROUP|NUMBER OF ED VISITS|AGE-ADJUSTED ED VISIT RATE|COMMENT|
+------+----+------+-----------+---------+-------------------+--------------------------+-------+
 0| 0| 0| 0| 0| 0| 0| 0|
+------+----+------+-----------+---------+-------------------+--------------------------+-------+

+------+----+------+-----------+---------+-------------------+--------------------------+-------+
COUNTY|YEAR|STRATA|STRATA NAME|AGE GROUP|NUMBER OF ED VISITS|AGE-ADJUSTED ED VISIT RATE|COMMENT|
+------+----+------+-----------+---------+-------------------+--------------------------+-------+
 0| 0| 0| 0| 0| 0| 0| 2920|
+------+----+------+-----------+---------+-------------------+--------------------------+-------+

+------+----+------+-----------+---------+-------------------+--------------------------+-------+
COUNTY|YEAR|STRATA|STRATA NAME|AGE GROUP|NUMBER OF ED VISITS|AGE-ADJUSTED ED VISIT RATE|COMMENT|
+------+----+------+-----------+---------+-------------------+--------------------------+-------+
 0| 0| 0| 0| 0| 0| 0| 0|
+------+----+------+-----------+---------+-------------------+--------------------------+-------+

In [0]:
from pyspark.sql.types import IntegerType
from pyspark.sql import functions as F
# Remove the commas in the column because the cast function will change those into null values instead of converting the number
asthmaDF = asthmaDF.withColumn('NUMBER OF ED VISITS(int)', F.regexp_replace(F.col('NUMBER OF ED VISITS'), ',', '').cast('integer'))
asthmaDF = asthmaDF.drop('NUMBER OF ED VISITS')
asthmaDF = asthmaDF.withColumnRenamed("NUMBER OF ED VISITS(int)","NUMBER OF ED VISITS")
display(asthmaDF)

COUNTY YEAR STRATA STRATA NAME AGE GROUP AGE-ADJUSTED ED VISIT RATE COMMENT NUMBER OF ED VISITS California 2015 Total population All ages All ages 50.4 null 191904 Alameda 2015 Total population All ages All ages 64.3 null 9939 Amador 2015 Total population All ages All ages 58.4 null 196 Butte 2015 Total population All ages All ages 50.2 null 1044 Calaveras 2015 Total population All ages All ages 48.0 null 185 Colusa 2015 Total population All ages All ages 41.4 null 97 Contra Costa 2015 Total population All ages All ages 65.2 null 6858 Del Norte 2015 Total population All ages All ages 53.0 null 140 El Dorado 2015 Total population All ages All ages 36.4 null 592 Fresno 2015 Total population All ages All ages 77.0 null 7936 Glenn 2015 Total population All ages All ages 42.6 null 122 Humboldt 2015 Total population All ages All ages 63.4 null 835 Imperial 2015 Total population All ages All ages 71.2 null 1388 Inyo 2015 Total population All ages All ages 53.5 null 88 Kern 2015 Total population All ages All ages 62.3 null 5859 Kings 2015 Total population All ages All ages 78.6 null 1250 Lake 2015 Total population All ages All ages 80.4 null 478 Lassen 2015 Total population All ages All ages 45.3 null 148 Los Angeles 2015 Total population All ages All ages 53.1 null 52227 Madera 2015 Total population All ages All ages 62.3 null 1031 Marin 2015 Total population All ages All ages 22.2 null 541 Mariposa 2015 Total population All ages All ages 47.4 null 79 Mendocino 2015 Total population All ages All ages 57.4 null 479 Merced 2015 Total population All ages All ages 87.4 null 2425 Modoc 2015 Total population All ages All ages 67.9 null 53 Mono 2015 Total population All ages All ages 32.0 null 43 Monterey 2015 Total population All ages All ages 50.2 null 2194 Napa 2015 Total population All ages All ages 41.9 null 572 Nevada 2015 Total population All ages All ages 42.8 null 351 Orange 2015 Total population All ages All ages 33.9 null 10275 Placer 2015 Total population All ages All ages 31.4 null 1125 Plumas 2015 Total population All ages All ages 56.3 null 99 Riverside 2015 Total population All ages All ages 43.2 null 10111 Sacramento 2015 Total population All ages All ages 69.2 null 10109 San Benito 2015 Total population All ages All ages 50.1 null 285 San Bernardino 2015 Total population All ages All ages 59.3 null 12761 San Diego 2015 Total population All ages All ages 37.0 null 11646 San Francisco 2015 Total population All ages All ages 41.3 null 3141 San Joaquin 2015 Total population All ages All ages 66.2 null 4802 San Luis Obispo 2015 Total population All ages All ages 40.1 null 950 San Mateo 2015 Total population All ages All ages 36.4 null 2695 Santa Barbara 2015 Total population All ages All ages 40.7 null 1734 Santa Clara 2015 Total population All ages All ages 35.1 null 6521 Santa Cruz 2015 Total population All ages All ages 36.5 null 910 Shasta 2015 Total population All ages All ages 60.5 null 1015 Siskiyou 2015 Total population All ages All ages 47.0 null 176 Solano 2015 Total population All ages All ages 83.2 null 3415 Sonoma 2015 Total population All ages All ages 40.2 null 1936 Stanislaus 2015 Total population All ages All ages 60.7 null 3281 Sutter 2015 Total population All ages All ages 34.1 null 337 Tehama 2015 Total population All ages All ages 52.7 null 323 Trinity 2015 Total population All ages All ages 60.5 null 67 Tulare 2015 Total population All ages All ages 51.3 null 2542 Tuolumne 2015 Total population All ages All ages 53.1 null 257 Ventura 2015 Total population All ages All ages 35.3 null 2933 Yolo 2015 Total population All ages All ages 44.1 null 852 Yuba 2015 Total population All ages All ages 45.4 null 346 California 2015 Child vs. adult 0�17 years 0�17 years 80.6 null 74050 Alameda 2015 Child vs. adult 0�17 years 0�17 years 96.7 null 3426 Amador 2015 Child vs. adult 0�17 years 0�17 years 85.1 null 45 Butte 2015 Child vs. adult 0�17 years 0�17 years 68.7 null 308 Calaveras 2015 Child vs. adult 0�17 years 0�17

Remove the Comment column

In [0]:
asthmaDF = asthmaDF.drop('COMMENT')

## 2. Pull out just the total population data

In [0]:
asthmaTotalDF = asthmaDF.filter(asthmaDF.STRATA == 'Total population')
display(asthmaTotalDF)


COUNTY YEAR STRATA STRATA NAME AGE GROUP AGE-ADJUSTED ED VISIT RATE NUMBER OF ED VISITS California 2015 Total population All ages All ages 50.4 191904 Alameda 2015 Total population All ages All ages 64.3 9939 Amador 2015 Total population All ages All ages 58.4 196 Butte 2015 Total population All ages All ages 50.2 1044 Calaveras 2015 Total population All ages All ages 48.0 185 Colusa 2015 Total population All ages All ages 41.4 97 Contra Costa 2015 Total population All ages All ages 65.2 6858 Del Norte 2015 Total population All ages All ages 53.0 140 El Dorado 2015 Total population All ages All ages 36.4 592 Fresno 2015 Total population All ages All ages 77.0 7936 Glenn 2015 Total population All ages All ages 42.6 122 Humboldt 2015 Total population All ages All ages 63.4 835 Imperial 2015 Total population All ages All ages 71.2 1388 Inyo 2015 Total population All ages All ages 53.5 88 Kern 2015 Total population All ages All ages 62.3 5859 Kings 2015 Total population All ages All ages 78.6 1250 Lake 2015 Total population All ages All ages 80.4 478 Lassen 2015 Total population All ages All ages 45.3 148 Los Angeles 2015 Total population All ages All ages 53.1 52227 Madera 2015 Total population All ages All ages 62.3 1031 Marin 2015 Total population All ages All ages 22.2 541 Mariposa 2015 Total population All ages All ages 47.4 79 Mendocino 2015 Total population All ages All ages 57.4 479 Merced 2015 Total population All ages All ages 87.4 2425 Modoc 2015 Total population All ages All ages 67.9 53 Mono 2015 Total population All ages All ages 32.0 43 Monterey 2015 Total population All ages All ages 50.2 2194 Napa 2015 Total population All ages All ages 41.9 572 Nevada 2015 Total population All ages All ages 42.8 351 Orange 2015 Total population All ages All ages 33.9 10275 Placer 2015 Total population All ages All ages 31.4 1125 Plumas 2015 Total population All ages All ages 56.3 99 Riverside 2015 Total population All ages All ages 43.2 10111 Sacramento 2015 Total population All ages All ages 69.2 10109 San Benito 2015 Total population All ages All ages 50.1 285 San Bernardino 2015 Total population All ages All ages 59.3 12761 San Diego 2015 Total population All ages All ages 37.0 11646 San Francisco 2015 Total population All ages All ages 41.3 3141 San Joaquin 2015 Total population All ages All ages 66.2 4802 San Luis Obispo 2015 Total population All ages All ages 40.1 950 San Mateo 2015 Total population All ages All ages 36.4 2695 Santa Barbara 2015 Total population All ages All ages 40.7 1734 Santa Clara 2015 Total population All ages All ages 35.1 6521 Santa Cruz 2015 Total population All ages All ages 36.5 910 Shasta 2015 Total population All ages All ages 60.5 1015 Siskiyou 2015 Total population All ages All ages 47.0 176 Solano 2015 Total population All ages All ages 83.2 3415 Sonoma 2015 Total population All ages All ages 40.2 1936 Stanislaus 2015 Total population All ages All ages 60.7 3281 Sutter 2015 Total population All ages All ages 34.1 337 Tehama 2015 Total population All ages All ages 52.7 323 Trinity 2015 Total population All ages All ages 60.5 67 Tulare 2015 Total population All ages All ages 51.3 2542 Tuolumne 2015 Total population All ages All ages 53.1 257 Ventura 2015 Total population All ages All ages 35.3 2933 Yolo 2015 Total population All ages All ages 44.1 852 Yuba 2015 Total population All ages All ages 45.4 346 California 2016 Total population All ages All ages 45.8 174733 Alameda 2016 Total population All ages All ages 57.8 9086 Amador 2016 Total population All ages All ages 61.8 187 Butte 2016 Total population All ages All ages 38.1 770 Calaveras 2016 Total population All ages All ages 45.3 171 Colusa 2016 Total population All ages All ages 29.6 67 Contra Costa 2016 Total population All ages All ages 56.8 6021 Del Norte 2016 Total population All ages All ages 71.1 172 El Dorado 2016 Total population All ages All ages 35.5 564 Fresno 2016 Total population All ages All ages 67.4 6930 Glenn 2016 Total 

Remove the columns that we don't need: Strata, Strata Name, and Age Group.

In [0]:
asthmaTotalDF = asthmaTotalDF.drop('STRATA', 'STRATA NAME', 'AGE GROUP')
print(asthmaTotalDF.printSchema())

root
-- COUNTY: string (nullable = true)
-- YEAR: integer (nullable = true)
-- AGE-ADJUSTED ED VISIT RATE: double (nullable = true)
-- NUMBER OF ED VISITS: integer (nullable = true)

None

Even though we know this data is from California, let's add a column for state name to keep in the database for possible later use.

In [0]:
from pyspark.sql.functions import col,lit
asthmaTotalDF = asthmaTotalDF.withColumn("STATE",lit("CA"))
asthmaTotalDF = asthmaTotalDF['STATE', 'COUNTY', 'YEAR', 'NUMBER OF ED VISITS', 'AGE-ADJUSTED ED VISIT RATE']
display(asthmaTotalDF)

STATE COUNTY YEAR NUMBER OF ED VISITS AGE-ADJUSTED ED VISIT RATE CA California 2015 191904 50.4 CA Alameda 2015 9939 64.3 CA Amador 2015 196 58.4 CA Butte 2015 1044 50.2 CA Calaveras 2015 185 48.0 CA Colusa 2015 97 41.4 CA Contra Costa 2015 6858 65.2 CA Del Norte 2015 140 53.0 CA El Dorado 2015 592 36.4 CA Fresno 2015 7936 77.0 CA Glenn 2015 122 42.6 CA Humboldt 2015 835 63.4 CA Imperial 2015 1388 71.2 CA Inyo 2015 88 53.5 CA Kern 2015 5859 62.3 CA Kings 2015 1250 78.6 CA Lake 2015 478 80.4 CA Lassen 2015 148 45.3 CA Los Angeles 2015 52227 53.1 CA Madera 2015 1031 62.3 CA Marin 2015 541 22.2 CA Mariposa 2015 79 47.4 CA Mendocino 2015 479 57.4 CA Merced 2015 2425 87.4 CA Modoc 2015 53 67.9 CA Mono 2015 43 32.0 CA Monterey 2015 2194 50.2 CA Napa 2015 572 41.9 CA Nevada 2015 351 42.8 CA Orange 2015 10275 33.9 CA Placer 2015 1125 31.4 CA Plumas 2015 99 56.3 CA Riverside 2015 10111 43.2 CA Sacramento 2015 10109 69.2 CA San Benito 2015 285 50.1 CA San Bernardino 2015 12761 59.3 CA San Diego 2015 11646 37.0 CA San Francisco 2015 3141 41.3 CA San Joaquin 2015 4802 66.2 CA San Luis Obispo 2015 950 40.1 CA San Mateo 2015 2695 36.4 CA Santa Barbara 2015 1734 40.7 CA Santa Clara 2015 6521 35.1 CA Santa Cruz 2015 910 36.5 CA Shasta 2015 1015 60.5 CA Siskiyou 2015 176 47.0 CA Solano 2015 3415 83.2 CA Sonoma 2015 1936 40.2 CA Stanislaus 2015 3281 60.7 CA Sutter 2015 337 34.1 CA Tehama 2015 323 52.7 CA Trinity 2015 67 60.5 CA Tulare 2015 2542 51.3 CA Tuolumne 2015 257 53.1 CA Ventura 2015 2933 35.3 CA Yolo 2015 852 44.1 CA Yuba 2015 346 45.4 CA California 2016 174733 45.8 CA Alameda 2016 9086 57.8 CA Amador 2016 187 61.8 CA Butte 2016 770 38.1 CA Calaveras 2016 171 45.3 CA Colusa 2016 67 29.6 CA Contra Costa 2016 6021 56.8 CA Del Norte 2016 172 71.1 CA El Dorado 2016 564 35.5 CA Fresno 2016 6930 67.4 CA Glenn 2016 103 36.3 CA Humboldt 2016 815 64.5 CA Imperial 2016 1287 66.3 CA Inyo 2016 90 53.7 CA Kern 2016 5008 54.5 CA Kings 2016 1027 65.0 CA Lake 2016 487 79.4 CA Lassen 2016 118 40.7 CA Los Angeles 2016 50778 51.5 CA Madera 2016 956 60.2 CA Marin 2016 543 23.1 CA Mariposa 2016 66 45.3 CA Mendocino 2016 451 56.4 CA Merced 2016 2211 79.2 CA Modoc 2016 59 80.1 CA Mono 2016 33 28.1 CA Monterey 2016 1959 44.3 CA Napa 2016 439 33.5 CA Nevada 2016 267 33.6 CA Orange 2016 8878 29.2 CA Placer 2016 968 28.3 CA Plumas 2016 99 61.4 CA Riverside 2016 9596 41.5 CA Sacramento 2016 8953 60.7 CA San Benito 2016 268 48.7 CA San Bernardino 2016 11335 51.9 CA San Diego 2016 10068 30.9 CA San Francisco 2016 2997 38.5 CA San Joaquin 2016 4245 57.5 CA San Luis Obispo 2016 926 38.1 CA San Mateo 2016 2382 32.5 CA Santa Barbara 2016 1641 37.7 CA Santa Clara 2016 5534 29.1 CA Santa Cruz 2016 864 34.4 CA Shasta 2016 726 46.4 CA Siskiyou 2016 128 33.7 CA Solano 2016 3349 80.8 CA Sonoma 2016 1682 36.6 CA Stanislaus 2016 2763 51.3 CA Sutter 2016 324 33.7 CA Tehama 2016 335 55.9 CA Trinity 2016 55 52.7 CA Tulare 2016 1980 40.5 CA Tuolumne 2016 224 46.9 CA Ventura 2016 2619 32.4 CA Yolo 2016 774 38.4 CA Yuba 2016 297 39.2 CA California 2017 180053 46.9 CA Alameda 2017 8942 56.3 CA Amador 2017 176 56.8 CA Butte 2017 936 45.3 CA Calaveras 2017 198 55.1 CA Colusa 2017 62 28.4 CA Contra Costa 2017 6706 62.6 CA Del Norte 2017 150 61.2 CA El Dorado 2017 650 40.5 CA Fresno 2017 7783 75.4 CA Glenn 2017 129 45.6 CA Humboldt 2017 851 67.1 CA Imperial 2017 1291 65.7 CA Inyo 2017 110 70.7 CA Kern 2017 4853 52.2 CA Kings 2017 1074 67.9 CA Lake 2017 482 80.1 CA Lassen 2017 131 44.0 CA Los Angeles 2017 49504 50.0 CA Madera 2017 979 61.7 CA Marin 2017 564 23.5 CA Mariposa 2017 63 46.5 CA Mendocino 2017 567 70.9 CA Merced 2017 2067 73.9 CA Modoc 2017 77 106.0 CA Mono 2017 40 32.0 CA Monterey 2017 1916 43.1 CA Napa 2017 537 40.2 CA Nevada 2017 306 38.5 CA Orange 2017 9084 29.7 CA Placer 2017 1193 34.7 CA Plumas 2017 86 63.2 CA Riverside 2017 10076 43.2 CA Sacramento 2017 10129 68.6 CA San Benito 2017 340 61.2 CA San Bernardino 2017 11204 51.4 CA San Diego 2017 10339 31.7 CA San Francisco 2

Write just the Asthma data to the SQL database. Note: We may want to change this to combine with air quality data first

## EXTRACT

### 3. Read in the air quality data and match up to the county and year in our asthma dataset

In [0]:
import requests
import json
### Read in API

# 2021 data 
# Documentation for API: https://aqs.epa.gov/aqsweb/documents/data_api.html#annual

# By county, annual data

# List of all counties in California
# https://aqs.epa.gov/data/api/list/countiesByState?email=test@aqs.api&key=test&state=06      
email = "dgerber@dev-10.com"
key = confluentRegistrySecret = dbutils.secrets.get(scope = "jadr_blob", key = "AQKey_dg")
# This returns Lead (TSP) LC, Carbon monoxide, Sulfur dioxide, Nitrogen dioxide (NO2), Ozone, PM10 Total 0-10um STP, Lead PM10 LC FRM/FEM,  and PM2.5 - Local Conditions
params = "14129,42401,42602,44201,81102,85129,88101" 


state = "06" # California
col_to_keep = ["state_code", "county_code", "latitude","longitude","parameter","metric_used","method","year","units_of_measure",
               "state","county","city","arithmetic_mean","standard_deviation", "first_max_value", "second_max_value", 
               "ninety_ninth_percentile", "cbsa_code"]

AQIList = []
# Our CA dataset goes from 2015 to 2019
dates = ['2015', '2016', '2017', '2018', '2019']

for date in dates:
    bdate = f"{date}0101"
    edate = f"{date}1231"

    stateurl = f'https://aqs.epa.gov/data/api/list/countiesByState?email={email}&key={key}&state={state}'
    for countyrow in json.loads(requests.get(stateurl).text)['Data']:
        county = countyrow['code']
        URL = f'https://aqs.epa.gov/data/api/annualData/byCounty?email={email}&key={key}&param={params}&bdate={bdate}&edate={edate}&state={state}&county={county}'
        for aDict in json.loads(requests.get(URL).text)['Data']:
            AQIList.append(dict((k, aDict[k]) for k in col_to_keep)) # Grab only the columns we want, and append it to the list of dictionaries



In [0]:
AQIDF = spark.createDataFrame(AQIList)


## TRANSFORM

In [0]:
from pyspark.sql.functions import col,lit
AQIDF = AQIDF.withColumn("state",lit("CA"))
display(AQIDF)
AQIDF.printSchema()
display(AQIDF.select("parameter").distinct())

arithmetic_mean cbsa_code city county county_code first_max_value latitude longitude method metric_used ninety_ninth_percentile parameter second_max_value standard_deviation state state_code units_of_measure year 0.758855 41860 Oakland Alameda 001 21.6 37.814781 -122.282347 INSTRUMENTAL - PULSED FLUORESCENT Observed Values 4.2 Sulfur dioxide 15.7 0.923692 CA 06 Parts per billion 2015 2.125905 41860 Oakland Alameda 001 21.6 37.814781 -122.282347 INSTRUMENTAL - PULSED FLUORESCENT Daily maximum 1-hour average 11.2 Sulfur dioxide 15.7 2.497825 CA 06 Parts per billion 2015 0.762953 41860 Oakland Alameda 001 3.9 37.814781 -122.282347 null Daily Average of observed values 2.3 Sulfur dioxide 2.8 0.57172 CA 06 Parts per billion 2015 0.743659 41860 Oakland Alameda 001 13.3 37.814781 -122.282347 null 3-Hour block average of observed hourly values 3.8 Sulfur dioxide 7.8 0.826127 CA 06 Parts per billion 2015 2.972808 41860 null Alameda 001 18.9 37.689615 -121.631916 INSTRUMENTAL - CHEMILUMINESCENCE Observed values 10.1 Nitrogen dioxide (NO2) 17.7 1.979219 CA 06 Parts per billion 2015 5.761826 41860 null Alameda 001 18.9 37.689615 -121.631916 INSTRUMENTAL - CHEMILUMINESCENCE Daily Maximum 1-hour average 15.6 Nitrogen dioxide (NO2) 17.2 3.139326 CA 06 Parts per billion 2015 18.12485 41860 Oakland Alameda 001 72.5 37.793624 -122.263376 INSTRUMENTAL - CHEMILUMINESCENCE Observed values 43.1 Nitrogen dioxide (NO2) 59.8 9.450608 CA 06 Parts per billion 2015 29.338187 41860 Oakland Alameda 001 72.5 37.793624 -122.263376 INSTRUMENTAL - CHEMILUMINESCENCE Daily Maximum 1-hour average 55.4 Nitrogen dioxide (NO2) 59.8 10.039421 CA 06 Parts per billion 2015 13.975694 41860 Oakland Alameda 001 57.1 37.814781 -122.282347 INSTRUMENTAL - CHEMILUMINESCENCE Observed values 39.7 Nitrogen dioxide (NO2) 56.6 9.404179 CA 06 Parts per billion 2015 24.574095 41860 Oakland Alameda 001 57.1 37.814781 -122.282347 INSTRUMENTAL - CHEMILUMINESCENCE Daily Maximum 1-hour average 49.8 Nitrogen dioxide (NO2) 56.6 10.749651 CA 06 Parts per billion 2015 11.339142 41860 Oakland Alameda 001 48.0 37.743065 -122.169935 INSTRUMENTAL - CHEMILUMINESCENCE Observed values 34.5 Nitrogen dioxide (NO2) 47.5 8.019285 CA 06 Parts per billion 2015 20.957382 41860 Oakland Alameda 001 48.0 37.743065 -122.169935 INSTRUMENTAL - CHEMILUMINESCENCE Daily Maximum 1-hour average 47.0 Nitrogen dioxide (NO2) 47.5 10.580479 CA 06 Parts per billion 2015 10.19611 41860 Livermore Alameda 001 49.6 37.687526 -121.784217 INSTRUMENTAL - CHEMILUMINESCENCE Observed values 33.0 Nitrogen dioxide (NO2) 46.4 8.550349 CA 06 Parts per billion 2015 20.007692 41860 Livermore Alameda 001 49.6 37.687526 -121.784217 INSTRUMENTAL - CHEMILUMINESCENCE Daily Maximum 1-hour average 40.7 Nitrogen dioxide (NO2) 45.3 10.788528 CA 06 Parts per billion 2015 0.050203 41860 null Alameda 001 0.099 37.689615 -121.631916 INSTRUMENTAL - ULTRA VIOLET Daily maxima of observed hourly values (between 9:00 AM and 8:00 PM) 0.099 Ozone 0.099 0.01376 CA 06 Parts per million 2015 0.044542 41860 null Alameda 001 0.082 37.689615 -121.631916 null Daily maximum of 8 hour running average of observed hourly values 0.078 Ozone 0.078 0.01118 CA 06 Parts per million 2015 0.044542 41860 null Alameda 001 0.082 37.689615 -121.631916 null Daily maximum of 8 hour running average of observed hourly values 0.078 Ozone 0.078 0.01118 CA 06 Parts per million 2015 0.044219 41860 null Alameda 001 0.082 37.689615 -121.631916 null Daily maximum of 8-hour running average 0.078 Ozone 0.078 0.011502 CA 06 Parts per million 2015 0.0425 41860 Hayward Alameda 001 0.103 37.654456 -122.031547 INSTRUMENTAL - ULTRA VIOLET Daily maxima of observed hourly values (between 9:00 AM and 8:00 PM) 0.093 Ozone 0.099 0.011796 CA 06 Parts per million 2015 0.036939 41860 Hayward Alameda 001 0.084 37.654456 -122.031547 null Daily maximum of 8 hour running average of observed hourly values 0.066 Ozone 0.082 0.009289 CA 06 Parts per million 2015 0.036939 41860 Hayward Alameda 001 0.084 37.65445

root
-- arithmetic_mean: double (nullable = true)
-- cbsa_code: string (nullable = true)
-- city: string (nullable = true)
-- county: string (nullable = true)
-- county_code: string (nullable = true)
-- first_max_value: double (nullable = true)
-- latitude: double (nullable = true)
-- longitude: double (nullable = true)
-- method: string (nullable = true)
-- metric_used: string (nullable = true)
-- ninety_ninth_percentile: double (nullable = true)
-- parameter: string (nullable = true)
-- second_max_value: double (nullable = true)
-- standard_deviation: double (nullable = true)
-- state: string (nullable = false)
-- state_code: string (nullable = true)
-- units_of_measure: string (nullable = true)
-- year: long (nullable = true)

parameter PM10 Total 0-10um STP Lead (TSP) LC PM2.5 - Local Conditions Sulfur dioxide Ozone Nitrogen dioxide (NO2) Lead PM10 LC FRM/FEM

Let's take a look at just Los Angeles County for Lead for 2015 to see what we have to help narrow down what to keep.

In [0]:

LosAngelesDF = AQIDF.filter(
                           (AQIDF['parameter']  == 'Lead PM10 LC FRM/FEM') &
                           (AQIDF['year']  == '2015'))
display(LosAngelesDF)
display(LosAngelesDF.select("method").distinct())
display(LosAngelesDF.select("metric_used").distinct())

arithmetic_mean cbsa_code city county county_code first_max_value latitude longitude method metric_used ninety_ninth_percentile parameter second_max_value standard_deviation state state_code units_of_measure year 0.001529 40900 Arden-Arcade Sacramento 067 0.007 38.613779 -121.368014 Thermo/R & P 2025 PM10 - X-ray Fluorescence (EDXRF) FRM Observed Values 0.007 Lead PM10 LC FRM/FEM 0.007 0.001901 CA 06 Micrograms/cubic meter (LC) 2015 0.003151 41940 San Jose Santa Clara 085 0.0121 37.348497 -121.894898 Thermo/R & P 2025 Teflon - ICPMS Observed Values 0.0121 Lead PM10 LC FRM/FEM 0.0103 0.002745 CA 06 Micrograms/cubic meter (LC) 2015

method Thermo/R & P 2025 PM10 - X-ray Fluorescence (EDXRF) FRM Thermo/R & P 2025 Teflon - ICPMS

metric_used Observed Values

The dataset contains multiple measurements for each pollutant using different methods and metrics. We will narrow down the measurements used so we can get only one per site per year.

In [0]:
parameters = ['PM10 Total 0-10um STP',
              'Lead (TSP) LC',
              'PM2.5 - Local Conditions',
              'Sulfur dioxide',
              'Ozone',
              'Nitrogen dioxide (NO2)']

preferredMethods = ['Hi-Vol - ICAP SPECTRA (ICP-MS); 0.45M HNO3 Boil30 min',
                    'INSTRUMENTAL - GAS PHASE CHEMILUMINESCENCE',
                   'INSTRUMENTAL - CHEMILUMINESCENCE',
                   'INSTRUMENTAL - ULTRA VIOLET ABSORPTION',
                   'INSTRUMENTAL - ULTRA VIOLET',
                   'Andersen RAAS2.5-300 PM2.5 SEQ w/WINS - GRAVIMETRIC',
                   'R & P Model 2025 PM-2.5 Sequential Air Sampler w/VSCC - Gravimetric',
                   'Multiple Methods Used',
                   'INSTRUMENTAL - Pulsed Fluorescent 43C-TLE/43i-TLE']
preferredMetrics = ['Daily Maximum 1-hour average',
                    'Daily maxima of observed hourly values (between 9:00 AM and 8:00 PM)',
                    'Daily Mean',
                    'Daily maximum 1-hour average',
                   'Observed Values']

In [0]:
AQIDFclean = AQIDF.filter(AQIDF.parameter.isin(parameters))
display(AQIDFclean.select("parameter").distinct())
AQIDFclean = AQIDFclean.filter(AQIDF.method.isin(preferredMethods))
display(AQIDFclean.select("method").distinct())
AQIDFclean = AQIDFclean.filter(AQIDF.metric_used.isin(preferredMetrics))
display(AQIDFclean.select("metric_used").distinct())

parameter PM10 Total 0-10um STP Lead (TSP) LC PM2.5 - Local Conditions Sulfur dioxide Ozone Nitrogen dioxide (NO2)

method INSTRUMENTAL - Pulsed Fluorescent 43C-TLE/43i-TLE Andersen RAAS2.5-300 PM2.5 SEQ w/WINS - GRAVIMETRIC Multiple Methods Used R & P Model 2025 PM-2.5 Sequential Air Sampler w/VSCC - Gravimetric Hi-Vol - ICAP SPECTRA (ICP-MS); 0.45M HNO3 Boil30 min INSTRUMENTAL - ULTRA VIOLET ABSORPTION INSTRUMENTAL - CHEMILUMINESCENCE INSTRUMENTAL - ULTRA VIOLET INSTRUMENTAL - GAS PHASE CHEMILUMINESCENCE

metric_used Daily maximum 1-hour average Daily maxima of observed hourly values (between 9:00 AM and 8:00 PM) Daily Mean Observed Values Daily Maximum 1-hour average

In [0]:
LosAngelesDF = AQIDFclean.filter(
                           (AQIDFclean['metric_used']  == 'Observed Values') &
                           (AQIDFclean['year']  == '2015'))
display(LosAngelesDF)
display(LosAngelesDF.select("method").distinct())
display(LosAngelesDF.select("parameter").distinct())

arithmetic_mean cbsa_code city county county_code first_max_value latitude longitude method metric_used ninety_ninth_percentile parameter second_max_value standard_deviation state state_code units_of_measure year 0.003579 23420 Fresno Fresno 019 0.014 36.78538 -119.77321 Multiple Methods Used Observed Values 0.014 Lead (TSP) LC 0.007 0.002129 CA 06 Micrograms/cubic meter (LC) 2015 0.506257 23420 Fresno Fresno 019 10.8 36.78538 -119.77321 INSTRUMENTAL - Pulsed Fluorescent 43C-TLE/43i-TLE Observed Values 3.0 Sulfur dioxide 7.7 0.646618 CA 06 Parts per billion 2015 0.017739 20940 Calexico Imperial 025 0.087 32.67618 -115.48307 Multiple Methods Used Observed Values 0.087 Lead (TSP) LC 0.046 0.01728 CA 06 Micrograms/cubic meter (LC) 2015 0.726755 20940 Calexico Imperial 025 16.1 32.67618 -115.48307 INSTRUMENTAL - Pulsed Fluorescent 43C-TLE/43i-TLE Observed Values 4.5 Sulfur dioxide 13.0 0.975822 CA 06 Parts per billion 2015 0.051669 13860 null Inyo 027 0.3 37.360684 -118.330783 INSTRUMENTAL - Pulsed Fluorescent 43C-TLE/43i-TLE Observed Values 0.2 Sulfur dioxide 0.3 0.056891 CA 06 Parts per billion 2015 0.002931 31080 Los Angeles Los Angeles 037 0.01 33.95507 -118.43049 Hi-Vol - ICAP SPECTRA (ICP-MS); 0.45M HNO3 Boil30 min Observed Values 0.01 Lead (TSP) LC 0.01 0.002784 CA 06 Micrograms/cubic meter (LC) 2015 0.00445 31080 Long Beach Los Angeles 037 0.017 33.79236 -118.17533 Hi-Vol - ICAP SPECTRA (ICP-MS); 0.45M HNO3 Boil30 min Observed Values 0.017 Lead (TSP) LC 0.012 0.003753 CA 06 Micrograms/cubic meter (LC) 2015 0.007362 31080 Pico Rivera Los Angeles 037 0.026 34.01029 -118.0685 Hi-Vol - ICAP SPECTRA (ICP-MS); 0.45M HNO3 Boil30 min Observed Values 0.026 Lead (TSP) LC 0.022 0.005074 CA 06 Micrograms/cubic meter (LC) 2015 0.016517 31080 Commerce Los Angeles 037 0.031 34.008333 -118.190556 Hi-Vol - ICAP SPECTRA (ICP-MS); 0.45M HNO3 Boil30 min Observed Values 0.031 Lead (TSP) LC 0.031 0.007486 CA 06 Micrograms/cubic meter (LC) 2015 0.011488 31080 Commerce Los Angeles 037 0.025 34.008333 -118.190556 Hi-Vol - ICAP SPECTRA (ICP-MS); 0.45M HNO3 Boil30 min Observed Values 0.025 Lead (TSP) LC 0.024 0.00573 CA 06 Micrograms/cubic meter (LC) 2015 0.017859 31080 Vernon Los Angeles 037 0.052 34.006389 -118.193056 Hi-Vol - ICAP SPECTRA (ICP-MS); 0.45M HNO3 Boil30 min Observed Values 0.038 Lead (TSP) LC 0.038 0.007715 CA 06 Micrograms/cubic meter (LC) 2015 0.020161 31080 Vernon Los Angeles 037 0.067 34.006389 -118.193056 Hi-Vol - ICAP SPECTRA (ICP-MS); 0.45M HNO3 Boil30 min Observed Values 0.06 Lead (TSP) LC 0.06 0.010168 CA 06 Micrograms/cubic meter (LC) 2015 0.021236 31080 Vernon Los Angeles 037 0.062 34.006389 -118.193056 Hi-Vol - ICAP SPECTRA (ICP-MS); 0.45M HNO3 Boil30 min Observed Values 0.057 Lead (TSP) LC 0.057 0.010019 CA 06 Micrograms/cubic meter (LC) 2015 0.011389 31080 Industry (corporate name for City of Industry) Los Angeles 037 0.034 34.02637 -117.9822 Hi-Vol - ICAP SPECTRA (ICP-MS); 0.45M HNO3 Boil30 min Observed Values 0.034 Lead (TSP) LC 0.023 0.005584 CA 06 Micrograms/cubic meter (LC) 2015 0.028678 31080 Santa Fe Springs Los Angeles 037 0.097 33.954952 -118.055768 Hi-Vol - ICAP SPECTRA (ICP-MS); 0.45M HNO3 Boil30 min Observed Values 0.097 Lead (TSP) LC 0.064 0.016331 CA 06 Micrograms/cubic meter (LC) 2015 0.006902 31080 Compton Los Angeles 037 0.02 33.901389 -118.205 Hi-Vol - ICAP SPECTRA (ICP-MS); 0.45M HNO3 Boil30 min Observed Values 0.02 Lead (TSP) LC 0.016 0.004557 CA 06 Micrograms/cubic meter (LC) 2015 0.006755 31080 Compton Los Angeles 037 0.02 33.901389 -118.205 Hi-Vol - ICAP SPECTRA (ICP-MS); 0.45M HNO3 Boil30 min Observed Values 0.02 Lead (TSP) LC 0.019 0.004899 CA 06 Micrograms/cubic meter (LC) 2015 0.008719 31080 Los Angeles Los Angeles 037 0.025 34.06659 -118.22688 Hi-Vol - ICAP SPECTRA (ICP-MS); 0.45M HNO3 Boil30 min Observed Values 0.025 Lead (TSP) LC 0.02 0.004938 CA 06 Micrograms/cubic meter (LC) 2015 0.008787 31080 Los Angeles Los Angeles 037 0.023 34.06659 -118.22688 Hi-Vol - ICAP SPECTRA (ICP-MS); 0.45M HNO

method INSTRUMENTAL - Pulsed Fluorescent 43C-TLE/43i-TLE Multiple Methods Used Hi-Vol - ICAP SPECTRA (ICP-MS); 0.45M HNO3 Boil30 min

parameter Lead (TSP) LC Sulfur dioxide

In [0]:
# Handle bringing in some SO2 types we don't want with 'Observed Values'
AQIDFclean = AQIDFclean.filter(~((AQIDF.parameter == 'Sulfur dioxide') & 
    (AQIDF.metric_used == 'Observed Values')))


In [0]:
LosAngelesDF = AQIDFclean.filter((AQIDFclean['county']  == 'Los Angeles') &
                           (AQIDFclean['metric_used']  == 'Observed Values') &
                           (AQIDFclean['year']  == '2015'))
display(LosAngelesDF)
display(LosAngelesDF.select("method").distinct())
display(LosAngelesDF.select("parameter").distinct())

arithmetic_mean cbsa_code city county county_code first_max_value latitude longitude method metric_used ninety_ninth_percentile parameter second_max_value standard_deviation state state_code units_of_measure year 0.002931 31080 Los Angeles Los Angeles 037 0.01 33.95507 -118.43049 Hi-Vol - ICAP SPECTRA (ICP-MS); 0.45M HNO3 Boil30 min Observed Values 0.01 Lead (TSP) LC 0.01 0.002784 CA 06 Micrograms/cubic meter (LC) 2015 0.00445 31080 Long Beach Los Angeles 037 0.017 33.79236 -118.17533 Hi-Vol - ICAP SPECTRA (ICP-MS); 0.45M HNO3 Boil30 min Observed Values 0.017 Lead (TSP) LC 0.012 0.003753 CA 06 Micrograms/cubic meter (LC) 2015 0.007362 31080 Pico Rivera Los Angeles 037 0.026 34.01029 -118.0685 Hi-Vol - ICAP SPECTRA (ICP-MS); 0.45M HNO3 Boil30 min Observed Values 0.026 Lead (TSP) LC 0.022 0.005074 CA 06 Micrograms/cubic meter (LC) 2015 0.016517 31080 Commerce Los Angeles 037 0.031 34.008333 -118.190556 Hi-Vol - ICAP SPECTRA (ICP-MS); 0.45M HNO3 Boil30 min Observed Values 0.031 Lead (TSP) LC 0.031 0.007486 CA 06 Micrograms/cubic meter (LC) 2015 0.011488 31080 Commerce Los Angeles 037 0.025 34.008333 -118.190556 Hi-Vol - ICAP SPECTRA (ICP-MS); 0.45M HNO3 Boil30 min Observed Values 0.025 Lead (TSP) LC 0.024 0.00573 CA 06 Micrograms/cubic meter (LC) 2015 0.017859 31080 Vernon Los Angeles 037 0.052 34.006389 -118.193056 Hi-Vol - ICAP SPECTRA (ICP-MS); 0.45M HNO3 Boil30 min Observed Values 0.038 Lead (TSP) LC 0.038 0.007715 CA 06 Micrograms/cubic meter (LC) 2015 0.020161 31080 Vernon Los Angeles 037 0.067 34.006389 -118.193056 Hi-Vol - ICAP SPECTRA (ICP-MS); 0.45M HNO3 Boil30 min Observed Values 0.06 Lead (TSP) LC 0.06 0.010168 CA 06 Micrograms/cubic meter (LC) 2015 0.021236 31080 Vernon Los Angeles 037 0.062 34.006389 -118.193056 Hi-Vol - ICAP SPECTRA (ICP-MS); 0.45M HNO3 Boil30 min Observed Values 0.057 Lead (TSP) LC 0.057 0.010019 CA 06 Micrograms/cubic meter (LC) 2015 0.011389 31080 Industry (corporate name for City of Industry) Los Angeles 037 0.034 34.02637 -117.9822 Hi-Vol - ICAP SPECTRA (ICP-MS); 0.45M HNO3 Boil30 min Observed Values 0.034 Lead (TSP) LC 0.023 0.005584 CA 06 Micrograms/cubic meter (LC) 2015 0.028678 31080 Santa Fe Springs Los Angeles 037 0.097 33.954952 -118.055768 Hi-Vol - ICAP SPECTRA (ICP-MS); 0.45M HNO3 Boil30 min Observed Values 0.097 Lead (TSP) LC 0.064 0.016331 CA 06 Micrograms/cubic meter (LC) 2015 0.006902 31080 Compton Los Angeles 037 0.02 33.901389 -118.205 Hi-Vol - ICAP SPECTRA (ICP-MS); 0.45M HNO3 Boil30 min Observed Values 0.02 Lead (TSP) LC 0.016 0.004557 CA 06 Micrograms/cubic meter (LC) 2015 0.006755 31080 Compton Los Angeles 037 0.02 33.901389 -118.205 Hi-Vol - ICAP SPECTRA (ICP-MS); 0.45M HNO3 Boil30 min Observed Values 0.02 Lead (TSP) LC 0.019 0.004899 CA 06 Micrograms/cubic meter (LC) 2015 0.008719 31080 Los Angeles Los Angeles 037 0.025 34.06659 -118.22688 Hi-Vol - ICAP SPECTRA (ICP-MS); 0.45M HNO3 Boil30 min Observed Values 0.025 Lead (TSP) LC 0.02 0.004938 CA 06 Micrograms/cubic meter (LC) 2015 0.008787 31080 Los Angeles Los Angeles 037 0.023 34.06659 -118.22688 Hi-Vol - ICAP SPECTRA (ICP-MS); 0.45M HNO3 Boil30 min Observed Values 0.023 Lead (TSP) LC 0.022 0.004862 CA 06 Micrograms/cubic meter (LC) 2015

method Hi-Vol - ICAP SPECTRA (ICP-MS); 0.45M HNO3 Boil30 min

parameter Lead (TSP) LC

In [0]:
from pyspark.sql import functions as F
AQIDFAgg = AQIDFclean.groupBy( 'state', 'county','year','parameter').pivot('parameter').agg(F.mean('arithmetic_mean'),
                              F.mean('first_max_value'),
                              F.mean('ninety_ninth_percentile'), 
                              F.mean('standard_deviation'),
                              F.mean('second_max_value'),
                              F.first('method'),
                              F.first('metric_used'),                            
                              F.first('units_of_measure'))

display(AQIDFAgg)

state county year parameter Lead (TSP) LC_avg(arithmetic_mean) Lead (TSP) LC_avg(first_max_value) Lead (TSP) LC_avg(ninety_ninth_percentile) Lead (TSP) LC_avg(standard_deviation) Lead (TSP) LC_avg(second_max_value) Lead (TSP) LC_first(method) Lead (TSP) LC_first(metric_used) Lead (TSP) LC_first(units_of_measure) Nitrogen dioxide (NO2)_avg(arithmetic_mean) Nitrogen dioxide (NO2)_avg(first_max_value) Nitrogen dioxide (NO2)_avg(ninety_ninth_percentile) Nitrogen dioxide (NO2)_avg(standard_deviation) Nitrogen dioxide (NO2)_avg(second_max_value) Nitrogen dioxide (NO2)_first(method) Nitrogen dioxide (NO2)_first(metric_used) Nitrogen dioxide (NO2)_first(units_of_measure) Ozone_avg(arithmetic_mean) Ozone_avg(first_max_value) Ozone_avg(ninety_ninth_percentile) Ozone_avg(standard_deviation) Ozone_avg(second_max_value) Ozone_first(method) Ozone_first(metric_used) Ozone_first(units_of_measure) PM10 Total 0-10um STP_avg(arithmetic_mean) PM10 Total 0-10um STP_avg(first_max_value) PM10 Total 0-10um STP_avg(ninety_ninth_percentile) PM10 Total 0-10um STP_avg(standard_deviation) PM10 Total 0-10um STP_avg(second_max_value) PM10 Total 0-10um STP_first(method) PM10 Total 0-10um STP_first(metric_used) PM10 Total 0-10um STP_first(units_of_measure) PM2.5 - Local Conditions_avg(arithmetic_mean) PM2.5 - Local Conditions_avg(first_max_value) PM2.5 - Local Conditions_avg(ninety_ninth_percentile) PM2.5 - Local Conditions_avg(standard_deviation) PM2.5 - Local Conditions_avg(second_max_value) PM2.5 - Local Conditions_first(method) PM2.5 - Local Conditions_first(metric_used) PM2.5 - Local Conditions_first(units_of_measure) Sulfur dioxide_avg(arithmetic_mean) Sulfur dioxide_avg(first_max_value) Sulfur dioxide_avg(ninety_ninth_percentile) Sulfur dioxide_avg(standard_deviation) Sulfur dioxide_avg(second_max_value) Sulfur dioxide_first(method) Sulfur dioxide_first(metric_used) Sulfur dioxide_first(units_of_measure) CA Alameda 2015 Nitrogen dioxide (NO2) null null null null null null null null 20.1278364 49.22 41.7 9.059481 45.279999999999994 INSTRUMENTAL - CHEMILUMINESCENCE Daily Maximum 1-hour average Parts per billion null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null CA Alameda 2015 Ozone null null null null null null null null null null null null null null null null 0.0409086 0.0984 0.08620000000000001 0.0122206 0.092 INSTRUMENTAL - ULTRA VIOLET Daily maxima of observed hourly values (between 9:00 AM and 8:00 PM) Parts per million null null null null null null null null null null null null null null null null null null null null null null null null CA Alameda 2016 Nitrogen dioxide (NO2) null null null null null null null null 19.29764116666667 46.116666666666674 37.73333333333333 7.934909333333333 39.199999999999996 INSTRUMENTAL - CHEMILUMINESCENCE Daily Maximum 1-hour average Parts per billion null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null CA Alameda 2016 Ozone null null null null null null null null null null null null null null null null 0.03733583333333334 0.08216666666666667 0.074 0.011103 0.07816666666666666 INSTRUMENTAL - ULTRA VIOLET Daily maxima of observed hourly values (between 9:00 AM and 8:00 PM) Parts per million null null null null null null null null null null null null null null null null null null null null null null null null CA Alameda 2017 Nitrogen dioxide (NO2) null null null null null null null null 20.515038 61.19999999999999 44.43333333333334 9.129422 49.883333333333326 INSTRUMENTAL - CHEMILUMINESCENCE Daily Maximum 1-hour average Parts per billion null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null null CA Alameda 2017 Ozone null null null null null null null null null null null null null null null null 0.038411 0.

Need to aggregate the parameters into a single row for each year and county

In [0]:
print(AQIDFAgg.printSchema())

root
-- state: string (nullable = false)
-- county: string (nullable = true)
-- year: long (nullable = true)
-- parameter: string (nullable = true)
-- Lead (TSP) LC_avg(arithmetic_mean): double (nullable = true)
-- Lead (TSP) LC_avg(first_max_value): double (nullable = true)
-- Lead (TSP) LC_avg(ninety_ninth_percentile): double (nullable = true)
-- Lead (TSP) LC_avg(standard_deviation): double (nullable = true)
-- Lead (TSP) LC_avg(second_max_value): double (nullable = true)
-- Lead (TSP) LC_first(method): string (nullable = true)
-- Lead (TSP) LC_first(metric_used): string (nullable = true)
-- Lead (TSP) LC_first(units_of_measure): string (nullable = true)
-- Nitrogen dioxide (NO2)_avg(arithmetic_mean): double (nullable = true)
-- Nitrogen dioxide (NO2)_avg(first_max_value): double (nullable = true)
-- Nitrogen dioxide (NO2)_avg(ninety_ninth_percentile): double (nullable = true)
-- Nitrogen dioxide (NO2)_avg(standard_deviation): double (nullable = true)
-- Nitrogen dioxide (NO2)_avg(second_max_value): double (nullable = true)
-- Nitrogen dioxide (NO2)_first(method): string (nullable = true)
-- Nitrogen dioxide (NO2)_first(metric_used): string (nullable = true)
-- Nitrogen dioxide (NO2)_first(units_of_measure): string (nullable = true)
-- Ozone_avg(arithmetic_mean): double (nullable = true)
-- Ozone_avg(first_max_value): double (nullable = true)
-- Ozone_avg(ninety_ninth_percentile): double (nullable = true)
-- Ozone_avg(standard_deviation): double (nullable = true)
-- Ozone_avg(second_max_value): double (nullable = true)
-- Ozone_first(method): string (nullable = true)
-- Ozone_first(metric_used): string (nullable = true)
-- Ozone_first(units_of_measure): string (nullable = true)
-- PM10 Total 0-10um STP_avg(arithmetic_mean): double (nullable = true)
-- PM10 Total 0-10um STP_avg(first_max_value): double (nullable = true)
-- PM10 Total 0-10um STP_avg(ninety_ninth_percentile): double (nullable = true)
-- PM10 Total 0-10um STP_avg(standard_deviation): double (nullable = true)
-- PM10 Total 0-10um STP_avg(second_max_value): double (nullable = true)
-- PM10 Total 0-10um STP_first(method): string (nullable = true)
-- PM10 Total 0-10um STP_first(metric_used): string (nullable = true)
-- PM10 Total 0-10um STP_first(units_of_measure): string (nullable = true)
-- PM2.5 - Local Conditions_avg(arithmetic_mean): double (nullable = true)
-- PM2.5 - Local Conditions_avg(first_max_value): double (nullable = true)
-- PM2.5 - Local Conditions_avg(ninety_ninth_percentile): double (nullable = true)
-- PM2.5 - Local Conditions_avg(standard_deviation): double (nullable = true)
-- PM2.5 - Local Conditions_avg(second_max_value): double (nullable = true)
-- PM2.5 - Local Conditions_first(method): string (nullable = true)
-- PM2.5 - Local Conditions_first(metric_used): string (nullable = true)
-- PM2.5 - Local Conditions_first(units_of_measure): string (nullable = true)
-- Sulfur dioxide_avg(arithmetic_mean): double (nullable = true)
-- Sulfur dioxide_avg(first_max_value): double (nullable = true)
-- Sulfur dioxide_avg(ninety_ninth_percentile): double (nullable = true)
-- Sulfur dioxide_avg(standard_deviation): double (nullable = true)
-- Sulfur dioxide_avg(second_max_value): double (nullable = true)
-- Sulfur dioxide_first(method): string (nullable = true)
-- Sulfur dioxide_first(metric_used): string (nullable = true)
-- Sulfur dioxide_first(units_of_measure): string (nullable = true)

None

Rename the PM2.5 columns because the agg() function does not handle column names with periods in them

In [0]:
AQIDFAgg = AQIDFAgg.withColumnRenamed("PM2.5 - Local Conditions_avg(ninety_ninth_percentile)","PM25 - Local Conditions_avg(ninety_ninth_percentile)")
AQIDFAgg = AQIDFAgg.withColumnRenamed("PM2.5 - Local Conditions_avg(arithmetic_mean)","PM25 - Local Conditions_avg(arithmetic_mean)")
AQIDFAgg = AQIDFAgg.withColumnRenamed("PM2.5 - Local Conditions_avg(first_max_value)","PM25 - Local Conditions_avg(first_max_value)")
AQIDFAgg = AQIDFAgg.withColumnRenamed("PM2.5 - Local Conditions_avg(standard_deviation)","PM25 - Local Conditions_avg(standard_deviation)")
AQIDFAgg = AQIDFAgg.withColumnRenamed("PM2.5 - Local Conditions_avg(second_max_value)","PM25 - Local Conditions_avg(second_max_value)")
AQIDFAgg = AQIDFAgg.withColumnRenamed("PM2.5 - Local Conditions_first(method)","PM25 - Local Conditions_first(method)")
AQIDFAgg = AQIDFAgg.withColumnRenamed("PM2.5 - Local Conditions_first(metric_used)","PM25 - Local Conditions_first(metric_used)")
AQIDFAgg = AQIDFAgg.withColumnRenamed("PM2.5 - Local Conditions_first(units_of_measure)","PM25 - Local Conditions_first(units_of_measure)")


AQIDFAgg.printSchema()


root
-- state: string (nullable = false)
-- county: string (nullable = true)
-- year: long (nullable = true)
-- parameter: string (nullable = true)
-- Lead (TSP) LC_avg(arithmetic_mean): double (nullable = true)
-- Lead (TSP) LC_avg(first_max_value): double (nullable = true)
-- Lead (TSP) LC_avg(ninety_ninth_percentile): double (nullable = true)
-- Lead (TSP) LC_avg(standard_deviation): double (nullable = true)
-- Lead (TSP) LC_avg(second_max_value): double (nullable = true)
-- Lead (TSP) LC_first(method): string (nullable = true)
-- Lead (TSP) LC_first(metric_used): string (nullable = true)
-- Lead (TSP) LC_first(units_of_measure): string (nullable = true)
-- Nitrogen dioxide (NO2)_avg(arithmetic_mean): double (nullable = true)
-- Nitrogen dioxide (NO2)_avg(first_max_value): double (nullable = true)
-- Nitrogen dioxide (NO2)_avg(ninety_ninth_percentile): double (nullable = true)
-- Nitrogen dioxide (NO2)_avg(standard_deviation): double (nullable = true)
-- Nitrogen dioxide (NO2)_avg(second_max_value): double (nullable = true)
-- Nitrogen dioxide (NO2)_first(method): string (nullable = true)
-- Nitrogen dioxide (NO2)_first(metric_used): string (nullable = true)
-- Nitrogen dioxide (NO2)_first(units_of_measure): string (nullable = true)
-- Ozone_avg(arithmetic_mean): double (nullable = true)
-- Ozone_avg(first_max_value): double (nullable = true)
-- Ozone_avg(ninety_ninth_percentile): double (nullable = true)
-- Ozone_avg(standard_deviation): double (nullable = true)
-- Ozone_avg(second_max_value): double (nullable = true)
-- Ozone_first(method): string (nullable = true)
-- Ozone_first(metric_used): string (nullable = true)
-- Ozone_first(units_of_measure): string (nullable = true)
-- PM10 Total 0-10um STP_avg(arithmetic_mean): double (nullable = true)
-- PM10 Total 0-10um STP_avg(first_max_value): double (nullable = true)
-- PM10 Total 0-10um STP_avg(ninety_ninth_percentile): double (nullable = true)
-- PM10 Total 0-10um STP_avg(standard_deviation): double (nullable = true)
-- PM10 Total 0-10um STP_avg(second_max_value): double (nullable = true)
-- PM10 Total 0-10um STP_first(method): string (nullable = true)
-- PM10 Total 0-10um STP_first(metric_used): string (nullable = true)
-- PM10 Total 0-10um STP_first(units_of_measure): string (nullable = true)
-- PM25 - Local Conditions_avg(arithmetic_mean): double (nullable = true)
-- PM25 - Local Conditions_avg(first_max_value): double (nullable = true)
-- PM25 - Local Conditions_avg(ninety_ninth_percentile): double (nullable = true)
-- PM25 - Local Conditions_avg(standard_deviation): double (nullable = true)
-- PM25 - Local Conditions_avg(second_max_value): double (nullable = true)
-- PM25 - Local Conditions_first(method): string (nullable = true)
-- PM25 - Local Conditions_first(metric_used): string (nullable = true)
-- PM25 - Local Conditions_first(units_of_measure): string (nullable = true)
-- Sulfur dioxide_avg(arithmetic_mean): double (nullable = true)
-- Sulfur dioxide_avg(first_max_value): double (nullable = true)
-- Sulfur dioxide_avg(ninety_ninth_percentile): double (nullable = true)
-- Sulfur dioxide_avg(standard_deviation): double (nullable = true)
-- Sulfur dioxide_avg(second_max_value): double (nullable = true)
-- Sulfur dioxide_first(method): string (nullable = true)
-- Sulfur dioxide_first(metric_used): string (nullable = true)
-- Sulfur dioxide_first(units_of_measure): string (nullable = true)

In [0]:
AQIDFAgg2 = AQIDFAgg.groupBy('state','county','year').agg(F.first('Lead (TSP) LC_avg(arithmetic_mean)', ignorenulls=True).alias('LEAD_MEAN'),
                             F.first('Lead (TSP) LC_avg(first_max_value)', ignorenulls=True).alias('LEAD_1STMAX'),
                              F.first('Lead (TSP) LC_avg(ninety_ninth_percentile)', ignorenulls=True).alias('LEAD_99PERC'), 
                              F.first('Lead (TSP) LC_avg(standard_deviation)', ignorenulls=True).alias('LEAD_STD'),
                              F.first('Lead (TSP) LC_avg(second_max_value)', ignorenulls=True).alias('LEAD_2NDMAX'),
                              F.first('Lead (TSP) LC_first(method)', ignorenulls=True).alias('LEAD_METHOD'),
                              F.first('Lead (TSP) LC_first(metric_used)', ignorenulls=True).alias('LEAD_METRIC'),                            
                              F.first('Lead (TSP) LC_first(units_of_measure)', ignorenulls=True).alias('LEAD_UNITS'),
                              F.first('Nitrogen dioxide (NO2)_avg(arithmetic_mean)', ignorenulls=True).alias('NO2_MEAN'),
                              F.first('Nitrogen dioxide (NO2)_avg(first_max_value)', ignorenulls=True).alias('NO2_1STMAX'),
                              F.first('Nitrogen dioxide (NO2)_avg(ninety_ninth_percentile)', ignorenulls=True).alias('NO2_99PERC'),
                              F.first('Nitrogen dioxide (NO2)_avg(standard_deviation)', ignorenulls=True).alias('NO2_STD'),
                              F.first('Nitrogen dioxide (NO2)_avg(second_max_value)', ignorenulls=True).alias('NO2_2NDMAX'),
                              F.first('Nitrogen dioxide (NO2)_first(method)', ignorenulls=True).alias('NO2_METHOD'),
                              F.first('Nitrogen dioxide (NO2)_first(metric_used)', ignorenulls=True).alias('NO2_METRIC'),
                              F.first('Nitrogen dioxide (NO2)_first(units_of_measure)', ignorenulls=True).alias('NO2_UNITS'),
                              F.first('Ozone_avg(arithmetic_mean)', ignorenulls=True).alias('OZONE_MEAN'),
                              F.first('Ozone_avg(first_max_value)', ignorenulls=True).alias('OZONE_1STMAX'),
                              F.first('Ozone_avg(ninety_ninth_percentile)', ignorenulls=True).alias('OZONE_99PERC'),
                              F.first('Ozone_avg(standard_deviation)', ignorenulls=True).alias('OZONE_STD'),
                              F.first('Ozone_avg(second_max_value)', ignorenulls=True).alias('OZONE_2NDMAX'),
                              F.first('Ozone_first(method)', ignorenulls=True).alias('OZONE_METHOD'),
                              F.first('Ozone_first(metric_used)', ignorenulls=True).alias('OZONE_METRIC'),
                              F.first('Ozone_first(units_of_measure)', ignorenulls=True).alias('OZONE_UNITS'),                                                                       
                              F.first('PM10 Total 0-10um STP_avg(arithmetic_mean)', ignorenulls=True).alias('PM10_MEAN'),
                              F.first('PM10 Total 0-10um STP_avg(first_max_value)', ignorenulls=True).alias('PM10_1STMAX'),
                              F.first('PM10 Total 0-10um STP_avg(ninety_ninth_percentile)', ignorenulls=True).alias('PM10_99PERC'),
                              F.first('PM10 Total 0-10um STP_avg(standard_deviation)', ignorenulls=True).alias('PM10_STD'),
                              F.first('PM10 Total 0-10um STP_avg(second_max_value)', ignorenulls=True).alias('PM10_2NDMAX'),
                              F.first('PM10 Total 0-10um STP_first(method)', ignorenulls=True).alias('PM10_METHOD'),
                              F.first('PM10 Total 0-10um STP_first(metric_used)', ignorenulls=True).alias('PM10_METRIC'),
                              F.first('PM10 Total 0-10um STP_first(units_of_measure)', ignorenulls=True).alias('PM10_UNITS'),
                              F.first('PM25 - Local Conditions_avg(arithmetic_mean)', ignorenulls=True).alias('PM25_MEAN'),
                              F.first('PM25 - Local Conditions_avg(first_max_value)', ignorenulls=True).alias('PM25_1STMAX'),
                              F.first('PM25 - Local Conditions_avg(ninety_ninth_percentile)', ignorenulls=True).alias('PM25_99PERC'),
                              F.first('PM25 - Local Conditions_avg(standard_deviation)', ignorenulls=True).alias('PM25_STD'),
                              F.first('PM25 - Local Conditions_avg(second_max_value)', ignorenulls=True).alias('PM25_2NDMAX'),
                              F.first('PM25 - Local Conditions_first(method)', ignorenulls=True).alias('PM25_METHOD'),
                              F.first('PM25 - Local Conditions_first(metric_used)', ignorenulls=True).alias('PM25_METRIC'),
                              F.first('PM25 - Local Conditions_first(units_of_measure)', ignorenulls=True).alias('PM25_UNITS'),
                              F.first('Sulfur dioxide_avg(arithmetic_mean)', ignorenulls=True).alias('SO2_MEAN'),                                     
                              F.first('Sulfur dioxide_avg(first_max_value)', ignorenulls=True).alias('SO2_1STMAX'),
                              F.first('Sulfur dioxide_avg(ninety_ninth_percentile)', ignorenulls=True).alias('SO2_99PERC'),
                              F.first('Sulfur dioxide_avg(standard_deviation)', ignorenulls=True).alias('SO2_STD'),
                              F.first('Sulfur dioxide_avg(second_max_value)', ignorenulls=True).alias('SO2_2NDMAX'),
                              F.first('Sulfur dioxide_first(method)', ignorenulls=True).alias('SO2_METHOD'),
                              F.first('Sulfur dioxide_first(metric_used)', ignorenulls=True).alias('SO2_METRIC'),
                              F.first('Sulfur dioxide_first(units_of_measure)', ignorenulls=True).alias('SO2_UNITS'))
                                                                                                    
display(AQIDFAgg2)

state county year LEAD_MEAN LEAD_1STMAX LEAD_99PERC LEAD_STD LEAD_2NDMAX LEAD_METHOD LEAD_METRIC LEAD_UNITS NO2_MEAN NO2_1STMAX NO2_99PERC NO2_STD NO2_2NDMAX NO2_METHOD NO2_METRIC NO2_UNITS OZONE_MEAN OZONE_1STMAX OZONE_99PERC OZONE_STD OZONE_2NDMAX OZONE_METHOD OZONE_METRIC OZONE_UNITS PM10_MEAN PM10_1STMAX PM10_99PERC PM10_STD PM10_2NDMAX PM10_METHOD PM10_METRIC PM10_UNITS PM25_MEAN PM25_1STMAX PM25_99PERC PM25_STD PM25_2NDMAX PM25_METHOD PM25_METRIC PM25_UNITS SO2_MEAN SO2_1STMAX SO2_99PERC SO2_STD SO2_2NDMAX SO2_METHOD SO2_METRIC SO2_UNITS CA Alameda 2015 null null null null null null null null 20.1278364 49.22 41.7 9.059481 45.279999999999994 INSTRUMENTAL - CHEMILUMINESCENCE Daily Maximum 1-hour average Parts per billion 0.0409086 0.0984 0.08620000000000001 0.0122206 0.092 INSTRUMENTAL - ULTRA VIOLET Daily maxima of observed hourly values (between 9:00 AM and 8:00 PM) Parts per million null null null null null null null null null null null null null null null null null null null null null null null null CA Alameda 2016 null null null null null null null null 19.29764116666667 46.116666666666674 37.73333333333333 7.934909333333333 39.199999999999996 INSTRUMENTAL - CHEMILUMINESCENCE Daily Maximum 1-hour average Parts per billion 0.03733583333333334 0.08216666666666667 0.074 0.011103 0.07816666666666666 INSTRUMENTAL - ULTRA VIOLET Daily maxima of observed hourly values (between 9:00 AM and 8:00 PM) Parts per million null null null null null null null null null null null null null null null null null null null null null null null null CA Alameda 2017 null null null null null null null null 20.515038 61.19999999999999 44.43333333333334 9.129422 49.883333333333326 INSTRUMENTAL - CHEMILUMINESCENCE Daily Maximum 1-hour average Parts per billion 0.038411 0.09766666666666667 0.07100000000000001 0.010734666666666665 0.08733333333333333 INSTRUMENTAL - ULTRA VIOLET Daily maxima of observed hourly values (between 9:00 AM and 8:00 PM) Parts per million null null null null null null null null null null null null null null null null null null null null null null null null CA Alameda 2018 null null null null null null null null 22.827882166666665 69.06666666666666 59.199999999999996 10.554471166666668 65.26666666666667 INSTRUMENTAL - CHEMILUMINESCENCE Daily Maximum 1-hour average Parts per billion 0.036052799999999996 0.07139999999999999 0.0612 0.0095216 0.06739999999999999 INSTRUMENTAL - ULTRA VIOLET Daily maxima of observed hourly values (between 9:00 AM and 8:00 PM) Parts per million null null null null null null null null null null null null null null null null null null null null null null null null CA Alameda 2019 null null null null null null null null 21.414331500000003 55.18333333333334 45.63333333333333 9.367031333333331 50.48333333333334 INSTRUMENTAL - CHEMILUMINESCENCE Daily Maximum 1-hour average Parts per billion 0.0366726 0.0914 0.06799999999999999 0.0104352 0.08499999999999999 INSTRUMENTAL - ULTRA VIOLET Daily maxima of observed hourly values (between 9:00 AM and 8:00 PM) Parts per million null null null null null null null null null null null null null null null null null null null null null null null null CA Amador 2015 null null null null null null null null null null null null null null null null 0.048449 0.103 0.088 0.015178 0.094 INSTRUMENTAL - ULTRA VIOLET ABSORPTION Daily maxima of observed hourly values (between 9:00 AM and 8:00 PM) Parts per million null null null null null null null null null null null null null null null null null null null null null null null null CA Amador 2016 null null null null null null null null null null null null null null null null 0.047055 0.104 0.081 0.014501 0.084 INSTRUMENTAL - ULTRA VIOLET ABSORPTION Daily maxima of observed hourly values (between 9:00 AM and 8:00 PM) Parts per million null null null null null null null null null null null null null null null null null null null null null null null null CA Amador 2017 null null null null null null null null null null null null nul

In [0]:

print(AQIDFAgg2.printSchema())

root
-- state: string (nullable = false)
-- county: string (nullable = true)
-- year: long (nullable = true)
-- LEAD_MEAN: double (nullable = true)
-- LEAD_1STMAX: double (nullable = true)
-- LEAD_99PERC: double (nullable = true)
-- LEAD_STD: double (nullable = true)
-- LEAD_2NDMAX: double (nullable = true)
-- LEAD_METHOD: string (nullable = true)
-- LEAD_METRIC: string (nullable = true)
-- LEAD_UNITS: string (nullable = true)
-- NO2_MEAN: double (nullable = true)
-- NO2_1STMAX: double (nullable = true)
-- NO2_99PERC: double (nullable = true)
-- NO2_STD: double (nullable = true)
-- NO2_2NDMAX: double (nullable = true)
-- NO2_METHOD: string (nullable = true)
-- NO2_METRIC: string (nullable = true)
-- NO2_UNITS: string (nullable = true)
-- OZONE_MEAN: double (nullable = true)
-- OZONE_1STMAX: double (nullable = true)
-- OZONE_99PERC: double (nullable = true)
-- OZONE_STD: double (nullable = true)
-- OZONE_2NDMAX: double (nullable = true)
-- OZONE_METHOD: string (nullable = true)
-- OZONE_METRIC: string (nullable = true)
-- OZONE_UNITS: string (nullable = true)
-- PM10_MEAN: double (nullable = true)
-- PM10_1STMAX: double (nullable = true)
-- PM10_99PERC: double (nullable = true)
-- PM10_STD: double (nullable = true)
-- PM10_2NDMAX: double (nullable = true)
-- PM10_METHOD: string (nullable = true)
-- PM10_METRIC: string (nullable = true)
-- PM10_UNITS: string (nullable = true)
-- PM25_MEAN: double (nullable = true)
-- PM25_1STMAX: double (nullable = true)
-- PM25_99PERC: double (nullable = true)
-- PM25_STD: double (nullable = true)
-- PM25_2NDMAX: double (nullable = true)
-- PM25_METHOD: string (nullable = true)
-- PM25_METRIC: string (nullable = true)
-- PM25_UNITS: string (nullable = true)
-- SO2_MEAN: double (nullable = true)
-- SO2_1STMAX: double (nullable = true)
-- SO2_99PERC: double (nullable = true)
-- SO2_STD: double (nullable = true)
-- SO2_2NDMAX: double (nullable = true)
-- SO2_METHOD: string (nullable = true)
-- SO2_METRIC: string (nullable = true)
-- SO2_UNITS: string (nullable = true)

None

## LOAD

### 5. Link the asthma dataframe to the counties table

In [0]:
server = 'gen10-data-fundamentals-21-11-sql-server.database.windows.net'
database = 'jadr-SQL-Database'
port = '1433'
user = dbutils.secrets.get(scope = "jadr_blob", key = "SQLUser_dg")
password = dbutils.secrets.get(scope = "jadr_blob", key = "SQLPassword_dg")
url = f"jdbc:sqlserver://{server}:{port};databaseName={database};user={user};password={password};" 

Read in the current county table and state table and join them. We will match up the county state in each and join to the asthma dataframe. If a match is not found, do a quick check that there isn't an error. If not, go ahead and add the mising county to the database.

In [0]:

countyDF = spark.read.format("jdbc") \
    .option("url", url) \
    .option("dbtable", "County") \
    .option("user", user) \
    .option("password", password) \
    .option("driver", "com.microsoft.sqlserver.jdbc.SQLServerDriver") \
    .load()
display(countyDF)
countySchema = countyDF.schema
print(countySchema)
print(countySchema[1].name)

stateDF = spark.read.format("jdbc") \
    .option("url", url) \
    .option("dbtable", "State") \
    .option("user", user) \
    .option("password", password) \
    .option("driver", "com.microsoft.sqlserver.jdbc.SQLServerDriver") \
    .load()
display(stateDF)


countyStateDF = countyDF.join(stateDF, on='STATE_ID', how='inner')
display(countyStateDF)

COUNTY_ID COUNTY_NAME STATE_ID 1 Tuscaloosa 28 2 Sumter 28 3 Fremont 22 4 Pratt 42 5 Baltimo 3 6 Oregon 43 7 Carroll 20 8 Warren 19 9 Cattaraugus 19 10 Jefferson 26 11 San Saba 26 12 Guadalupe 26 13 Sublette 7 14 Wheeler 26 15 Waukesha 31 16 Chaffee 4 17 Mohave 41 18 Nassau 25 19 Webster 37 20 Hancock 32 21 Worth 22 22 Whitley 32 23 Renville 27 24 Lincoln 43 25 Clatsop 48 26 Briscoe 26 27 Clark 33 28 Ozaukee 31 29 Lassen 15 30 Baxter 11 31 Elmore 28 32 Marion 24 33 Bienville 12 34 Clayton 22 35 Chautauqua 42 36 Cottonwood 27 37 Silver Bow 1 38 Douglas 46 39 Putnam 45 40 Bedford 29 41 Cass 26 42 Hemphill 26 43 Obion 13 44 Berkeley 36 45 Bennington 40 46 Contra Costa 15 47 Ben Hill 37 48 Jasper 22 49 McPherson 46 50 Iredell 2 51 Ashe 2 52 Oklahoma 47 53 Foard 26 54 Maricopa 41 55 Morgan 37 56 Poweshiek 22 57 Watonwan 27 58 Cabarrus 2 59 Franklin 29 60 Gonzales 26 61 Wood 26 62 Northumberland 34 63 Bullock 28 64 Pasco 25 65 Calaveras 15 66 DeSoto 25 67 Latah 50 68 Crawford 42 69 Carter 43 70 Dillon 44 71 Sandusky 45 72 Trumbull 45 73 Potter 33 74 Marengo 28 75 Marshall 28 76 Gibson 32 77 Linn 42 78 Trego 42 79 Wilkin 27 80 Carroll 43 81 Ralls 43 82 Quay 16 83 La Salle 26 84 Vernon 31 85 Shenandoah 34 86 Calumet 31 87 Franklin 6 88 DeKalb 6 89 Liberty 37 90 Upson 37 91 Gilmer 37 92 Franklin 12 93 Wyandotte 42 94 Socorro 16 95 Rockingham 20 96 Uinta 7 97 Asotin 21 98 Sussex 34 99 Chambers 28 100 Monroe 28 101 Avoyelles 12 102 Lincoln 16 103 Ulster 19 104 Ontario 19 105 Mason 26 106 Rusk 26 107 Manitowoc 31 108 Franklin 21 109 Zapata 26 110 Adams 22 111 Scott 38 112 Niagara 19 113 Loup 46 114 De Baca 16 115 Cleveland 2 116 Teton 1 117 Cameron 26 118 Ellis 26 119 Hampshire 36 120 Pepin 31 121 Newton 11 122 Escambia 25 123 Pike 6 124 Daviess 32 125 Pendleton 24 126 Scott 22 127 Oneida 19 128 Rowan 2 129 Gaines 26 130 Chelan 21 131 King William 34 132 Greenlee 41 133 Wrangell City and 14 134 Nevada 15 135 Valdez-Cordova Cens 14 136 Lee 6 137 Worth 37 138 Osage 42 139 Gratiot 18 140 Camden 43 141 Hill 1 142 Carbon 1 143 Franklin 46 144 Bottineau 39 145 Ramsey 39 146 Chester 29 147 Latimer 47 148 Jasper 26 149 Clarke 34 150 Northampton 34 151 Pike 11 152 Butte 15 153 Mobile 28 154 Martin 25 155 Phillips 11 156 Idaho 50 157 De Soto 12 158 Crittenden 24 159 Sioux 22 160 Monroe 22 161 Pike 43 162 Osage 43 163 Greene 38 164 Wayne 18 165 Passaic 8 166 Ste. Genevieve 43 167 Sheridan 1 168 Sullivan 29 169 Grundy 13 170 Juneau 31 171 Summers 36 172 Autauga 28 173 Mineral 4 174 Lincoln 4 175 Jackson 6 176 Colquitt 37 177 Walker 37 178 Mitchell 22 179 Marshall 22 180 Chippewa 27 181 Macon 43 182 Lewis and Clark 1 183 Washington 43 184 Fulton 19 185 Stone 43 186 Storey 49 187 Wilkes 2 188 Cavalier 39 189 Crawford 29 190 Hickman 13 191 Northwest Arctic 14 192 Blount 28 193 Breckinridge 24 194 Warren 22 195 Labette 42 196 Hampshire 51 197 Billings 39 198 Clermont 45 199 Sumter 44 200 Lowndes 28 201 Lawrence 32 202 Clinch 37 203 Peoria 6 204 Wichita 42 205 Nodaway 43 206 Howell 43 207 Maries 43 208 Mackinac 18 209 Perkins 46 210 Brunswick 2 211 Stillwater 1 212 Jefferson 45 213 York 29 214 Wallowa 48 215 Clark 45 216 Oldham 26 217 Garza 26 218 Grant 36 219 Orleans 40 220 Fremont 4 221 Boone 11 222 Santa Cruz 15 223 Greene 28 224 Humboldt 15 225 Coconino 41 226 Rooks 42 227 Caldwell 12 228 Clare 18 229 Lafayette 43 230 Park 1 231 Anson 2 232 Merrimack 20 233 Richmond 2 234 Laurens 44 235 Clarendon 44 236 Stephens 47 237 Chester 13 238 Boone 36 239 Sevier 17 240 Walla Walla 21 241 Essex 34 242 Escambia 28 243 Putnam 25 244 Chicot 11 245 Marion 37 246 Fulton 6 247 Canyon 50 248 Page 22 249 Pointe Coupee 12 250 Knox 43 251 Le Sueur 27 252 Butler 43 253 Lake of the Woods 27 254 Benton 38 255 Washington 3 256 Watauga 2 257 Hartley 26 258 Comanche 26 259 Sanborn 33 260 Meigs 13 261 Willacy 26 262 Monroe 36 263 Kenai Peninsula 14 264 Marion 28 265 Barbour 28 266 Long 37 267 Ada 50 268 Clearwater 27 269 Clay 27 270 Lewis 19 271 Robeson 2 272 Knox 45 273 Tillam

StructType(List(StructField(COUNTY_ID,IntegerType,true),StructField(COUNTY_NAME,StringType,true),StructField(STATE_ID,IntegerType,true)))
COUNTY_NAME

STATE_ID STATE_ABBR STATE_NAME 1 MT Montana 2 NC North Carolina 3 MD Maryland 4 CO Colorado 5 CT Connecticut 6 IL Illinois 7 WY Wyoming 8 NJ New Jersey 9 DE Delaware 10 DC District of Columbia 11 AR Arkansas 12 LA Louisiana 13 TN Tennessee 14 AK Alaska 15 CA California 16 NM New Mexico 17 UT Utah 18 MI Michigan 19 NY New York 20 NH New Hampshire 21 WA Washington 22 IA Iowa 23 ME Maine 24 KY Kentucky 25 FL Florida 26 TX Texas 27 MN Minnesota 28 AL Alabama 29 PA Pennsylvania 30 RI Rhode Island 31 WI Wisconsin 32 IN Indiana 33 SD South Dakota 34 VA Virginia 35 HI Hawaii 36 WV West Virginia 37 GA Georgia 38 MS Mississippi 39 ND North Dakota 40 VT Vermont 41 AZ Arizona 42 KS Kansas 43 MO Missouri 44 SC South Carolina 45 OH Ohio 46 NE Nebraska 47 OK Oklahoma 48 OR Oregon 49 NV Nevada 50 ID Idaho 51 MA Massachusetts 64 null District Of Columbia

STATE_ID COUNTY_ID COUNTY_NAME STATE_ABBR STATE_NAME 1 3109 Big Horn MT Montana 1 2975 Petroleum MT Montana 1 2953 Granite MT Montana 1 2924 Carter MT Montana 1 2832 Rosebud MT Montana 1 2770 Flathead MT Montana 1 2639 Daniels MT Montana 1 2568 Deer Lodge MT Montana 1 2498 Ravalli MT Montana 1 2497 McCone MT Montana 1 2409 Valley MT Montana 1 2378 Blaine MT Montana 1 2363 Beaverhead MT Montana 1 2307 Sanders MT Montana 1 2306 Dawson MT Montana 1 2287 Richland MT Montana 1 2272 Lake MT Montana 1 2158 Musselshell MT Montana 1 2126 Fallon MT Montana 1 2094 Judith Basin MT Montana 1 2074 Gallatin MT Montana 1 2014 Meagher MT Montana 1 1978 Madison MT Montana 1 1812 Cascade MT Montana 1 1707 Yellowstone MT Montana 1 1689 Toole MT Montana 1 1582 Prairie MT Montana 1 1557 Pondera MT Montana 1 1533 Custer MT Montana 1 1456 Jefferson MT Montana 1 1398 Liberty MT Montana 1 1374 Powder River MT Montana 1 1279 Chouteau MT Montana 1 1171 Broadwater MT Montana 1 1133 Sweet Grass MT Montana 1 1008 Powell MT Montana 1 951 Wheatland MT Montana 1 806 Phillips MT Montana 1 678 Golden Valley MT Montana 1 644 Glacier MT Montana 1 627 Fergus MT Montana 1 610 Missoula MT Montana 1 559 Mineral MT Montana 1 487 Lincoln MT Montana 1 467 Roosevelt MT Montana 1 359 Garfield MT Montana 1 357 Treasure MT Montana 1 323 Wibaux MT Montana 1 230 Park MT Montana 1 211 Stillwater MT Montana 1 182 Lewis and Clark MT Montana 1 167 Sheridan MT Montana 1 142 Carbon MT Montana 1 141 Hill MT Montana 1 116 Teton MT Montana 1 37 Silver Bow MT Montana 2 3092 Currituck NC North Carolina 2 2999 Mitchell NC North Carolina 2 2998 Durham NC North Carolina 2 2974 Beaufort NC North Carolina 2 2925 Duplin NC North Carolina 2 2908 Davidson NC North Carolina 2 2810 Greene NC North Carolina 2 2785 Alleghany NC North Carolina 2 2769 Guilford NC North Carolina 2 2731 Yancey NC North Carolina 2 2714 McDowell NC North Carolina 2 2692 Caswell NC North Carolina 2 2691 Columbus NC North Carolina 2 2672 Transylvania NC North Carolina 2 2671 Madison NC North Carolina 2 2638 Hertford NC North Carolina 2 2597 Cherokee NC North Carolina 2 2587 Randolph NC North Carolina 2 2585 Northampton NC North Carolina 2 2520 Franklin NC North Carolina 2 2501 Stanly NC North Carolina 2 2482 Wilson NC North Carolina 2 2448 Graham NC North Carolina 2 2408 Orange NC North Carolina 2 2377 Gaston NC North Carolina 2 2285 Hyde NC North Carolina 2 2193 Burke NC North Carolina 2 2110 Pender NC North Carolina 2 2092 Clay NC North Carolina 2 2041 Scotland NC North Carolina 2 2003 Alamance NC North Carolina 2 1980 Montgomery NC North Carolina 2 1979 Cumberland NC North Carolina 2 1964 Onslow NC North Carolina 2 1934 Forsyth NC North Carolina 2 1849 Warren NC North Carolina 2 1811 Catawba NC North Carolina 2 1784 Carteret NC North Carolina 2 1730 Lincoln NC North Carolina 2 1712 Vance NC North Carolina 2 1708 Moore NC North Carolina 2 1688 Bladen NC North Carolina 2 1687 Gates NC North Carolina 2 1670 Martin NC North Carolina 2 1649 Harnett NC North Carolina 2 1635 Caldwell NC North Carolina 2 1634 Alexander NC North Carolina 2 1568 Davie NC North Carolina 2 1545 Person NC North Carolina 2 1519 Perquimans NC North Carolina 2 1505 Surry NC North Carolina 2 1479 New Hanover NC North Carolina 2 1438 Camden NC North Carolina 2 1390 Mecklenburg NC North Carolina 2 1246 Pasquotank NC North Carolina 2 1104 Yadkin NC North Carolina 2 1089 Lenoir NC North Carolina 2 1069 Wayne NC North Carolina 2 1057 Lee NC North Carolina 2 1045 Dare NC North Carolina 2 994 Pitt NC North Carolina 2 960 Edgecombe NC North Carolina 2 917 Chatham NC North Carolina 2 904 Stokes NC North Carolina 2 901 Swain NC North Carolina 2 851 Avery NC North Carolina 2 836 Rutherford NC North Carolina 2 818 Wake NC North Carolina 2 816 Macon NC North Carolina 2 792 Washington NC North Carolina 2 790 Rockingham NC North Carolina 2 788 Chowan NC North Carolina 2 746 Buncombe NC North Carolina 2 732 Haywood NC North Carolina 2 698 Tyrrell NC North Carolina 2 676

In [0]:
from pyspark.sql.types import StructType,StructField, StringType
import pyodbc
# If nothing has been loaded in the county table in the database, we need to construct the first set from the asthma dataset
if(countyStateDF.count() == 0):
    schema = StructType([ \
        StructField("STATE_ABBR",StringType(),True), \
        StructField("STATE_NAME",StringType(),True)])
    newStateDF = spark.createDataFrame([("CA", "California")],schema)
    
    # Save and reload to get the latest ID numbers
    # Put in a try statement in case the state already exists
    try:
        writer = newStateDF.write.format("jdbc").option("url", url) \
            .mode("append") \
            .option("dbtable", 'State') \
            .option("user", user) \
            .option("password", password) \
            .option("driver", "com.microsoft.sqlserver.jdbc.SQLServerDriver")
        writer.save()
    except Exception as e:
        print(e)
    
    stateDF = spark.read.format("jdbc") \
        .option("url", url) \
        .option("dbtable", "State") \
        .option("user", user) \
        .option("password", password) \
        .option("driver", "com.microsoft.sqlserver.jdbc.SQLServerDriver") \
        .load()
    display(stateDF)
    
    countyDF = asthmaTotalDFjoined.select('COUNTY').distinct()
    # Need to remember that this list has statewide data. Remove California from the county list
    countyDF = countyDF.filter(countyDF.COUNTY != 'California')
    display(countyDF)
    countyDF = countyDF.withColumn('STATE_ID', lit(stateDF.filter((stateDF.STATE_ABBR == 'CA')).first()['STATE_ID']))
    display(countyDF)
    # Rename the column to match the SQL table
    countyDF = countyDF.withColumnRenamed("COUNTY",countySchema[1].name)
    print(countyDF.printSchema())
    # Write and reload to get the latest ID numbers
    try:
        writer = countyDF.write.format("jdbc").option("url", url) \
            .mode("append") \
            .option("dbtable", 'County') \
            .option("user", user) \
            .option("password", password) \
            .option("driver", "com.microsoft.sqlserver.jdbc.SQLServerDriver")
        writer.save()
    except Exception as e:
        print(e)
    
    countyDF = spark.read.format("jdbc") \
        .option("url", url) \
        .option("dbtable", "County") \
        .option("user", user) \
        .option("password", password) \
        .option("driver", "com.microsoft.sqlserver.jdbc.SQLServerDriver") \
        .load()
    display(countyDF)
    
    # Join the two new dataframes and continue
    countyStateDF = countyDF.join(stateDF, on='STATE_ID', how='inner')
    display(countyStateDF)

In [0]:
import pandas as pd
# Add in an ID to the table 
asthmaTotalDF = asthmaTotalDF.withColumn('AsthmaID',F.monotonically_increasing_id()+1)

matched = pd.DataFrame([])
noMatchFound = False
display(asthmaTotalDF)
# If there are current countyies in the database, look through them for a match
if(countyStateDF.count() > 0):
    for countyAsthma in asthmaTotalDF.toLocalIterator():
        matchedCol = countyStateDF.filter((countyStateDF.COUNTY_NAME == countyAsthma.COUNTY) & (countyStateDF.STATE_ABBR == countyAsthma.STATE)).select('COUNTY_ID')  
        # There are conditions where there isn't a match like if the county isn't loaded in the in the table, yet, or we have statewide data.
        if(matchedCol.count() >0):
            matched = matched.append({'AsthmaID': countyAsthma.AsthmaID, 
                                      'COUNTY_ID': matchedCol.collect()[0][0]},
                                     ignore_index=True)
        else: noMatchFound = True
    if(len(matched)>0):    
        matched = spark.createDataFrame(matched)
        display(matched)
        # if everything went ok, then join the matched tabled of county ID's to the asthma dataframe
        asthmaTotalDF = asthmaTotalDF.join(matched, on='AsthmaID', how='left_outer')
        display(asthmaTotalDF)
    else:
        print("NOTHING MATCHED")
        asthmaTotalDF = asthmaTotalDF.withColumn('COUNTY_ID', lit(None))

display(asthmaTotalDF)


STATE COUNTY YEAR NUMBER OF ED VISITS AGE-ADJUSTED ED VISIT RATE AsthmaID CA California 2015 191904 50.4 1 CA Alameda 2015 9939 64.3 2 CA Amador 2015 196 58.4 3 CA Butte 2015 1044 50.2 4 CA Calaveras 2015 185 48.0 5 CA Colusa 2015 97 41.4 6 CA Contra Costa 2015 6858 65.2 7 CA Del Norte 2015 140 53.0 8 CA El Dorado 2015 592 36.4 9 CA Fresno 2015 7936 77.0 10 CA Glenn 2015 122 42.6 11 CA Humboldt 2015 835 63.4 12 CA Imperial 2015 1388 71.2 13 CA Inyo 2015 88 53.5 14 CA Kern 2015 5859 62.3 15 CA Kings 2015 1250 78.6 16 CA Lake 2015 478 80.4 17 CA Lassen 2015 148 45.3 18 CA Los Angeles 2015 52227 53.1 19 CA Madera 2015 1031 62.3 20 CA Marin 2015 541 22.2 21 CA Mariposa 2015 79 47.4 22 CA Mendocino 2015 479 57.4 23 CA Merced 2015 2425 87.4 24 CA Modoc 2015 53 67.9 25 CA Mono 2015 43 32.0 26 CA Monterey 2015 2194 50.2 27 CA Napa 2015 572 41.9 28 CA Nevada 2015 351 42.8 29 CA Orange 2015 10275 33.9 30 CA Placer 2015 1125 31.4 31 CA Plumas 2015 99 56.3 32 CA Riverside 2015 10111 43.2 33 CA Sacramento 2015 10109 69.2 34 CA San Benito 2015 285 50.1 35 CA San Bernardino 2015 12761 59.3 36 CA San Diego 2015 11646 37.0 37 CA San Francisco 2015 3141 41.3 38 CA San Joaquin 2015 4802 66.2 39 CA San Luis Obispo 2015 950 40.1 40 CA San Mateo 2015 2695 36.4 41 CA Santa Barbara 2015 1734 40.7 42 CA Santa Clara 2015 6521 35.1 43 CA Santa Cruz 2015 910 36.5 44 CA Shasta 2015 1015 60.5 45 CA Siskiyou 2015 176 47.0 46 CA Solano 2015 3415 83.2 47 CA Sonoma 2015 1936 40.2 48 CA Stanislaus 2015 3281 60.7 49 CA Sutter 2015 337 34.1 50 CA Tehama 2015 323 52.7 51 CA Trinity 2015 67 60.5 52 CA Tulare 2015 2542 51.3 53 CA Tuolumne 2015 257 53.1 54 CA Ventura 2015 2933 35.3 55 CA Yolo 2015 852 44.1 56 CA Yuba 2015 346 45.4 57 CA California 2016 174733 45.8 58 CA Alameda 2016 9086 57.8 59 CA Amador 2016 187 61.8 60 CA Butte 2016 770 38.1 61 CA Calaveras 2016 171 45.3 62 CA Colusa 2016 67 29.6 63 CA Contra Costa 2016 6021 56.8 64 CA Del Norte 2016 172 71.1 65 CA El Dorado 2016 564 35.5 66 CA Fresno 2016 6930 67.4 67 CA Glenn 2016 103 36.3 68 CA Humboldt 2016 815 64.5 69 CA Imperial 2016 1287 66.3 70 CA Inyo 2016 90 53.7 71 CA Kern 2016 5008 54.5 72 CA Kings 2016 1027 65.0 73 CA Lake 2016 487 79.4 74 CA Lassen 2016 118 40.7 75 CA Los Angeles 2016 50778 51.5 76 CA Madera 2016 956 60.2 77 CA Marin 2016 543 23.1 78 CA Mariposa 2016 66 45.3 79 CA Mendocino 2016 451 56.4 80 CA Merced 2016 2211 79.2 81 CA Modoc 2016 59 80.1 82 CA Mono 2016 33 28.1 83 CA Monterey 2016 1959 44.3 84 CA Napa 2016 439 33.5 85 CA Nevada 2016 267 33.6 86 CA Orange 2016 8878 29.2 87 CA Placer 2016 968 28.3 88 CA Plumas 2016 99 61.4 89 CA Riverside 2016 9596 41.5 90 CA Sacramento 2016 8953 60.7 91 CA San Benito 2016 268 48.7 92 CA San Bernardino 2016 11335 51.9 93 CA San Diego 2016 10068 30.9 94 CA San Francisco 2016 2997 38.5 95 CA San Joaquin 2016 4245 57.5 96 CA San Luis Obispo 2016 926 38.1 97 CA San Mateo 2016 2382 32.5 98 CA Santa Barbara 2016 1641 37.7 99 CA Santa Clara 2016 5534 29.1 100 CA Santa Cruz 2016 864 34.4 101 CA Shasta 2016 726 46.4 102 CA Siskiyou 2016 128 33.7 103 CA Solano 2016 3349 80.8 104 CA Sonoma 2016 1682 36.6 105 CA Stanislaus 2016 2763 51.3 106 CA Sutter 2016 324 33.7 107 CA Tehama 2016 335 55.9 108 CA Trinity 2016 55 52.7 109 CA Tulare 2016 1980 40.5 110 CA Tuolumne 2016 224 46.9 111 CA Ventura 2016 2619 32.4 112 CA Yolo 2016 774 38.4 113 CA Yuba 2016 297 39.2 114 CA California 2017 180053 46.9 115 CA Alameda 2017 8942 56.3 116 CA Amador 2017 176 56.8 117 CA Butte 2017 936 45.3 118 CA Calaveras 2017 198 55.1 119 CA Colusa 2017 62 28.4 120 CA Contra Costa 2017 6706 62.6 121 CA Del Norte 2017 150 61.2 122 CA El Dorado 2017 650 40.5 123 CA Fresno 2017 7783 75.4 124 CA Glenn 2017 129 45.6 125 CA Humboldt 2017 851 67.1 126 CA Imperial 2017 1291 65.7 127 CA Inyo 2017 110 70.7 128 CA Kern 2017 4853 52.2 129 CA Kings 2017 1074 67.9 130 CA Lake 2017 482 80.1 131 CA Lassen 2017 131 44.0 132 CA Los Angeles 2017 49504 50.0 133 CA Madera 2017 979 61.7 134 CA Marin 2017 564 23.

AsthmaID COUNTY_ID 2.0 3085.0 3.0 843.0 4.0 152.0 5.0 65.0 6.0 545.0 7.0 46.0 8.0 2947.0 9.0 1751.0 10.0 2778.0 11.0 2490.0 12.0 224.0 13.0 1113.0 14.0 1797.0 15.0 1697.0 16.0 1973.0 17.0 603.0 18.0 29.0 19.0 3118.0 20.0 2633.0 21.0 2492.0 22.0 1371.0 23.0 568.0 24.0 318.0 25.0 2173.0 26.0 3048.0 27.0 2548.0 28.0 1252.0 29.0 134.0 30.0 2491.0 31.0 605.0 32.0 1349.0 33.0 586.0 34.0 536.0 35.0 2508.0 36.0 2590.0 37.0 2343.0 38.0 2816.0 39.0 2664.0 40.0 2457.0 41.0 822.0 42.0 1796.0 43.0 1737.0 44.0 222.0 45.0 3005.0 46.0 534.0 47.0 1775.0 48.0 862.0 49.0 809.0 50.0 2929.0 51.0 1971.0 52.0 2966.0 53.0 1720.0 54.0 1144.0 55.0 1406.0 56.0 1994.0 57.0 782.0 59.0 3085.0 60.0 843.0 61.0 152.0 62.0 65.0 63.0 545.0 64.0 46.0 65.0 2947.0 66.0 1751.0 67.0 2778.0 68.0 2490.0 69.0 224.0 70.0 1113.0 71.0 1797.0 72.0 1697.0 73.0 1973.0 74.0 603.0 75.0 29.0 76.0 3118.0 77.0 2633.0 78.0 2492.0 79.0 1371.0 80.0 568.0 81.0 318.0 82.0 2173.0 83.0 3048.0 84.0 2548.0 85.0 1252.0 86.0 134.0 87.0 2491.0 88.0 605.0 89.0 1349.0 90.0 586.0 91.0 536.0 92.0 2508.0 93.0 2590.0 94.0 2343.0 95.0 2816.0 96.0 2664.0 97.0 2457.0 98.0 822.0 99.0 1796.0 100.0 1737.0 101.0 222.0 102.0 3005.0 103.0 534.0 104.0 1775.0 105.0 862.0 106.0 809.0 107.0 2929.0 108.0 1971.0 109.0 2966.0 110.0 1720.0 111.0 1144.0 112.0 1406.0 113.0 1994.0 114.0 782.0 116.0 3085.0 117.0 843.0 118.0 152.0 119.0 65.0 120.0 545.0 121.0 46.0 122.0 2947.0 123.0 1751.0 124.0 2778.0 125.0 2490.0 126.0 224.0 127.0 1113.0 128.0 1797.0 129.0 1697.0 130.0 1973.0 131.0 603.0 132.0 29.0 133.0 3118.0 134.0 2633.0 135.0 2492.0 136.0 1371.0 137.0 568.0 138.0 318.0 139.0 2173.0 140.0 3048.0 141.0 2548.0 142.0 1252.0 143.0 134.0 144.0 2491.0 145.0 605.0 146.0 1349.0 147.0 586.0 148.0 536.0 149.0 2508.0 150.0 2590.0 151.0 2343.0 152.0 2816.0 153.0 2664.0 154.0 2457.0 155.0 822.0 156.0 1796.0 157.0 1737.0 158.0 222.0 159.0 3005.0 160.0 534.0 161.0 1775.0 162.0 862.0 163.0 809.0 164.0 2929.0 165.0 1971.0 166.0 2966.0 167.0 1720.0 168.0 1144.0 169.0 1406.0 170.0 1994.0 171.0 782.0 173.0 3085.0 174.0 843.0 175.0 152.0 176.0 65.0 177.0 545.0 178.0 46.0 179.0 2947.0 180.0 1751.0 181.0 2778.0 182.0 2490.0 183.0 224.0 184.0 1113.0 185.0 1797.0 186.0 1697.0 187.0 1973.0 188.0 603.0 189.0 29.0 190.0 3118.0 191.0 2633.0 192.0 2492.0 193.0 1371.0 194.0 568.0 195.0 318.0 196.0 2173.0 197.0 3048.0 198.0 2548.0 199.0 1252.0 200.0 134.0 201.0 2491.0 202.0 605.0 203.0 1349.0 204.0 586.0 205.0 536.0 206.0 2508.0 207.0 2590.0 208.0 2343.0 209.0 2816.0 210.0 2664.0 211.0 2457.0 212.0 822.0 213.0 1796.0 214.0 1737.0 215.0 222.0 216.0 3005.0 217.0 2547.0 218.0 534.0 219.0 1775.0 220.0 862.0 221.0 809.0 222.0 2929.0 223.0 1971.0 224.0 2966.0 225.0 1720.0 226.0 1144.0 227.0 1406.0 228.0 1994.0 229.0 782.0 231.0 3085.0 232.0 843.0 233.0 152.0 234.0 65.0 235.0 545.0 236.0 46.0 237.0 2947.0 238.0 1751.0 239.0 2778.0 240.0 2490.0 241.0 224.0 242.0 1113.0 243.0 1797.0 244.0 1697.0 245.0 1973.0 246.0 603.0 247.0 29.0 248.0 3118.0 249.0 2633.0 250.0 2492.0 251.0 1371.0 252.0 568.0 253.0 318.0 254.0 2173.0 255.0 3048.0 256.0 2548.0 257.0 1252.0 258.0 134.0 259.0 2491.0 260.0 605.0 261.0 1349.0 262.0 586.0 263.0 536.0 264.0 2508.0 265.0 2590.0 266.0 2343.0 267.0 2816.0 268.0 2664.0 269.0 2457.0 270.0 822.0 271.0 1796.0 272.0 1737.0 273.0 222.0 274.0 3005.0 275.0 534.0 276.0 1775.0 277.0 862.0 278.0 809.0 279.0 2929.0 280.0 1971.0 281.0 2966.0 282.0 1720.0 283.0 1144.0 284.0 1406.0 285.0 1994.0 286.0 782.0

AsthmaID STATE COUNTY YEAR NUMBER OF ED VISITS AGE-ADJUSTED ED VISIT RATE COUNTY_ID 147 CA Riverside 2017 10076 43.2 586.0 170 CA Yolo 2017 894 43.3 1994.0 184 CA Imperial 2018 1147 58.1 1113.0 160 CA Siskiyou 2017 159 42.1 534.0 169 CA Ventura 2017 2836 34.8 1406.0 8 CA Del Norte 2015 140 53.0 2947.0 67 CA Fresno 2016 6930 67.4 2778.0 70 CA Imperial 2016 1287 66.3 1113.0 168 CA Tuolumne 2017 244 53.6 1144.0 69 CA Humboldt 2016 815 64.5 224.0 206 CA San Benito 2018 318 56.7 2508.0 7 CA Contra Costa 2015 6858 65.2 46.0 249 CA Madera 2019 781 49.1 2633.0 142 CA Napa 2017 537 40.2 1252.0 191 CA Madera 2018 813 50.9 2633.0 112 CA Ventura 2016 2619 32.4 1406.0 154 CA San Luis Obispo 2017 800 33.3 2457.0 232 CA Amador 2019 169 53.2 843.0 124 CA Fresno 2017 7783 75.4 2778.0 253 CA Merced 2019 1690 59.4 318.0 128 CA Inyo 2017 110 70.7 1797.0 201 CA Orange 2018 8183 26.5 2491.0 235 CA Colusa 2019 103 45.4 545.0 108 CA Tehama 2016 335 55.9 1971.0 180 CA El Dorado 2018 564 34.1 1751.0 255 CA Mono 2019 51 46.5 3048.0 271 CA Santa Barbara 2019 1228 27.8 1796.0 234 CA Calaveras 2019 199 58.4 65.0 133 CA Los Angeles 2017 49504 50.0 3118.0 181 CA Fresno 2018 6935 67.0 2778.0 88 CA Placer 2016 968 28.3 605.0 280 CA Tehama 2019 274 47.0 1971.0 49 CA Stanislaus 2015 3281 60.7 809.0 286 CA Yuba 2019 328 42.3 782.0 155 CA San Mateo 2017 2346 31.8 822.0 214 CA Santa Clara 2018 5095 26.4 1737.0 101 CA Santa Cruz 2016 864 34.4 222.0 217 CA Sierra 2018 12 52.5 2547.0 98 CA San Mateo 2016 2382 32.5 822.0 116 CA Alameda 2017 8942 56.3 3085.0 167 CA Tulare 2017 2134 43.4 1720.0 238 CA El Dorado 2019 539 33.7 1751.0 29 CA Nevada 2015 351 42.8 134.0 107 CA Sutter 2016 324 33.7 2929.0 182 CA Glenn 2018 101 35.9 2490.0 268 CA San Joaquin 2019 4390 57.9 2664.0 64 CA Contra Costa 2016 6021 56.8 46.0 75 CA Lassen 2016 118 40.7 29.0 47 CA Solano 2015 3415 83.2 1775.0 279 CA Sutter 2019 274 27.8 2929.0 42 CA Santa Barbara 2015 1734 40.7 1796.0 144 CA Orange 2017 9084 29.7 2491.0 215 CA Santa Cruz 2018 725 27.9 222.0 44 CA Santa Cruz 2015 910 36.5 222.0 236 CA Contra Costa 2019 5910 54.2 46.0 35 CA San Benito 2015 285 50.1 2508.0 62 CA Calaveras 2016 171 45.3 65.0 96 CA San Joaquin 2016 4245 57.5 2664.0 219 CA Solano 2018 3354 79.6 1775.0 151 CA San Diego 2017 10339 31.7 2343.0 18 CA Lassen 2015 148 45.3 29.0 258 CA Nevada 2019 218 27.2 134.0 275 CA Siskiyou 2019 148 40.4 534.0 80 CA Mendocino 2016 451 56.4 568.0 86 CA Nevada 2016 267 33.6 134.0 171 CA Yuba 2017 366 47.9 782.0 178 CA Contra Costa 2018 6001 55.4 46.0 218 CA Siskiyou 2018 138 34.1 534.0 120 CA Colusa 2017 62 28.4 545.0 161 CA Solano 2017 3850 91.7 1775.0 237 CA Del Norte 2019 117 48.9 2947.0 139 CA Modoc 2017 77 106.0 2173.0 177 CA Colusa 2018 118 53.6 545.0 251 CA Mariposa 2019 63 37.1 1371.0 229 CA Yuba 2018 333 43.0 782.0 159 CA Shasta 2017 722 45.3 3005.0 231 CA Alameda 2019 7448 45.8 3085.0 272 CA Santa Clara 2019 4655 23.9 1737.0 274 CA Shasta 2019 632 39.8 3005.0 207 CA San Bernardino 2018 10343 47.4 2590.0 267 CA San Francisco 2019 2673 33.2 2816.0 1 CA California 2015 191904 50.4 null 39 CA San Joaquin 2015 4802 66.2 2664.0 104 CA Solano 2016 3349 80.8 1775.0 179 CA Del Norte 2018 132 53.6 2947.0 250 CA Marin 2019 540 22.6 2492.0 266 CA San Diego 2019 9873 29.8 2343.0 94 CA San Diego 2016 10068 30.9 2343.0 270 CA San Mateo 2019 1987 25.9 822.0 210 CA San Joaquin 2018 4527 60.5 2664.0 114 CA Yuba 2016 297 39.2 782.0 121 CA Contra Costa 2017 6706 62.6 46.0 205 CA Sacramento 2018 9656 64.5 536.0 239 CA Fresno 2019 6592 63.1 2778.0 166 CA Trinity 2017 55 50.1 2966.0 34 CA Sacramento 2015 10109 69.2 536.0 37 CA San Diego 2015 11646 37.0 2343.0 25 CA Modoc 2015 53 67.9 2173.0 36 CA San Bernardino 2015 12761 59.3 2590.0 225 CA Tulare 2018 1600 32.2 1720.0 41 CA San Mateo 2015 2695 36.4 822.0 220 CA Sonoma 2018 1770 38.0 862.0 149 CA San Benito 2017 340 61.2 2508.0 216 CA Shasta 2018 608 38.6 3005.0 193 CA Mariposa 2018 68 48.0 1371.0 284 CA Ventura 2019 2413 29.8 1406.0 4 CA Butte 2015 1044 50.2 1

AsthmaID STATE COUNTY YEAR NUMBER OF ED VISITS AGE-ADJUSTED ED VISIT RATE COUNTY_ID 147 CA Riverside 2017 10076 43.2 586.0 170 CA Yolo 2017 894 43.3 1994.0 184 CA Imperial 2018 1147 58.1 1113.0 160 CA Siskiyou 2017 159 42.1 534.0 169 CA Ventura 2017 2836 34.8 1406.0 8 CA Del Norte 2015 140 53.0 2947.0 67 CA Fresno 2016 6930 67.4 2778.0 70 CA Imperial 2016 1287 66.3 1113.0 168 CA Tuolumne 2017 244 53.6 1144.0 69 CA Humboldt 2016 815 64.5 224.0 206 CA San Benito 2018 318 56.7 2508.0 7 CA Contra Costa 2015 6858 65.2 46.0 249 CA Madera 2019 781 49.1 2633.0 142 CA Napa 2017 537 40.2 1252.0 191 CA Madera 2018 813 50.9 2633.0 112 CA Ventura 2016 2619 32.4 1406.0 154 CA San Luis Obispo 2017 800 33.3 2457.0 232 CA Amador 2019 169 53.2 843.0 124 CA Fresno 2017 7783 75.4 2778.0 253 CA Merced 2019 1690 59.4 318.0 128 CA Inyo 2017 110 70.7 1797.0 201 CA Orange 2018 8183 26.5 2491.0 235 CA Colusa 2019 103 45.4 545.0 108 CA Tehama 2016 335 55.9 1971.0 180 CA El Dorado 2018 564 34.1 1751.0 255 CA Mono 2019 51 46.5 3048.0 271 CA Santa Barbara 2019 1228 27.8 1796.0 234 CA Calaveras 2019 199 58.4 65.0 133 CA Los Angeles 2017 49504 50.0 3118.0 181 CA Fresno 2018 6935 67.0 2778.0 88 CA Placer 2016 968 28.3 605.0 280 CA Tehama 2019 274 47.0 1971.0 49 CA Stanislaus 2015 3281 60.7 809.0 286 CA Yuba 2019 328 42.3 782.0 155 CA San Mateo 2017 2346 31.8 822.0 214 CA Santa Clara 2018 5095 26.4 1737.0 101 CA Santa Cruz 2016 864 34.4 222.0 217 CA Sierra 2018 12 52.5 2547.0 98 CA San Mateo 2016 2382 32.5 822.0 116 CA Alameda 2017 8942 56.3 3085.0 167 CA Tulare 2017 2134 43.4 1720.0 238 CA El Dorado 2019 539 33.7 1751.0 29 CA Nevada 2015 351 42.8 134.0 107 CA Sutter 2016 324 33.7 2929.0 182 CA Glenn 2018 101 35.9 2490.0 268 CA San Joaquin 2019 4390 57.9 2664.0 64 CA Contra Costa 2016 6021 56.8 46.0 75 CA Lassen 2016 118 40.7 29.0 47 CA Solano 2015 3415 83.2 1775.0 279 CA Sutter 2019 274 27.8 2929.0 42 CA Santa Barbara 2015 1734 40.7 1796.0 144 CA Orange 2017 9084 29.7 2491.0 215 CA Santa Cruz 2018 725 27.9 222.0 44 CA Santa Cruz 2015 910 36.5 222.0 236 CA Contra Costa 2019 5910 54.2 46.0 35 CA San Benito 2015 285 50.1 2508.0 62 CA Calaveras 2016 171 45.3 65.0 96 CA San Joaquin 2016 4245 57.5 2664.0 219 CA Solano 2018 3354 79.6 1775.0 151 CA San Diego 2017 10339 31.7 2343.0 18 CA Lassen 2015 148 45.3 29.0 258 CA Nevada 2019 218 27.2 134.0 275 CA Siskiyou 2019 148 40.4 534.0 80 CA Mendocino 2016 451 56.4 568.0 86 CA Nevada 2016 267 33.6 134.0 171 CA Yuba 2017 366 47.9 782.0 178 CA Contra Costa 2018 6001 55.4 46.0 218 CA Siskiyou 2018 138 34.1 534.0 120 CA Colusa 2017 62 28.4 545.0 161 CA Solano 2017 3850 91.7 1775.0 237 CA Del Norte 2019 117 48.9 2947.0 139 CA Modoc 2017 77 106.0 2173.0 177 CA Colusa 2018 118 53.6 545.0 251 CA Mariposa 2019 63 37.1 1371.0 229 CA Yuba 2018 333 43.0 782.0 159 CA Shasta 2017 722 45.3 3005.0 231 CA Alameda 2019 7448 45.8 3085.0 272 CA Santa Clara 2019 4655 23.9 1737.0 274 CA Shasta 2019 632 39.8 3005.0 207 CA San Bernardino 2018 10343 47.4 2590.0 267 CA San Francisco 2019 2673 33.2 2816.0 1 CA California 2015 191904 50.4 null 39 CA San Joaquin 2015 4802 66.2 2664.0 104 CA Solano 2016 3349 80.8 1775.0 179 CA Del Norte 2018 132 53.6 2947.0 250 CA Marin 2019 540 22.6 2492.0 266 CA San Diego 2019 9873 29.8 2343.0 94 CA San Diego 2016 10068 30.9 2343.0 270 CA San Mateo 2019 1987 25.9 822.0 210 CA San Joaquin 2018 4527 60.5 2664.0 114 CA Yuba 2016 297 39.2 782.0 121 CA Contra Costa 2017 6706 62.6 46.0 205 CA Sacramento 2018 9656 64.5 536.0 239 CA Fresno 2019 6592 63.1 2778.0 166 CA Trinity 2017 55 50.1 2966.0 34 CA Sacramento 2015 10109 69.2 536.0 37 CA San Diego 2015 11646 37.0 2343.0 25 CA Modoc 2015 53 67.9 2173.0 36 CA San Bernardino 2015 12761 59.3 2590.0 225 CA Tulare 2018 1600 32.2 1720.0 41 CA San Mateo 2015 2695 36.4 822.0 220 CA Sonoma 2018 1770 38.0 862.0 149 CA San Benito 2017 340 61.2 2508.0 216 CA Shasta 2018 608 38.6 3005.0 193 CA Mariposa 2018 68 48.0 1371.0 284 CA Ventura 2019 2413 29.8 1406.0 4 CA Butte 2015 1044 50.2 1

In [0]:
# If there was a missing county, we need to add it to the database
if noMatchFound:
    missingCountyAsthmaDF = asthmaTotalDF.filter((asthmaTotalDF.COUNTY.isNull()))
   
    display(missingCountyAsthmaDF)

    missingStates = pd.DataFrame()
    missingCounties = pd.DataFrame()
    for countyAsthma in missingCountyAsthmaDF.toLocalIterator():
        # We need to check to see if this is the statewide row. All others, add them to the county table. 
        if countyAsthma.COUNTY == 'California': continue
        else:
            # Check if state already exists
            if(stateDF.filter(stateDF.STATE_ABBR == countyAsthma.STATE).count() == 0):
                # If not, add it to a list of missing states
                missingStates.append({'STATE_ABBR': countyAsthma.STATE, 
                                      'STATE_NAME': "California"}, # Need to get a full name for general use
                                     ignore_index=True)      
            # Add to the list of missing counties
            missingCounties.append({'COUNTY_NAME': countyAsthma.COUNTY,
                                   'STATE': countyAsthma.STATE},
                                   ignore_index=True)
                                      
    # If we were missing states, add them to the DB                                  
    if(len(missingStates) > 0):       
        statesSchema = StructType([ \
            StructField("STATE_ABBR",StringType(),True), \
            StructField("STATE_NAME",StringType(),True)]) 
        newStatesDF = spark.createDataFrame(missingStates,schema)
        # Save and reload to get the latest ID numbers
        # Put in a try statement in case the state already exists
        try:
            writer = newStatesDF.write.format("jdbc").option("url", url) \
                .mode("append") \
                .option("dbtable", 'State') \
                .option("user", user) \
                .option("password", password) \
                .option("driver", "com.microsoft.sqlserver.jdbc.SQLServerDriver")
            writer.save()
        except Exception as e:
            print(e)

        stateDF = spark.read.format("jdbc") \
            .option("url", url) \
            .option("dbtable", "State") \
            .option("user", user) \
            .option("password", password) \
            .option("driver", "com.microsoft.sqlserver.jdbc.SQLServerDriver") \
            .load()
        display(stateDF)    
        
    if(len(missingCounties) > 0):   
        # Get the state ID and add to the dataframe
        missingCounties = spark.createDataFrame(missingCounties)
        newcountyDF = missingCounties.withColumn('STATE_ID', lit(stateDF.filter((stateDF.STATE_ABBR == missingCounties.STATE)).first()['STATE_ID']))
        # Append and reload to get the latest ID numbers
        try:
            writer = newcountyDF.write.format("jdbc").option("url", url) \
                .mode("append") \
                .option("dbtable", 'County') \
                .option("user", user) \
                .option("password", password) \
                .option("driver", "com.microsoft.sqlserver.jdbc.SQLServerDriver")
            writer.save()
        except Exception as e:
            print(e)

        countyDF = spark.read.format("jdbc") \
            .option("url", url) \
            .option("dbtable", "County") \
            .option("user", user) \
            .option("password", password) \
            .option("driver", "com.microsoft.sqlserver.jdbc.SQLServerDriver") \
            .load()
        display(countyDF)

        # Get the new combined county state dataframe
        countyStateDF = countyDF.join(stateDF, on='STATE_ID', how='inner')
        display(countyStateDF)           
            
        # Redo the step of finding the county matches in the asthma dataframe
        matched = pd.DataFrame([])
        for countyAsthma in asthmaTotalDFjoined.toLocalIterator():
            matchedCol = countyStateDF.filter((countyStateDF.COUNTY_NAME == countyAsthma.COUNTY) & (countyStateDF.STATE_ABBR == countyAsthma.STATE)).select('COUNTY_ID')  
            # There are conditions where there isn't a match still like if the we have statewide data.
            if(matchedCol.count() >0):
                matched = matched.append({'AsthmaID': countyAsthma.AsthmaID, 
                                          'COUNTY_ID': matchedCol.collect()[0][0]},
                                         ignore_index=True)
        if(len(matched) > 0):
            matched = spark.createDataFrame(matched)
            display(matched)
            # if everything went ok, then join the matched tabled of county ID's to the asthma dataframe
            # Since we ran this once already to find the missing columns, there may already be a COUNTY_ID column. If so remove it
            try:
                asthmaTotalDFjoined = asthmaTotalDFjoined.drop('COUNTY_ID')
            except Exception as e:
                print(e)
            asthmaTotalDFjoined = asthmaTotalDFjoined.join(matched, on='AsthmaID', how='left_outer')
            display(asthmaTotalDFjoined)
        else:
            print("NOTHING MATCHED")
 
            
    

AsthmaID STATE COUNTY YEAR NUMBER OF ED VISITS AGE-ADJUSTED ED VISIT RATE COUNTY_ID

Since we merged in the COUNTY_ID, there is no need for the STATE and COUNTY columns

In [0]:
asthmaTotalDF = asthmaTotalDF.drop('STATE', 'COUNTY')
display(asthmaTotalDF)

AsthmaID YEAR NUMBER OF ED VISITS AGE-ADJUSTED ED VISIT RATE COUNTY_ID 147 2017 10076 43.2 586.0 170 2017 894 43.3 1994.0 184 2018 1147 58.1 1113.0 160 2017 159 42.1 534.0 169 2017 2836 34.8 1406.0 8 2015 140 53.0 2947.0 67 2016 6930 67.4 2778.0 70 2016 1287 66.3 1113.0 168 2017 244 53.6 1144.0 69 2016 815 64.5 224.0 206 2018 318 56.7 2508.0 7 2015 6858 65.2 46.0 249 2019 781 49.1 2633.0 142 2017 537 40.2 1252.0 191 2018 813 50.9 2633.0 112 2016 2619 32.4 1406.0 154 2017 800 33.3 2457.0 232 2019 169 53.2 843.0 124 2017 7783 75.4 2778.0 253 2019 1690 59.4 318.0 128 2017 110 70.7 1797.0 201 2018 8183 26.5 2491.0 235 2019 103 45.4 545.0 108 2016 335 55.9 1971.0 180 2018 564 34.1 1751.0 255 2019 51 46.5 3048.0 271 2019 1228 27.8 1796.0 234 2019 199 58.4 65.0 133 2017 49504 50.0 3118.0 181 2018 6935 67.0 2778.0 88 2016 968 28.3 605.0 280 2019 274 47.0 1971.0 49 2015 3281 60.7 809.0 286 2019 328 42.3 782.0 155 2017 2346 31.8 822.0 214 2018 5095 26.4 1737.0 101 2016 864 34.4 222.0 217 2018 12 52.5 2547.0 98 2016 2382 32.5 822.0 116 2017 8942 56.3 3085.0 167 2017 2134 43.4 1720.0 238 2019 539 33.7 1751.0 29 2015 351 42.8 134.0 107 2016 324 33.7 2929.0 182 2018 101 35.9 2490.0 268 2019 4390 57.9 2664.0 64 2016 6021 56.8 46.0 75 2016 118 40.7 29.0 47 2015 3415 83.2 1775.0 279 2019 274 27.8 2929.0 42 2015 1734 40.7 1796.0 144 2017 9084 29.7 2491.0 215 2018 725 27.9 222.0 44 2015 910 36.5 222.0 236 2019 5910 54.2 46.0 35 2015 285 50.1 2508.0 62 2016 171 45.3 65.0 96 2016 4245 57.5 2664.0 219 2018 3354 79.6 1775.0 151 2017 10339 31.7 2343.0 18 2015 148 45.3 29.0 258 2019 218 27.2 134.0 275 2019 148 40.4 534.0 80 2016 451 56.4 568.0 86 2016 267 33.6 134.0 171 2017 366 47.9 782.0 178 2018 6001 55.4 46.0 218 2018 138 34.1 534.0 120 2017 62 28.4 545.0 161 2017 3850 91.7 1775.0 237 2019 117 48.9 2947.0 139 2017 77 106.0 2173.0 177 2018 118 53.6 545.0 251 2019 63 37.1 1371.0 229 2018 333 43.0 782.0 159 2017 722 45.3 3005.0 231 2019 7448 45.8 3085.0 272 2019 4655 23.9 1737.0 274 2019 632 39.8 3005.0 207 2018 10343 47.4 2590.0 267 2019 2673 33.2 2816.0 1 2015 191904 50.4 null 39 2015 4802 66.2 2664.0 104 2016 3349 80.8 1775.0 179 2018 132 53.6 2947.0 250 2019 540 22.6 2492.0 266 2019 9873 29.8 2343.0 94 2016 10068 30.9 2343.0 270 2019 1987 25.9 822.0 210 2018 4527 60.5 2664.0 114 2016 297 39.2 782.0 121 2017 6706 62.6 46.0 205 2018 9656 64.5 536.0 239 2019 6592 63.1 2778.0 166 2017 55 50.1 2966.0 34 2015 10109 69.2 536.0 37 2015 11646 37.0 2343.0 25 2015 53 67.9 2173.0 36 2015 12761 59.3 2590.0 225 2018 1600 32.2 1720.0 41 2015 2695 36.4 822.0 220 2018 1770 38.0 862.0 149 2017 340 61.2 2508.0 216 2018 608 38.6 3005.0 193 2018 68 48.0 1371.0 284 2019 2413 29.8 1406.0 4 2015 1044 50.2 152.0 204 2018 8935 37.9 586.0 137 2017 567 70.9 568.0 245 2019 753 47.9 1973.0 246 2019 510 89.8 603.0 212 2018 2051 27.5 822.0 85 2016 439 33.5 1252.0 122 2017 150 61.2 2947.0 145 2017 1193 34.7 605.0 165 2017 350 59.7 1971.0 197 2018 65 54.9 3048.0 23 2015 479 57.4 568.0 252 2019 489 60.0 568.0 77 2016 956 60.2 2633.0 140 2017 40 32.0 3048.0 199 2018 511 37.4 1252.0 282 2019 1996 40.2 1720.0 50 2015 337 34.1 2929.0 56 2015 852 44.1 1994.0 78 2016 543 23.1 2492.0 123 2017 650 40.5 1751.0 242 2019 1198 60.2 1113.0 248 2019 46804 47.1 3118.0 285 2019 743 34.5 1994.0 79 2016 66 45.3 1371.0 113 2016 774 38.4 1994.0 213 2018 1213 27.5 1796.0 259 2019 8321 26.9 2491.0 45 2015 1015 60.5 3005.0 83 2016 33 28.1 3048.0 129 2017 4853 52.2 1697.0 134 2017 979 61.7 2633.0 118 2017 936 45.3 152.0 71 2016 90 53.7 1797.0 186 2018 4299 46.2 1697.0 143 2017 306 38.5 134.0 156 2017 1471 33.5 1796.0 173 2018 7795 48.6 3085.0 93 2016 11335 51.9 2590.0 241 2019 614 48.0 224.0 31 2015 1125 31.4 605.0 132 2017 131 44.0 29.0 162 2017 1938 41.6 862.0 281 2019 48 43.0 2966.0 146 2017 86 63.2 1349.0 164 2017 301 31.7 2929.0 230 2019 165449 42.6 null 11 2015 122 42.6 2490.0 103 2016 128 33.7 534.0 58 2016 174733 45.8 null 106 2016 2763 51.3 809.0 264 2019 341 60.6 2508.0 21 2015 541 22.2 2492.0 

### 6. Create the metric, method, and unit tables and link to the air quality dataset. Link  the County Table , too.

In [0]:
# Add in an ID to the table 
AQIDFAgg2 = AQIDFAgg2.withColumn('AQ_ID',F.monotonically_increasing_id()+1)
print(AQIDFAgg2.printSchema())
display(AQIDFAgg2)

root
-- state: string (nullable = false)
-- county: string (nullable = true)
-- year: long (nullable = true)
-- LEAD_MEAN: double (nullable = true)
-- LEAD_1STMAX: double (nullable = true)
-- LEAD_99PERC: double (nullable = true)
-- LEAD_STD: double (nullable = true)
-- LEAD_2NDMAX: double (nullable = true)
-- LEAD_METHOD: string (nullable = true)
-- LEAD_METRIC: string (nullable = true)
-- LEAD_UNITS: string (nullable = true)
-- NO2_MEAN: double (nullable = true)
-- NO2_1STMAX: double (nullable = true)
-- NO2_99PERC: double (nullable = true)
-- NO2_STD: double (nullable = true)
-- NO2_2NDMAX: double (nullable = true)
-- NO2_METHOD: string (nullable = true)
-- NO2_METRIC: string (nullable = true)
-- NO2_UNITS: string (nullable = true)
-- OZONE_MEAN: double (nullable = true)
-- OZONE_1STMAX: double (nullable = true)
-- OZONE_99PERC: double (nullable = true)
-- OZONE_STD: double (nullable = true)
-- OZONE_2NDMAX: double (nullable = true)
-- OZONE_METHOD: string (nullable = true)
-- OZONE_METRIC: string (nullable = true)
-- OZONE_UNITS: string (nullable = true)
-- PM10_MEAN: double (nullable = true)
-- PM10_1STMAX: double (nullable = true)
-- PM10_99PERC: double (nullable = true)
-- PM10_STD: double (nullable = true)
-- PM10_2NDMAX: double (nullable = true)
-- PM10_METHOD: string (nullable = true)
-- PM10_METRIC: string (nullable = true)
-- PM10_UNITS: string (nullable = true)
-- PM25_MEAN: double (nullable = true)
-- PM25_1STMAX: double (nullable = true)
-- PM25_99PERC: double (nullable = true)
-- PM25_STD: double (nullable = true)
-- PM25_2NDMAX: double (nullable = true)
-- PM25_METHOD: string (nullable = true)
-- PM25_METRIC: string (nullable = true)
-- PM25_UNITS: string (nullable = true)
-- SO2_MEAN: double (nullable = true)
-- SO2_1STMAX: double (nullable = true)
-- SO2_99PERC: double (nullable = true)
-- SO2_STD: double (nullable = true)
-- SO2_2NDMAX: double (nullable = true)
-- SO2_METHOD: string (nullable = true)
-- SO2_METRIC: string (nullable = true)
-- SO2_UNITS: string (nullable = true)
-- AQ_ID: long (nullable = false)

None

state county year LEAD_MEAN LEAD_1STMAX LEAD_99PERC LEAD_STD LEAD_2NDMAX LEAD_METHOD LEAD_METRIC LEAD_UNITS NO2_MEAN NO2_1STMAX NO2_99PERC NO2_STD NO2_2NDMAX NO2_METHOD NO2_METRIC NO2_UNITS OZONE_MEAN OZONE_1STMAX OZONE_99PERC OZONE_STD OZONE_2NDMAX OZONE_METHOD OZONE_METRIC OZONE_UNITS PM10_MEAN PM10_1STMAX PM10_99PERC PM10_STD PM10_2NDMAX PM10_METHOD PM10_METRIC PM10_UNITS PM25_MEAN PM25_1STMAX PM25_99PERC PM25_STD PM25_2NDMAX PM25_METHOD PM25_METRIC PM25_UNITS SO2_MEAN SO2_1STMAX SO2_99PERC SO2_STD SO2_2NDMAX SO2_METHOD SO2_METRIC SO2_UNITS AQ_ID CA Alameda 2015 null null null null null null null null 20.1278364 49.22 41.7 9.059481 45.279999999999994 INSTRUMENTAL - CHEMILUMINESCENCE Daily Maximum 1-hour average Parts per billion 0.0409086 0.0984 0.08620000000000001 0.0122206 0.092 INSTRUMENTAL - ULTRA VIOLET Daily maxima of observed hourly values (between 9:00 AM and 8:00 PM) Parts per million null null null null null null null null null null null null null null null null null null null null null null null null 1 CA Alameda 2016 null null null null null null null null 19.29764116666667 46.116666666666674 37.73333333333333 7.934909333333333 39.199999999999996 INSTRUMENTAL - CHEMILUMINESCENCE Daily Maximum 1-hour average Parts per billion 0.03733583333333334 0.08216666666666667 0.074 0.011103 0.07816666666666666 INSTRUMENTAL - ULTRA VIOLET Daily maxima of observed hourly values (between 9:00 AM and 8:00 PM) Parts per million null null null null null null null null null null null null null null null null null null null null null null null null 2 CA Alameda 2017 null null null null null null null null 20.515038 61.19999999999999 44.43333333333334 9.129422 49.883333333333326 INSTRUMENTAL - CHEMILUMINESCENCE Daily Maximum 1-hour average Parts per billion 0.038411 0.09766666666666667 0.07100000000000001 0.010734666666666665 0.08733333333333333 INSTRUMENTAL - ULTRA VIOLET Daily maxima of observed hourly values (between 9:00 AM and 8:00 PM) Parts per million null null null null null null null null null null null null null null null null null null null null null null null null 3 CA Alameda 2018 null null null null null null null null 22.827882166666665 69.06666666666666 59.199999999999996 10.554471166666668 65.26666666666667 INSTRUMENTAL - CHEMILUMINESCENCE Daily Maximum 1-hour average Parts per billion 0.036052799999999996 0.07139999999999999 0.0612 0.0095216 0.06739999999999999 INSTRUMENTAL - ULTRA VIOLET Daily maxima of observed hourly values (between 9:00 AM and 8:00 PM) Parts per million null null null null null null null null null null null null null null null null null null null null null null null null 4 CA Alameda 2019 null null null null null null null null 21.414331500000003 55.18333333333334 45.63333333333333 9.367031333333331 50.48333333333334 INSTRUMENTAL - CHEMILUMINESCENCE Daily Maximum 1-hour average Parts per billion 0.0366726 0.0914 0.06799999999999999 0.0104352 0.08499999999999999 INSTRUMENTAL - ULTRA VIOLET Daily maxima of observed hourly values (between 9:00 AM and 8:00 PM) Parts per million null null null null null null null null null null null null null null null null null null null null null null null null 5 CA Amador 2015 null null null null null null null null null null null null null null null null 0.048449 0.103 0.088 0.015178 0.094 INSTRUMENTAL - ULTRA VIOLET ABSORPTION Daily maxima of observed hourly values (between 9:00 AM and 8:00 PM) Parts per million null null null null null null null null null null null null null null null null null null null null null null null null 6 CA Amador 2016 null null null null null null null null null null null null null null null null 0.047055 0.104 0.081 0.014501 0.084 INSTRUMENTAL - ULTRA VIOLET ABSORPTION Daily maxima of observed hourly values (between 9:00 AM and 8:00 PM) Parts per million null null null null null null null null null null null null null null null null null null null null null null null null 7 CA Amador 2017 null null null null null null null null nul

Method

In [0]:
# Get the unique methods across all method columns in the airquality dataframe
methodsDF = AQIDFAgg2.select('LEAD_METHOD').distinct()
methodsDF = methodsDF.withColumnRenamed("LEAD_METHOD","METHOD_NAME")
methodsDF2 = AQIDFAgg2.select('NO2_METHOD').distinct()
methodsDF2 = methodsDF2.withColumnRenamed("NO2_METHOD","METHOD_NAME")
methodsDF = methodsDF2.union(methodsDF)

methodsDF2 = AQIDFAgg2.select('OZONE_METHOD').distinct()
methodsDF2 = methodsDF2.withColumnRenamed("OZONE_METHOD","METHOD_NAME")
methodsDF = methodsDF2.union(methodsDF)

methodsDF2 = AQIDFAgg2.select('PM10_METHOD').distinct()
methodsDF2 = methodsDF2.withColumnRenamed("PM10_METHOD","METHOD_NAME")
methodsDF = methodsDF2.union(methodsDF)

methodsDF2 = AQIDFAgg2.select('PM25_METHOD').distinct()
methodsDF2 = methodsDF2.withColumnRenamed("PM25_METHOD","METHOD_NAME")
methodsDF = methodsDF2.union(methodsDF)

methodsDF2 = AQIDFAgg2.select('SO2_METHOD').distinct()
methodsDF2 = methodsDF2.withColumnRenamed("SO2_METHOD","METHOD_NAME")
methodsDF = methodsDF2.union(methodsDF)

methodsDF = methodsDF.select('METHOD_NAME').distinct()
display(methodsDF)

METHOD_NAME INSTRUMENTAL - Pulsed Fluorescent 43C-TLE/43i-TLE null Andersen RAAS2.5-300 PM2.5 SEQ w/WINS - GRAVIMETRIC Multiple Methods Used R & P Model 2025 PM-2.5 Sequential Air Sampler w/VSCC - Gravimetric INSTRUMENTAL - ULTRA VIOLET ABSORPTION INSTRUMENTAL - ULTRA VIOLET INSTRUMENTAL - CHEMILUMINESCENCE INSTRUMENTAL - GAS PHASE CHEMILUMINESCENCE Hi-Vol - ICAP SPECTRA (ICP-MS); 0.45M HNO3 Boil30 min

In [0]:
try:
    writer = methodsDF.write.format("jdbc").option("url", url) \
        .mode("append") \
        .option("dbtable", 'Method') \
        .option("user", user) \
        .option("password", password) \
        .option("driver", "com.microsoft.sqlserver.jdbc.SQLServerDriver")
    writer.save()
except Exception as e:
    print(e)

    df_loaded = spark.read.format("jdbc") \
        .option("url", url) \
        .option("dbtable", "Method") \
        .option("user", user) \
        .option("password", password) \
        .option("driver", "com.microsoft.sqlserver.jdbc.SQLServerDriver") \
        .load()
    display(df_loaded)   
        
    # Subtract the two to only leave what is not in the database
    # remove the index column of the loaded dataframe
    df_loaded = df_loaded.drop('METHOD_ID')
    df_toload = methodsDF.subtract(df_loaded)
    display(df_toload)
    
    # Upload all the data that wasn't already in the database
    df_toload.write.format("jdbc")  \
        .option("url", url) \
        .mode("append") \
        .option("dbtable", "Method") \
        .option("user", user) \
        .option("password", password) \
        .option("driver", "com.microsoft.sqlserver.jdbc.SQLServerDriver") \
        .save()
    
methodsDF = spark.read.format("jdbc") \
    .option("url", url) \
    .option("dbtable", "Method") \
    .option("user", user) \
    .option("password", password) \
    .option("driver", "com.microsoft.sqlserver.jdbc.SQLServerDriver") \
    .load()
display(methodsDF)  


An error occurred while calling o6347.save.
: org.apache.spark.SparkException: Job aborted due to stage failure: Task 0 in stage 99287.0 failed 4 times, most recent failure: Lost task 0.3 in stage 99287.0 (TID 79538) (10.139.64.5 executor driver): java.sql.BatchUpdateException: Violation of UNIQUE KEY constraint 'uq_Method_MethodName'. Cannot insert duplicate key in object 'dbo.Method'. The duplicate key value is (INSTRUMENTAL - Pulsed Fluorescent 43C-TLE/43i-TLE).
	at com.microsoft.sqlserver.jdbc.SQLServerPreparedStatement.executeBatch(SQLServerPreparedStatement.java:2085)
	at org.apache.spark.sql.execution.datasources.jdbc.JdbcUtils$.savePartition(JdbcUtils.scala:731)
	at org.apache.spark.sql.execution.datasources.jdbc.JdbcUtils$.$anonfun$saveTable$1(JdbcUtils.scala:888)
	at org.apache.spark.sql.execution.datasources.jdbc.JdbcUtils$.$anonfun$saveTable$1$adapted(JdbcUtils.scala:886)
	at org.apache.spark.rdd.RDD.$anonfun$foreachPartition$2(RDD.scala:1025)
	at org.apache.spark.rdd.RDD.$anonfun$foreachPartition$2$adapted(RDD.scala:1025)
	at org.apache.spark.SparkContext.$anonfun$runJob$2(SparkContext.scala:2576)
	at org.apache.spark.scheduler.ResultTask.$anonfun$runTask$3(ResultTask.scala:75)
	at com.databricks.spark.util.ExecutorFrameProfiler$.record(ExecutorFrameProfiler.scala:110)
	at org.apache.spark.scheduler.ResultTask.$anonfun$runTask$1(ResultTask.scala:75)
	at com.databricks.spark.util.ExecutorFrameProfiler$.record(ExecutorFrameProfiler.scala:110)
	at org.apache.spark.scheduler.ResultTask.runTask(ResultTask.scala:55)
	at org.apache.spark.scheduler.Task.doRunTask(Task.scala:153)
	at org.apache.spark.scheduler.Task.$anonfun$run$1(Task.scala:122)
	at com.databricks.spark.util.ExecutorFrameProfiler$.record(ExecutorFrameProfiler.scala:110)
	at org.apache.spark.scheduler.Task.run(Task.scala:93)
	at org.apache.spark.executor.Executor$TaskRunner.$anonfun$run$13(Executor.scala:824)
	at org.apache.spark.util.Utils$.tryWithSafeFinally(Utils.scala:1621)
	at org.apache.spark.executor.Executor$TaskRunner.$anonfun$run$4(Executor.scala:827)
	at scala.runtime.java8.JFunction0$mcV$sp.apply(JFunction0$mcV$sp.java:23)
	at com.databricks.spark.util.ExecutorFrameProfiler$.record(ExecutorFrameProfiler.scala:110)
	at org.apache.spark.executor.Executor$TaskRunner.run(Executor.scala:683)
	at java.util.concurrent.ThreadPoolExecutor.runWorker(ThreadPoolExecutor.java:1149)
	at java.util.concurrent.ThreadPoolExecutor$Worker.run(ThreadPoolExecutor.java:624)
	at java.lang.Thread.run(Thread.java:748)

Driver stacktrace:
	at org.apache.spark.scheduler.DAGScheduler.failJobAndIndependentStages(DAGScheduler.scala:2973)
	at org.apache.spark.scheduler.DAGScheduler.$anonfun$abortStage$2(DAGScheduler.scala:2920)
	at org.apache.spark.scheduler.DAGScheduler.$anonfun$abortStage$2$adapted(DAGScheduler.scala:2914)
	at scala.collection.mutable.ResizableArray.foreach(ResizableArray.scala:62)
	at scala.collection.mutable.ResizableArray.foreach$(ResizableArray.scala:55)
	at scala.collection.mutable.ArrayBuffer.foreach(ArrayBuffer.scala:49)
	at org.apache.spark.scheduler.DAGScheduler.abortStage(DAGScheduler.scala:2914)
	at org.apache.spark.scheduler.DAGScheduler.$anonfun$handleTaskSetFailed$1(DAGScheduler.scala:1334)
	at org.apache.spark.scheduler.DAGScheduler.$anonfun$handleTaskSetFailed$1$adapted(DAGScheduler.scala:1334)
	at scala.Option.foreach(Option.scala:407)
	at org.apache.spark.scheduler.DAGScheduler.handleTaskSetFailed(DAGScheduler.scala:1334)
	at org.apache.spark.scheduler.DAGSchedulerEventProcessLoop.doOnReceive(DAGScheduler.scala:3182)
	at org.apache.spark.scheduler.DAGSchedulerEventProcessLoop.onReceive(DAGScheduler.scala:3123)
	at org.apache.spark.scheduler.DAGSchedulerEventProcessLoop.onReceive(DAGScheduler.scala:3111)
	at org.apache.spark.util.EventLoop$$anon$1.run(EventLoop.scala:49)
	at org.apache.spark.scheduler.DAGScheduler.runJob(DAGScheduler.scala:1096)
	at org.apache.spark.SparkContext.runJobInternal(SparkContext.scala:2536)
	at org.apache.spark.Sp

METHOD_ID METHOD_NAME 3 null 50 Andersen RAAS2.5-300 PM2.5 SEQ w/WINS - GRAVIMETRIC 2 Hi-Vol - ICAP SPECTRA (ICP-MS); 0.45M HNO3 Boil30 min 4 INSTRUMENTAL - CHEMILUMINESCENCE 5 INSTRUMENTAL - GAS PHASE CHEMILUMINESCENCE 9 INSTRUMENTAL - Pulsed Fluorescent 43C-TLE/43i-TLE 6 INSTRUMENTAL - ULTRA VIOLET 7 INSTRUMENTAL - ULTRA VIOLET ABSORPTION 1 Multiple Methods Used 8 R & P Model 2025 PM-2.5 Sequential Air Sampler w/VSCC - Gravimetric

METHOD_NAME

METHOD_ID METHOD_NAME 3 null 50 Andersen RAAS2.5-300 PM2.5 SEQ w/WINS - GRAVIMETRIC 2 Hi-Vol - ICAP SPECTRA (ICP-MS); 0.45M HNO3 Boil30 min 4 INSTRUMENTAL - CHEMILUMINESCENCE 5 INSTRUMENTAL - GAS PHASE CHEMILUMINESCENCE 9 INSTRUMENTAL - Pulsed Fluorescent 43C-TLE/43i-TLE 6 INSTRUMENTAL - ULTRA VIOLET 7 INSTRUMENTAL - ULTRA VIOLET ABSORPTION 1 Multiple Methods Used 8 R & P Model 2025 PM-2.5 Sequential Air Sampler w/VSCC - Gravimetric

In [0]:
if(methodsDF.count() > 0):
    lead_matched = pd.DataFrame([])    
    NO2_matched = pd.DataFrame([])
    ozone_matched = pd.DataFrame([])
    PM10_matched = pd.DataFrame([])
    PM25_matched = pd.DataFrame([])
    SO2_matched = pd.DataFrame([])

    # Loop through all the rows in the AQ dataframe and find the matching method in the methods dataframe
    for AQrow in AQIDFAgg2.toLocalIterator():
        if(AQrow.LEAD_METHOD == None): lead_matchedCol = methodsDF.filter((methodsDF.METHOD_NAME.isNull())).select('METHOD_ID')
        else: lead_matchedCol = methodsDF.filter((methodsDF.METHOD_NAME == AQrow.LEAD_METHOD)).select('METHOD_ID')  
        
        if(AQrow.NO2_METHOD == None): NO2_matchedCol = methodsDF.filter((methodsDF.METHOD_NAME.isNull())).select('METHOD_ID')
        else: NO2_matchedCol = methodsDF.filter((methodsDF.METHOD_NAME == AQrow.NO2_METHOD)).select('METHOD_ID')  
            
        if(AQrow.OZONE_METHOD == None): ozone_matchedCol = methodsDF.filter((methodsDF.METHOD_NAME.isNull())).select('METHOD_ID')
        else: ozone_matchedCol = methodsDF.filter((methodsDF.METHOD_NAME == AQrow.OZONE_METHOD)).select('METHOD_ID')  
            
        if(AQrow.PM10_METHOD == None): PM10_matchedCol = methodsDF.filter((methodsDF.METHOD_NAME.isNull())).select('METHOD_ID')
        else: PM10_matchedCol = methodsDF.filter((methodsDF.METHOD_NAME == AQrow.PM10_METHOD)).select('METHOD_ID')  
            
        if(AQrow.PM25_METHOD == None): PM25_matchedCol = methodsDF.filter((methodsDF.METHOD_NAME.isNull())).select('METHOD_ID')
        else: PM25_matchedCol = methodsDF.filter((methodsDF.METHOD_NAME == AQrow.PM25_METHOD)).select('METHOD_ID')  
            
        if(AQrow.SO2_METHOD == None): SO2_matchedCol = methodsDF.filter((methodsDF.METHOD_NAME.isNull())).select('METHOD_ID')
        else: SO2_matchedCol = methodsDF.filter((methodsDF.METHOD_NAME == AQrow.SO2_METHOD)).select('METHOD_ID')  

        if(lead_matchedCol.count() > 0): lead_matched = lead_matched.append({'AQ_ID': AQrow.AQ_ID, 'LEAD_METHOD_ID': lead_matchedCol.collect()[0][0]}, ignore_index=True)        
        if(NO2_matchedCol.count() > 0): NO2_matched = NO2_matched.append({'AQ_ID': AQrow.AQ_ID, 'NO2_METHOD_ID': NO2_matchedCol.collect()[0][0]}, ignore_index=True)
        if(ozone_matchedCol.count() > 0): ozone_matched = ozone_matched.append({'AQ_ID': AQrow.AQ_ID, 'OZONE_METHOD_ID': ozone_matchedCol.collect()[0][0]}, ignore_index=True)
        if(PM10_matchedCol.count() > 0): PM10_matched = PM10_matched.append({'AQ_ID': AQrow.AQ_ID, 'PM10_METHOD_ID': PM10_matchedCol.collect()[0][0]}, ignore_index=True)
        if(PM25_matchedCol.count() > 0): PM25_matched = PM25_matched.append({'AQ_ID': AQrow.AQ_ID, 'PM25_METHOD_ID': PM25_matchedCol.collect()[0][0]}, ignore_index=True)
        if(SO2_matchedCol.count() > 0): SO2_matched = SO2_matched.append({'AQ_ID': AQrow.AQ_ID, 'SO2_METHOD_ID': SO2_matchedCol.collect()[0][0]}, ignore_index=True)

                
    if(len(lead_matched) > 0): AQIDFAgg2 = AQIDFAgg2.join(spark.createDataFrame(lead_matched), on='AQ_ID', how='left_outer')
    if(len(NO2_matched) > 0): AQIDFAgg2 = AQIDFAgg2.join(spark.createDataFrame(NO2_matched), on='AQ_ID', how='left_outer')
    if(len(ozone_matched) > 0): AQIDFAgg2 = AQIDFAgg2.join(spark.createDataFrame(ozone_matched), on='AQ_ID', how='left_outer')
    if(len(PM10_matched) > 0): AQIDFAgg2 = AQIDFAgg2.join(spark.createDataFrame(PM10_matched), on='AQ_ID', how='left_outer')
    if(len(PM25_matched) > 0): AQIDFAgg2 = AQIDFAgg2.join(spark.createDataFrame(PM25_matched), on='AQ_ID', how='left_outer')
    if(len(SO2_matched) > 0): AQIDFAgg2 = AQIDFAgg2.join(spark.createDataFrame(SO2_matched), on='AQ_ID', how='left_outer')
   

    display(AQIDFAgg2)


AQ_ID state county year LEAD_MEAN LEAD_1STMAX LEAD_99PERC LEAD_STD LEAD_2NDMAX LEAD_METHOD LEAD_METRIC LEAD_UNITS NO2_MEAN NO2_1STMAX NO2_99PERC NO2_STD NO2_2NDMAX NO2_METHOD NO2_METRIC NO2_UNITS OZONE_MEAN OZONE_1STMAX OZONE_99PERC OZONE_STD OZONE_2NDMAX OZONE_METHOD OZONE_METRIC OZONE_UNITS PM10_MEAN PM10_1STMAX PM10_99PERC PM10_STD PM10_2NDMAX PM10_METHOD PM10_METRIC PM10_UNITS PM25_MEAN PM25_1STMAX PM25_99PERC PM25_STD PM25_2NDMAX PM25_METHOD PM25_METRIC PM25_UNITS SO2_MEAN SO2_1STMAX SO2_99PERC SO2_STD SO2_2NDMAX SO2_METHOD SO2_METRIC SO2_UNITS LEAD_METHOD_ID NO2_METHOD_ID OZONE_METHOD_ID PM10_METHOD_ID PM25_METHOD_ID SO2_METHOD_ID 1 CA Alameda 2015 null null null null null null null null 20.1278364 49.22 41.7 9.059481 45.279999999999994 INSTRUMENTAL - CHEMILUMINESCENCE Daily Maximum 1-hour average Parts per billion 0.0409086 0.0984 0.08620000000000001 0.0122206 0.092 INSTRUMENTAL - ULTRA VIOLET Daily maxima of observed hourly values (between 9:00 AM and 8:00 PM) Parts per million null null null null null null null null null null null null null null null null null null null null null null null null 3.0 4.0 6.0 3.0 3.0 3.0 2 CA Alameda 2016 null null null null null null null null 19.29764116666667 46.116666666666674 37.73333333333333 7.934909333333333 39.199999999999996 INSTRUMENTAL - CHEMILUMINESCENCE Daily Maximum 1-hour average Parts per billion 0.03733583333333334 0.08216666666666667 0.074 0.011103 0.07816666666666666 INSTRUMENTAL - ULTRA VIOLET Daily maxima of observed hourly values (between 9:00 AM and 8:00 PM) Parts per million null null null null null null null null null null null null null null null null null null null null null null null null 3.0 4.0 6.0 3.0 3.0 3.0 3 CA Alameda 2017 null null null null null null null null 20.515038 61.19999999999999 44.43333333333334 9.129422 49.883333333333326 INSTRUMENTAL - CHEMILUMINESCENCE Daily Maximum 1-hour average Parts per billion 0.038411 0.09766666666666667 0.07100000000000001 0.010734666666666665 0.08733333333333333 INSTRUMENTAL - ULTRA VIOLET Daily maxima of observed hourly values (between 9:00 AM and 8:00 PM) Parts per million null null null null null null null null null null null null null null null null null null null null null null null null 3.0 4.0 6.0 3.0 3.0 3.0 4 CA Alameda 2018 null null null null null null null null 22.827882166666665 69.06666666666666 59.199999999999996 10.554471166666668 65.26666666666667 INSTRUMENTAL - CHEMILUMINESCENCE Daily Maximum 1-hour average Parts per billion 0.036052799999999996 0.07139999999999999 0.0612 0.0095216 0.06739999999999999 INSTRUMENTAL - ULTRA VIOLET Daily maxima of observed hourly values (between 9:00 AM and 8:00 PM) Parts per million null null null null null null null null null null null null null null null null null null null null null null null null 3.0 4.0 6.0 3.0 3.0 3.0 5 CA Alameda 2019 null null null null null null null null 21.414331500000003 55.18333333333334 45.63333333333333 9.367031333333331 50.48333333333334 INSTRUMENTAL - CHEMILUMINESCENCE Daily Maximum 1-hour average Parts per billion 0.0366726 0.0914 0.06799999999999999 0.0104352 0.08499999999999999 INSTRUMENTAL - ULTRA VIOLET Daily maxima of observed hourly values (between 9:00 AM and 8:00 PM) Parts per million null null null null null null null null null null null null null null null null null null null null null null null null 3.0 4.0 6.0 3.0 3.0 3.0 6 CA Amador 2015 null null null null null null null null null null null null null null null null 0.048449 0.103 0.088 0.015178 0.094 INSTRUMENTAL - ULTRA VIOLET ABSORPTION Daily maxima of observed hourly values (between 9:00 AM and 8:00 PM) Parts per million null null null null null null null null null null null null null null null null null null null null null null null null 3.0 3.0 7.0 3.0 3.0 3.0 7 CA Amador 2016 null null null null null null null null null null null null null null null null 0.047055 0.104 0.081 0.014501 0.084 INSTRUMENTAL - ULTRA VIOLET ABSORPTION Daily maxima of observed hourly 

Metric

In [0]:
# Get the unique methods across all method columns in the airquality dataframe
metricsDF = AQIDFAgg2.select('LEAD_METRIC').distinct()
metricsDF = metricsDF.withColumnRenamed("LEAD_METRIC","METRIC_NAME")
metricsDF2 = AQIDFAgg2.select('NO2_METRIC').distinct()
metricsDF2 = metricsDF2.withColumnRenamed("NO2_METRIC","METRIC_NAME")
metricsDF = metricsDF2.union(metricsDF)

metricsDF2 = AQIDFAgg2.select('OZONE_METRIC').distinct()
metricsDF2 = metricsDF2.withColumnRenamed("OZONE_METRIC","METRIC_NAME")
metricsDF = metricsDF2.union(metricsDF)

metricsDF2 = AQIDFAgg2.select('PM10_METRIC').distinct()
metricsDF2 = metricsDF2.withColumnRenamed("PM10_METRIC","METRIC_NAME")
metricsDF = metricsDF2.union(metricsDF)

metricsDF2 = AQIDFAgg2.select('PM25_METRIC').distinct()
metricsDF2 = metricsDF2.withColumnRenamed("PM25_METRIC","METRIC_NAME")
metricsDF = metricsDF2.union(metricsDF)

metricsDF2 = AQIDFAgg2.select('SO2_METRIC').distinct()
metricsDF2 = metricsDF2.withColumnRenamed("SO2_METRIC","METRIC_NAME")
metricsDF = metricsDF2.union(metricsDF)

metricsDF = metricsDF.select('METRIC_NAME').distinct()
display(metricsDF)

METRIC_NAME Daily maximum 1-hour average null Daily Mean Observed Values Daily maxima of observed hourly values (between 9:00 AM and 8:00 PM) Daily Maximum 1-hour average

In [0]:
try:
    metricsDF = metricsDF.sort('METRIC_NAME')    
    display(metricsDF)
    writer = metricsDF.write.format("jdbc").option("url", url) \
        .mode("append") \
        .option("dbtable", 'Metric') \
        .option("user", user) \
        .option("password", password) \
        .option("driver", "com.microsoft.sqlserver.jdbc.SQLServerDriver")
    writer.save()
except Exception as e:
    print(e)

    df_loaded = spark.read.format("jdbc") \
        .option("url", url) \
        .option("dbtable", "Metric") \
        .option("user", user) \
        .option("password", password) \
        .option("driver", "com.microsoft.sqlserver.jdbc.SQLServerDriver") \
        .load()
    print('df_loaded')
    display(df_loaded)   
        
    # Subtract the two to only leave what is not in the database
    # remove the index column of the loaded dataframe
    df_loaded = df_loaded.drop('METRIC_ID')
    df_toload = metricsDF.subtract(df_loaded)
    print('df_toload')
    display(df_toload)
    
    if(df_toload.count() > 0):
        # Upload all the data that wasn't already in the database
        df_toload.write.format("jdbc")  \
            .option("url", url) \
            .mode("append") \
            .option("dbtable", "Metric") \
            .option("user", user) \
            .option("password", password) \
            .option("driver", "com.microsoft.sqlserver.jdbc.SQLServerDriver") \
            .save()
    
metricsDF = spark.read.format("jdbc") \
    .option("url", url) \
    .option("dbtable", "Metric") \
    .option("user", user) \
    .option("password", password) \
    .option("driver", "com.microsoft.sqlserver.jdbc.SQLServerDriver") \
    .load()
display(metricsDF)  


METRIC_NAME null Daily Maximum 1-hour average Daily Mean Daily maxima of observed hourly values (between 9:00 AM and 8:00 PM) Daily maximum 1-hour average Observed Values

An error occurred while calling o23375.save.
: org.apache.spark.SparkException: Job aborted due to stage failure: Task 0 in stage 105691.0 failed 4 times, most recent failure: Lost task 0.3 in stage 105691.0 (TID 84471) (10.139.64.5 executor driver): java.sql.BatchUpdateException: Violation of UNIQUE KEY constraint 'uq_Metric_MetricName'. Cannot insert duplicate key in object 'dbo.Metric'. The duplicate key value is (<NULL>).
	at com.microsoft.sqlserver.jdbc.SQLServerPreparedStatement.executeBatch(SQLServerPreparedStatement.java:2085)
	at org.apache.spark.sql.execution.datasources.jdbc.JdbcUtils$.savePartition(JdbcUtils.scala:731)
	at org.apache.spark.sql.execution.datasources.jdbc.JdbcUtils$.$anonfun$saveTable$1(JdbcUtils.scala:888)
	at org.apache.spark.sql.execution.datasources.jdbc.JdbcUtils$.$anonfun$saveTable$1$adapted(JdbcUtils.scala:886)
	at org.apache.spark.rdd.RDD.$anonfun$foreachPartition$2(RDD.scala:1025)
	at org.apache.spark.rdd.RDD.$anonfun$foreachPartition$2$adapted(RDD.scala:1025)
	at org.apache.spark.SparkContext.$anonfun$runJob$2(SparkContext.scala:2576)
	at org.apache.spark.scheduler.ResultTask.$anonfun$runTask$3(ResultTask.scala:75)
	at com.databricks.spark.util.ExecutorFrameProfiler$.record(ExecutorFrameProfiler.scala:110)
	at org.apache.spark.scheduler.ResultTask.$anonfun$runTask$1(ResultTask.scala:75)
	at com.databricks.spark.util.ExecutorFrameProfiler$.record(ExecutorFrameProfiler.scala:110)
	at org.apache.spark.scheduler.ResultTask.runTask(ResultTask.scala:55)
	at org.apache.spark.scheduler.Task.doRunTask(Task.scala:153)
	at org.apache.spark.scheduler.Task.$anonfun$run$1(Task.scala:122)
	at com.databricks.spark.util.ExecutorFrameProfiler$.record(ExecutorFrameProfiler.scala:110)
	at org.apache.spark.scheduler.Task.run(Task.scala:93)
	at org.apache.spark.executor.Executor$TaskRunner.$anonfun$run$13(Executor.scala:824)
	at org.apache.spark.util.Utils$.tryWithSafeFinally(Utils.scala:1621)
	at org.apache.spark.executor.Executor$TaskRunner.$anonfun$run$4(Executor.scala:827)
	at scala.runtime.java8.JFunction0$mcV$sp.apply(JFunction0$mcV$sp.java:23)
	at com.databricks.spark.util.ExecutorFrameProfiler$.record(ExecutorFrameProfiler.scala:110)
	at org.apache.spark.executor.Executor$TaskRunner.run(Executor.scala:683)
	at java.util.concurrent.ThreadPoolExecutor.runWorker(ThreadPoolExecutor.java:1149)
	at java.util.concurrent.ThreadPoolExecutor$Worker.run(ThreadPoolExecutor.java:624)
	at java.lang.Thread.run(Thread.java:748)

Driver stacktrace:
	at org.apache.spark.scheduler.DAGScheduler.failJobAndIndependentStages(DAGScheduler.scala:2973)
	at org.apache.spark.scheduler.DAGScheduler.$anonfun$abortStage$2(DAGScheduler.scala:2920)
	at org.apache.spark.scheduler.DAGScheduler.$anonfun$abortStage$2$adapted(DAGScheduler.scala:2914)
	at scala.collection.mutable.ResizableArray.foreach(ResizableArray.scala:62)
	at scala.collection.mutable.ResizableArray.foreach$(ResizableArray.scala:55)
	at scala.collection.mutable.ArrayBuffer.foreach(ArrayBuffer.scala:49)
	at org.apache.spark.scheduler.DAGScheduler.abortStage(DAGScheduler.scala:2914)
	at org.apache.spark.scheduler.DAGScheduler.$anonfun$handleTaskSetFailed$1(DAGScheduler.scala:1334)
	at org.apache.spark.scheduler.DAGScheduler.$anonfun$handleTaskSetFailed$1$adapted(DAGScheduler.scala:1334)
	at scala.Option.foreach(Option.scala:407)
	at org.apache.spark.scheduler.DAGScheduler.handleTaskSetFailed(DAGScheduler.scala:1334)
	at org.apache.spark.scheduler.DAGSchedulerEventProcessLoop.doOnReceive(DAGScheduler.scala:3182)
	at org.apache.spark.scheduler.DAGSchedulerEventProcessLoop.onReceive(DAGScheduler.scala:3123)
	at org.apache.spark.scheduler.DAGSchedulerEventProcessLoop.onReceive(DAGScheduler.scala:3111)
	at org.apache.spark.util.EventLoop$$anon$1.run(EventLoop.scala:49)
	at org.apache.spark.scheduler.DAGScheduler.runJob(DAGScheduler.scala:1096)
	at org.apache.spark.SparkContext.runJobInternal(SparkContext.scala:2536)
	at org.apache.spark.SparkContext.runJob(SparkContext.scala:251

METRIC_ID METRIC_NAME 2 null 4 Daily maxima of observed hourly values (between 9:00 AM and 8:00 PM) 3 Daily Maximum 1-hour average 6 Daily maximum 1-hour average 5 Daily Mean 1 Observed Values

df_toload

METRIC_NAME

METRIC_ID METRIC_NAME 2 null 4 Daily maxima of observed hourly values (between 9:00 AM and 8:00 PM) 3 Daily Maximum 1-hour average 6 Daily maximum 1-hour average 5 Daily Mean 1 Observed Values

In [0]:
if(metricsDF.count() > 0):
    lead_matched = pd.DataFrame([])    
    NO2_matched = pd.DataFrame([])
    ozone_matched = pd.DataFrame([])
    PM10_matched = pd.DataFrame([])
    PM25_matched = pd.DataFrame([])
    SO2_matched = pd.DataFrame([])

    # Loop through all the rows in the AQ dataframe and find the matching method in the metrics dataframe
    for AQrow in AQIDFAgg2.toLocalIterator():
        if(AQrow.LEAD_METRIC == None): lead_matchedCol = metricsDF.filter((metricsDF.METRIC_NAME.isNull())).select('METRIC_ID')
        else: lead_matchedCol = metricsDF.filter((metricsDF.METRIC_NAME == AQrow.LEAD_METRIC)).select('METRIC_ID')  
        
        if(AQrow.NO2_METRIC == None): NO2_matchedCol = metricsDF.filter((metricsDF.METRIC_NAME.isNull())).select('METRIC_ID')
        else: NO2_matchedCol = metricsDF.filter((metricsDF.METRIC_NAME == AQrow.NO2_METRIC)).select('METRIC_ID')  
            
        if(AQrow.OZONE_METRIC == None): ozone_matchedCol = metricsDF.filter((metricsDF.METRIC_NAME.isNull())).select('METRIC_ID')
        else: ozone_matchedCol = metricsDF.filter((metricsDF.METRIC_NAME == AQrow.OZONE_METRIC)).select('METRIC_ID')  
            
        if(AQrow.PM10_METRIC == None): PM10_matchedCol = metricsDF.filter((metricsDF.METRIC_NAME.isNull())).select('METRIC_ID')
        else: PM10_matchedCol = metricsDF.filter((metricsDF.METRIC_NAME == AQrow.PM10_METRIC)).select('METRIC_ID')  
            
        if(AQrow.PM25_METRIC == None): PM25_matchedCol = metricsDF.filter((metricsDF.METRIC_NAME.isNull())).select('METRIC_ID')
        else: PM25_matchedCol = metricsDF.filter((metricsDF.METRIC_NAME == AQrow.PM25_METRIC)).select('METRIC_ID')  
            
        if(AQrow.SO2_METRIC == None): SO2_matchedCol = metricsDF.filter((metricsDF.METRIC_NAME.isNull())).select('METRIC_ID')
        else: SO2_matchedCol = metricsDF.filter((metricsDF.METRIC_NAME == AQrow.SO2_METRIC)).select('METRIC_ID')  

        if(lead_matchedCol.count() > 0): lead_matched = lead_matched.append({'AQ_ID': AQrow.AQ_ID, 'LEAD_METRIC_ID': lead_matchedCol.collect()[0][0]}, ignore_index=True)        
        if(NO2_matchedCol.count() > 0): NO2_matched = NO2_matched.append({'AQ_ID': AQrow.AQ_ID, 'NO2_METRIC_ID': NO2_matchedCol.collect()[0][0]}, ignore_index=True)
        if(ozone_matchedCol.count() > 0): ozone_matched = ozone_matched.append({'AQ_ID': AQrow.AQ_ID, 'OZONE_METRIC_ID': ozone_matchedCol.collect()[0][0]}, ignore_index=True)
        if(PM10_matchedCol.count() > 0): PM10_matched = PM10_matched.append({'AQ_ID': AQrow.AQ_ID, 'PM10_METRIC_ID': PM10_matchedCol.collect()[0][0]}, ignore_index=True)
        if(PM25_matchedCol.count() > 0): PM25_matched = PM25_matched.append({'AQ_ID': AQrow.AQ_ID, 'PM25_METRIC_ID': PM25_matchedCol.collect()[0][0]}, ignore_index=True)
        if(SO2_matchedCol.count() > 0): SO2_matched = SO2_matched.append({'AQ_ID': AQrow.AQ_ID, 'SO2_METRIC_ID': SO2_matchedCol.collect()[0][0]}, ignore_index=True)

                
    if(len(lead_matched) > 0): AQIDFAgg2 = AQIDFAgg2.join(spark.createDataFrame(lead_matched), on='AQ_ID', how='left_outer')
    if(len(NO2_matched) > 0): AQIDFAgg2 = AQIDFAgg2.join(spark.createDataFrame(NO2_matched), on='AQ_ID', how='left_outer')
    if(len(ozone_matched) > 0): AQIDFAgg2 = AQIDFAgg2.join(spark.createDataFrame(ozone_matched), on='AQ_ID', how='left_outer')
    if(len(PM10_matched) > 0): AQIDFAgg2 = AQIDFAgg2.join(spark.createDataFrame(PM10_matched), on='AQ_ID', how='left_outer')
    if(len(PM25_matched) > 0): AQIDFAgg2 = AQIDFAgg2.join(spark.createDataFrame(PM25_matched), on='AQ_ID', how='left_outer')
    if(len(SO2_matched) > 0): AQIDFAgg2 = AQIDFAgg2.join(spark.createDataFrame(SO2_matched), on='AQ_ID', how='left_outer')

        
    display(AQIDFAgg2)


AQ_ID state county year LEAD_MEAN LEAD_1STMAX LEAD_99PERC LEAD_STD LEAD_2NDMAX LEAD_METHOD LEAD_METRIC LEAD_UNITS NO2_MEAN NO2_1STMAX NO2_99PERC NO2_STD NO2_2NDMAX NO2_METHOD NO2_METRIC NO2_UNITS OZONE_MEAN OZONE_1STMAX OZONE_99PERC OZONE_STD OZONE_2NDMAX OZONE_METHOD OZONE_METRIC OZONE_UNITS PM10_MEAN PM10_1STMAX PM10_99PERC PM10_STD PM10_2NDMAX PM10_METHOD PM10_METRIC PM10_UNITS PM25_MEAN PM25_1STMAX PM25_99PERC PM25_STD PM25_2NDMAX PM25_METHOD PM25_METRIC PM25_UNITS SO2_MEAN SO2_1STMAX SO2_99PERC SO2_STD SO2_2NDMAX SO2_METHOD SO2_METRIC SO2_UNITS LEAD_METHOD_ID NO2_METHOD_ID OZONE_METHOD_ID PM10_METHOD_ID PM25_METHOD_ID SO2_METHOD_ID LEAD_METRIC_ID NO2_METRIC_ID OZONE_METRIC_ID PM10_METRIC_ID PM25_METRIC_ID SO2_METRIC_ID 1 CA Alameda 2015 null null null null null null null null 20.1278364 49.22 41.7 9.059481 45.279999999999994 INSTRUMENTAL - CHEMILUMINESCENCE Daily Maximum 1-hour average Parts per billion 0.0409086 0.0984 0.08620000000000001 0.0122206 0.092 INSTRUMENTAL - ULTRA VIOLET Daily maxima of observed hourly values (between 9:00 AM and 8:00 PM) Parts per million null null null null null null null null null null null null null null null null null null null null null null null null 3.0 4.0 6.0 3.0 3.0 3.0 2.0 3.0 4.0 2.0 2.0 2.0 2 CA Alameda 2016 null null null null null null null null 19.29764116666667 46.116666666666674 37.73333333333333 7.934909333333333 39.199999999999996 INSTRUMENTAL - CHEMILUMINESCENCE Daily Maximum 1-hour average Parts per billion 0.03733583333333334 0.08216666666666667 0.074 0.011103 0.07816666666666666 INSTRUMENTAL - ULTRA VIOLET Daily maxima of observed hourly values (between 9:00 AM and 8:00 PM) Parts per million null null null null null null null null null null null null null null null null null null null null null null null null 3.0 4.0 6.0 3.0 3.0 3.0 2.0 3.0 4.0 2.0 2.0 2.0 3 CA Alameda 2017 null null null null null null null null 20.515038 61.19999999999999 44.43333333333334 9.129422 49.883333333333326 INSTRUMENTAL - CHEMILUMINESCENCE Daily Maximum 1-hour average Parts per billion 0.038411 0.09766666666666667 0.07100000000000001 0.010734666666666665 0.08733333333333333 INSTRUMENTAL - ULTRA VIOLET Daily maxima of observed hourly values (between 9:00 AM and 8:00 PM) Parts per million null null null null null null null null null null null null null null null null null null null null null null null null 3.0 4.0 6.0 3.0 3.0 3.0 2.0 3.0 4.0 2.0 2.0 2.0 4 CA Alameda 2018 null null null null null null null null 22.827882166666665 69.06666666666666 59.199999999999996 10.554471166666668 65.26666666666667 INSTRUMENTAL - CHEMILUMINESCENCE Daily Maximum 1-hour average Parts per billion 0.036052799999999996 0.07139999999999999 0.0612 0.0095216 0.06739999999999999 INSTRUMENTAL - ULTRA VIOLET Daily maxima of observed hourly values (between 9:00 AM and 8:00 PM) Parts per million null null null null null null null null null null null null null null null null null null null null null null null null 3.0 4.0 6.0 3.0 3.0 3.0 2.0 3.0 4.0 2.0 2.0 2.0 5 CA Alameda 2019 null null null null null null null null 21.414331500000003 55.18333333333334 45.63333333333333 9.367031333333331 50.48333333333334 INSTRUMENTAL - CHEMILUMINESCENCE Daily Maximum 1-hour average Parts per billion 0.0366726 0.0914 0.06799999999999999 0.0104352 0.08499999999999999 INSTRUMENTAL - ULTRA VIOLET Daily maxima of observed hourly values (between 9:00 AM and 8:00 PM) Parts per million null null null null null null null null null null null null null null null null null null null null null null null null 3.0 4.0 6.0 3.0 3.0 3.0 2.0 3.0 4.0 2.0 2.0 2.0 6 CA Amador 2015 null null null null null null null null null null null null null null null null 0.048449 0.103 0.088 0.015178 0.094 INSTRUMENTAL - ULTRA VIOLET ABSORPTION Daily maxima of observed hourly values (between 9:00 AM and 8:00 PM) Parts per million null null null null null null null null null null null null null null null null null null null null null null null null 3.0 3.0 7.0 3.0 3.0

Units

In [0]:
# Get the unique methods across all method columns in the airquality dataframe
unitsDF = AQIDFAgg2.select('LEAD_UNITS').distinct()
unitsDF = unitsDF.withColumnRenamed("LEAD_UNITS","UNIT_NAME")
unitsDF2 = AQIDFAgg2.select('NO2_UNITS').distinct()
unitsDF2 = unitsDF2.withColumnRenamed("NO2_UNITS","UNIT_NAME")
unitsDF = unitsDF2.union(unitsDF)

unitsDF2 = AQIDFAgg2.select('OZONE_UNITS').distinct()
unitsDF2 = unitsDF2.withColumnRenamed("OZONE_UNITS","UNIT_NAME")
unitsDF = unitsDF2.union(unitsDF)

unitsDF2 = AQIDFAgg2.select('PM10_UNITS').distinct()
unitsDF2 = unitsDF2.withColumnRenamed("PM10_UNITS","UNIT_NAME")
unitsDF = unitsDF2.union(unitsDF)

unitsDF2 = AQIDFAgg2.select('PM25_UNITS').distinct()
unitsDF2 = unitsDF2.withColumnRenamed("PM25_UNITS","UNIT_NAME")
unitsDF = unitsDF2.union(unitsDF)

unitsDF2 = AQIDFAgg2.select('SO2_UNITS').distinct()
unitsDF2 = unitsDF2.withColumnRenamed("SO2_UNITS","UNIT_NAME")
unitsDF = unitsDF2.union(unitsDF)

unitsDF = unitsDF.select('UNIT_NAME').distinct()
display(unitsDF)

UNIT_NAME null Parts per billion Micrograms/cubic meter (LC) Micrograms/cubic meter (25 C) Parts per million

In [0]:
try:
    writer = unitsDF.write.format("jdbc").option("url", url) \
        .mode("append") \
        .option("dbtable", 'Unit') \
        .option("user", user) \
        .option("password", password) \
        .option("driver", "com.microsoft.sqlserver.jdbc.SQLServerDriver")
    writer.save()
except Exception as e:
    print(e)

    df_loaded = spark.read.format("jdbc") \
        .option("url", url) \
        .option("dbtable", "Unit") \
        .option("user", user) \
        .option("password", password) \
        .option("driver", "com.microsoft.sqlserver.jdbc.SQLServerDriver") \
        .load()
    print('df_loaded')
    display(df_loaded)   
        
    # Subtract the two to only leave what is not in the database
    # remove the index column of the loaded dataframe
    df_loaded = df_loaded.drop('UNIT_ID')
    df_toload = unitsDF.subtract(df_loaded)
    print('df_toload')
    display(df_toload)
    
    if(df_toload.count() > 0):
        # Upload all the data that wasn't already in the database
        df_toload.write.format("jdbc")  \
            .option("url", url) \
            .mode("append") \
            .option("dbtable", "Unit") \
            .option("user", user) \
            .option("password", password) \
            .option("driver", "com.microsoft.sqlserver.jdbc.SQLServerDriver") \
            .save()
    
unitsDF = spark.read.format("jdbc") \
    .option("url", url) \
    .option("dbtable", "Unit") \
    .option("user", user) \
    .option("password", password) \
    .option("driver", "com.microsoft.sqlserver.jdbc.SQLServerDriver") \
    .load()
display(unitsDF)  


An error occurred while calling o40388.save.
: org.apache.spark.SparkException: Job aborted due to stage failure: Task 0 in stage 112225.0 failed 4 times, most recent failure: Lost task 0.3 in stage 112225.0 (TID 89838) (10.139.64.5 executor driver): java.sql.BatchUpdateException: Violation of UNIQUE KEY constraint 'uq_Unit_UnitName'. Cannot insert duplicate key in object 'dbo.Unit'. The duplicate key value is (<NULL>).
	at com.microsoft.sqlserver.jdbc.SQLServerPreparedStatement.executeBatch(SQLServerPreparedStatement.java:2085)
	at org.apache.spark.sql.execution.datasources.jdbc.JdbcUtils$.savePartition(JdbcUtils.scala:731)
	at org.apache.spark.sql.execution.datasources.jdbc.JdbcUtils$.$anonfun$saveTable$1(JdbcUtils.scala:888)
	at org.apache.spark.sql.execution.datasources.jdbc.JdbcUtils$.$anonfun$saveTable$1$adapted(JdbcUtils.scala:886)
	at org.apache.spark.rdd.RDD.$anonfun$foreachPartition$2(RDD.scala:1025)
	at org.apache.spark.rdd.RDD.$anonfun$foreachPartition$2$adapted(RDD.scala:1025)
	at org.apache.spark.SparkContext.$anonfun$runJob$2(SparkContext.scala:2576)
	at org.apache.spark.scheduler.ResultTask.$anonfun$runTask$3(ResultTask.scala:75)
	at com.databricks.spark.util.ExecutorFrameProfiler$.record(ExecutorFrameProfiler.scala:110)
	at org.apache.spark.scheduler.ResultTask.$anonfun$runTask$1(ResultTask.scala:75)
	at com.databricks.spark.util.ExecutorFrameProfiler$.record(ExecutorFrameProfiler.scala:110)
	at org.apache.spark.scheduler.ResultTask.runTask(ResultTask.scala:55)
	at org.apache.spark.scheduler.Task.doRunTask(Task.scala:153)
	at org.apache.spark.scheduler.Task.$anonfun$run$1(Task.scala:122)
	at com.databricks.spark.util.ExecutorFrameProfiler$.record(ExecutorFrameProfiler.scala:110)
	at org.apache.spark.scheduler.Task.run(Task.scala:93)
	at org.apache.spark.executor.Executor$TaskRunner.$anonfun$run$13(Executor.scala:824)
	at org.apache.spark.util.Utils$.tryWithSafeFinally(Utils.scala:1621)
	at org.apache.spark.executor.Executor$TaskRunner.$anonfun$run$4(Executor.scala:827)
	at scala.runtime.java8.JFunction0$mcV$sp.apply(JFunction0$mcV$sp.java:23)
	at com.databricks.spark.util.ExecutorFrameProfiler$.record(ExecutorFrameProfiler.scala:110)
	at org.apache.spark.executor.Executor$TaskRunner.run(Executor.scala:683)
	at java.util.concurrent.ThreadPoolExecutor.runWorker(ThreadPoolExecutor.java:1149)
	at java.util.concurrent.ThreadPoolExecutor$Worker.run(ThreadPoolExecutor.java:624)
	at java.lang.Thread.run(Thread.java:748)

Driver stacktrace:
	at org.apache.spark.scheduler.DAGScheduler.failJobAndIndependentStages(DAGScheduler.scala:2973)
	at org.apache.spark.scheduler.DAGScheduler.$anonfun$abortStage$2(DAGScheduler.scala:2920)
	at org.apache.spark.scheduler.DAGScheduler.$anonfun$abortStage$2$adapted(DAGScheduler.scala:2914)
	at scala.collection.mutable.ResizableArray.foreach(ResizableArray.scala:62)
	at scala.collection.mutable.ResizableArray.foreach$(ResizableArray.scala:55)
	at scala.collection.mutable.ArrayBuffer.foreach(ArrayBuffer.scala:49)
	at org.apache.spark.scheduler.DAGScheduler.abortStage(DAGScheduler.scala:2914)
	at org.apache.spark.scheduler.DAGScheduler.$anonfun$handleTaskSetFailed$1(DAGScheduler.scala:1334)
	at org.apache.spark.scheduler.DAGScheduler.$anonfun$handleTaskSetFailed$1$adapted(DAGScheduler.scala:1334)
	at scala.Option.foreach(Option.scala:407)
	at org.apache.spark.scheduler.DAGScheduler.handleTaskSetFailed(DAGScheduler.scala:1334)
	at org.apache.spark.scheduler.DAGSchedulerEventProcessLoop.doOnReceive(DAGScheduler.scala:3182)
	at org.apache.spark.scheduler.DAGSchedulerEventProcessLoop.onReceive(DAGScheduler.scala:3123)
	at org.apache.spark.scheduler.DAGSchedulerEventProcessLoop.onReceive(DAGScheduler.scala:3111)
	at org.apache.spark.util.EventLoop$$anon$1.run(EventLoop.scala:49)
	at org.apache.spark.scheduler.DAGScheduler.runJob(DAGScheduler.scala:1096)
	at org.apache.spark.SparkContext.runJobInternal(SparkContext.scala:2536)
	at org.apache.spark.SparkContext.runJob(SparkContext.scala:2519)
	at

UNIT_ID UNIT_NAME 2 null 5 Micrograms/cubic meter (25 C) 1 Micrograms/cubic meter (LC) 3 Parts per billion 4 Parts per million

df_toload

UNIT_NAME

UNIT_ID UNIT_NAME 2 null 5 Micrograms/cubic meter (25 C) 1 Micrograms/cubic meter (LC) 3 Parts per billion 4 Parts per million

In [0]:
if(unitsDF.count() > 0):
    lead_matched = pd.DataFrame([])    
    NO2_matched = pd.DataFrame([])
    ozone_matched = pd.DataFrame([])
    PM10_matched = pd.DataFrame([])
    PM25_matched = pd.DataFrame([])
    SO2_matched = pd.DataFrame([])

    # Loop through all the rows in the AQ dataframe and find the matching method in the metrics dataframe
    for AQrow in AQIDFAgg2.toLocalIterator():
        if(AQrow.LEAD_UNITS == None): lead_matchedCol = unitsDF.filter((unitsDF.UNIT_NAME.isNull())).select('UNIT_ID')
        else: lead_matchedCol = unitsDF.filter((unitsDF.UNIT_NAME == AQrow.LEAD_UNITS)).select('UNIT_ID')  
        
        if(AQrow.NO2_UNITS == None): NO2_matchedCol = unitsDF.filter((unitsDF.UNIT_NAME.isNull())).select('UNIT_ID')
        else: NO2_matchedCol = unitsDF.filter((unitsDF.UNIT_NAME == AQrow.NO2_UNITS)).select('UNIT_ID')  
            
        if(AQrow.OZONE_UNITS == None): ozone_matchedCol = unitsDF.filter((unitsDF.UNIT_NAME.isNull())).select('UNIT_ID')
        else: ozone_matchedCol = unitsDF.filter((unitsDF.UNIT_NAME == AQrow.OZONE_UNITS)).select('UNIT_ID')  
            
        if(AQrow.PM10_UNITS == None): PM10_matchedCol = unitsDF.filter((unitsDF.UNIT_NAME.isNull())).select('UNIT_ID')
        else: PM10_matchedCol = unitsDF.filter((unitsDF.UNIT_NAME == AQrow.PM10_UNITS)).select('UNIT_ID')  
            
        if(AQrow.PM25_UNITS == None): PM25_matchedCol = unitsDF.filter((unitsDF.UNIT_NAME.isNull())).select('UNIT_ID')
        else: PM25_matchedCol = unitsDF.filter((unitsDF.UNIT_NAME == AQrow.PM25_UNITS)).select('UNIT_ID')  
            
        if(AQrow.SO2_UNITS == None): SO2_matchedCol = unitsDF.filter((unitsDF.UNIT_NAME.isNull())).select('UNIT_ID')
        else: SO2_matchedCol = unitsDF.filter((unitsDF.UNIT_NAME == AQrow.SO2_UNITS)).select('UNIT_ID')  

        if(lead_matchedCol.count() > 0): lead_matched = lead_matched.append({'AQ_ID': AQrow.AQ_ID, 'LEAD_UNITS_ID': lead_matchedCol.collect()[0][0]}, ignore_index=True)        
        if(NO2_matchedCol.count() > 0): NO2_matched = NO2_matched.append({'AQ_ID': AQrow.AQ_ID, 'NO2_UNITS_ID': NO2_matchedCol.collect()[0][0]}, ignore_index=True)
        if(ozone_matchedCol.count() > 0): ozone_matched = ozone_matched.append({'AQ_ID': AQrow.AQ_ID, 'OZONE_UNITS_ID': ozone_matchedCol.collect()[0][0]}, ignore_index=True)
        if(PM10_matchedCol.count() > 0): PM10_matched = PM10_matched.append({'AQ_ID': AQrow.AQ_ID, 'PM10_UNITS_ID': PM10_matchedCol.collect()[0][0]}, ignore_index=True)
        if(PM25_matchedCol.count() > 0): PM25_matched = PM25_matched.append({'AQ_ID': AQrow.AQ_ID, 'PM25_UNITS_ID': PM25_matchedCol.collect()[0][0]}, ignore_index=True)
        if(SO2_matchedCol.count() > 0): SO2_matched = SO2_matched.append({'AQ_ID': AQrow.AQ_ID, 'SO2_UNITS_ID': SO2_matchedCol.collect()[0][0]}, ignore_index=True)

                
    if(len(lead_matched) > 0): AQIDFAgg2 = AQIDFAgg2.join(spark.createDataFrame(lead_matched), on='AQ_ID', how='left_outer')
    if(len(NO2_matched) > 0): AQIDFAgg2 = AQIDFAgg2.join(spark.createDataFrame(NO2_matched), on='AQ_ID', how='left_outer')
    if(len(ozone_matched) > 0): AQIDFAgg2 = AQIDFAgg2.join(spark.createDataFrame(ozone_matched), on='AQ_ID', how='left_outer')
    if(len(PM10_matched) > 0): AQIDFAgg2 = AQIDFAgg2.join(spark.createDataFrame(PM10_matched), on='AQ_ID', how='left_outer')
    if(len(PM25_matched) > 0): AQIDFAgg2 = AQIDFAgg2.join(spark.createDataFrame(PM25_matched), on='AQ_ID', how='left_outer')
    if(len(SO2_matched) > 0): AQIDFAgg2 = AQIDFAgg2.join(spark.createDataFrame(SO2_matched), on='AQ_ID', how='left_outer')

        
    display(AQIDFAgg2)


AQ_ID state county year LEAD_MEAN LEAD_1STMAX LEAD_99PERC LEAD_STD LEAD_2NDMAX LEAD_METHOD LEAD_METRIC LEAD_UNITS NO2_MEAN NO2_1STMAX NO2_99PERC NO2_STD NO2_2NDMAX NO2_METHOD NO2_METRIC NO2_UNITS OZONE_MEAN OZONE_1STMAX OZONE_99PERC OZONE_STD OZONE_2NDMAX OZONE_METHOD OZONE_METRIC OZONE_UNITS PM10_MEAN PM10_1STMAX PM10_99PERC PM10_STD PM10_2NDMAX PM10_METHOD PM10_METRIC PM10_UNITS PM25_MEAN PM25_1STMAX PM25_99PERC PM25_STD PM25_2NDMAX PM25_METHOD PM25_METRIC PM25_UNITS SO2_MEAN SO2_1STMAX SO2_99PERC SO2_STD SO2_2NDMAX SO2_METHOD SO2_METRIC SO2_UNITS LEAD_METHOD_ID NO2_METHOD_ID OZONE_METHOD_ID PM10_METHOD_ID PM25_METHOD_ID SO2_METHOD_ID LEAD_METRIC_ID NO2_METRIC_ID OZONE_METRIC_ID PM10_METRIC_ID PM25_METRIC_ID SO2_METRIC_ID LEAD_UNITS_ID NO2_UNITS_ID OZONE_UNITS_ID PM10_UNITS_ID PM25_UNITS_ID SO2_UNITS_ID 1 CA Alameda 2015 null null null null null null null null 20.1278364 49.22 41.7 9.059481 45.279999999999994 INSTRUMENTAL - CHEMILUMINESCENCE Daily Maximum 1-hour average Parts per billion 0.0409086 0.0984 0.08620000000000001 0.0122206 0.092 INSTRUMENTAL - ULTRA VIOLET Daily maxima of observed hourly values (between 9:00 AM and 8:00 PM) Parts per million null null null null null null null null null null null null null null null null null null null null null null null null 3.0 4.0 6.0 3.0 3.0 3.0 2.0 3.0 4.0 2.0 2.0 2.0 2.0 3.0 4.0 2.0 2.0 2.0 2 CA Alameda 2016 null null null null null null null null 19.29764116666667 46.116666666666674 37.73333333333333 7.934909333333333 39.199999999999996 INSTRUMENTAL - CHEMILUMINESCENCE Daily Maximum 1-hour average Parts per billion 0.03733583333333334 0.08216666666666667 0.074 0.011103 0.07816666666666666 INSTRUMENTAL - ULTRA VIOLET Daily maxima of observed hourly values (between 9:00 AM and 8:00 PM) Parts per million null null null null null null null null null null null null null null null null null null null null null null null null 3.0 4.0 6.0 3.0 3.0 3.0 2.0 3.0 4.0 2.0 2.0 2.0 2.0 3.0 4.0 2.0 2.0 2.0 3 CA Alameda 2017 null null null null null null null null 20.515038 61.19999999999999 44.43333333333334 9.129422 49.883333333333326 INSTRUMENTAL - CHEMILUMINESCENCE Daily Maximum 1-hour average Parts per billion 0.038411 0.09766666666666667 0.07100000000000001 0.010734666666666665 0.08733333333333333 INSTRUMENTAL - ULTRA VIOLET Daily maxima of observed hourly values (between 9:00 AM and 8:00 PM) Parts per million null null null null null null null null null null null null null null null null null null null null null null null null 3.0 4.0 6.0 3.0 3.0 3.0 2.0 3.0 4.0 2.0 2.0 2.0 2.0 3.0 4.0 2.0 2.0 2.0 4 CA Alameda 2018 null null null null null null null null 22.827882166666665 69.06666666666666 59.199999999999996 10.554471166666668 65.26666666666667 INSTRUMENTAL - CHEMILUMINESCENCE Daily Maximum 1-hour average Parts per billion 0.036052799999999996 0.07139999999999999 0.0612 0.0095216 0.06739999999999999 INSTRUMENTAL - ULTRA VIOLET Daily maxima of observed hourly values (between 9:00 AM and 8:00 PM) Parts per million null null null null null null null null null null null null null null null null null null null null null null null null 3.0 4.0 6.0 3.0 3.0 3.0 2.0 3.0 4.0 2.0 2.0 2.0 2.0 3.0 4.0 2.0 2.0 2.0 5 CA Alameda 2019 null null null null null null null null 21.414331500000003 55.18333333333334 45.63333333333333 9.367031333333331 50.48333333333334 INSTRUMENTAL - CHEMILUMINESCENCE Daily Maximum 1-hour average Parts per billion 0.0366726 0.0914 0.06799999999999999 0.0104352 0.08499999999999999 INSTRUMENTAL - ULTRA VIOLET Daily maxima of observed hourly values (between 9:00 AM and 8:00 PM) Parts per million null null null null null null null null null null null null null null null null null null null null null null null null 3.0 4.0 6.0 3.0 3.0 3.0 2.0 3.0 4.0 2.0 2.0 2.0 2.0 3.0 4.0 2.0 2.0 2.0 6 CA Amador 2015 null null null null null null null null null null null null null null null null 0.048449 0.103 0.088 0.015178 0.094 INSTRUMENTAL - ULTRA VIOLET ABSORPTION Daily maxima of observe

The method, metric, and unit ID columns have now been added. Deleted the columns they are replacing. ALso, drop the AQ_ID column because the SQL database is set to fill that in itself.

In [0]:
AQIDFAgg2 = AQIDFAgg2.drop('LEAD_METHOD','LEAD_METRIC', 'LEAD_UNITS')
AQIDFAgg2 = AQIDFAgg2.drop('NO2_METHOD','NO2_METRIC', 'NO2_UNITS')
AQIDFAgg2 = AQIDFAgg2.drop('OZONE_METHOD','OZONE_METRIC', 'OZONE_UNITS')
AQIDFAgg2 = AQIDFAgg2.drop('PM10_METHOD','PM10_METRIC', 'PM10_UNITS')
AQIDFAgg2 = AQIDFAgg2.drop('PM25_METHOD','PM25_METRIC', 'PM25_UNITS')
AQIDFAgg2 = AQIDFAgg2.drop('SO2_METHOD','SO2_METRIC', 'SO2_UNITS')


In [0]:
AQIDFAgg2 = AQIDFAgg2.drop('AQ_ID')
display(AQIDFAgg2)

state county year LEAD_MEAN LEAD_1STMAX LEAD_99PERC LEAD_STD LEAD_2NDMAX NO2_MEAN NO2_1STMAX NO2_99PERC NO2_STD NO2_2NDMAX OZONE_MEAN OZONE_1STMAX OZONE_99PERC OZONE_STD OZONE_2NDMAX PM10_MEAN PM10_1STMAX PM10_99PERC PM10_STD PM10_2NDMAX PM25_MEAN PM25_1STMAX PM25_99PERC PM25_STD PM25_2NDMAX SO2_MEAN SO2_1STMAX SO2_99PERC SO2_STD SO2_2NDMAX LEAD_METHOD_ID NO2_METHOD_ID OZONE_METHOD_ID PM10_METHOD_ID PM25_METHOD_ID SO2_METHOD_ID LEAD_METRIC_ID NO2_METRIC_ID OZONE_METRIC_ID PM10_METRIC_ID PM25_METRIC_ID SO2_METRIC_ID LEAD_UNITS_ID NO2_UNITS_ID OZONE_UNITS_ID PM10_UNITS_ID PM25_UNITS_ID SO2_UNITS_ID CA Sonoma 2018 null null null null null 10.831921 65.1 45.0 8.739281 56.4 0.0379805 0.073 0.0615 0.009461500000000001 0.0675 null null null null null null null null null null null null null null null 3.0 4.0 6.0 3.0 3.0 3.0 2.0 3.0 4.0 2.0 2.0 2.0 2.0 3.0 4.0 2.0 2.0 2.0 CA Stanislaus 2015 null null null null null 18.95788 42.0 38.0 8.758836 38.0 0.051584 0.112 0.0955 0.018962 0.1 32.051724 76.0 76.0 15.31359 64.0 null null null null null null null null null null 3.0 4.0 6.0 3.0 3.0 3.0 2.0 3.0 4.0 2.0 2.0 2.0 2.0 3.0 4.0 2.0 2.0 2.0 CA Calaveras 2017 null null null null null null null null null null 0.052957 0.109 0.089 0.015065 0.091 null null null null null null null null null null null null null null null 3.0 4.0 6.0 3.0 3.0 3.0 2.0 3.0 4.0 2.0 2.0 2.0 2.0 3.0 4.0 2.0 2.0 2.0 CA Contra Costa 2019 null null null null null 12.650939249999999 39.325 33.325 7.3735775 35.825 0.04185325 0.093 0.07650000000000001 0.0117075 0.08625 null null null null null 6.133333 25.5 25.5 3.794034 17.2 null null null null null 3.0 4.0 6.0 3.0 3.0 3.0 2.0 3.0 4.0 2.0 2.0 2.0 2.0 3.0 4.0 2.0 2.0 2.0 CA Lake 2016 null null null null null null null null null null 0.041474 0.068 0.065 0.008504 0.068 null null null null null null null null null null null null null null null 3.0 4.0 6.0 3.0 3.0 3.0 2.0 3.0 4.0 2.0 2.0 2.0 2.0 3.0 4.0 2.0 2.0 2.0 CA Santa Clara 2016 null null null null null 23.385278 51.650000000000006 46.0 9.6735115 50.25 0.04473725 0.08825000000000001 0.07775 0.01179375 0.08275 null null null null null 8.045263 22.7 22.7 3.8341620000000005 20.3 0.537047 1.8 1.6 0.381402 1.7 3.0 3.0 7.0 3.0 3.0 3.0 2.0 2.0 4.0 2.0 2.0 2.0 2.0 2.0 4.0 2.0 2.0 2.0 CA Los Angeles 2015 0.012373857142857143 0.036357142857142866 0.03450000000000001 0.006707142857142857 0.029857142857142863 29.4755605 73.84285714285714 62.38571428571429 12.8423125 67.30714285714286 0.05485715384615385 0.1123076923076923 0.09992307692307692 0.017254538461538464 0.1053846153846154 null null null null null 10.92832075 51.410000000000046 40.33500000000003 6.861900049999998 42.68500000000003 1.8496146666666669 21.666666666666668 8.3 1.8388513333333334 9.7 3.0 3.0 7.0 3.0 3.0 3.0 2.0 2.0 4.0 2.0 2.0 2.0 2.0 2.0 4.0 2.0 2.0 2.0 CA San Diego 2016 null null null null null 19.314231777777778 57.666666666666664 46.666666666666664 10.879725888888888 50.55555555555556 0.050642363636363645 0.08572727272727271 0.08072727272727272 0.01088409090909091 0.08281818181818179 null null null null null 8.451768666666668 23.533333333333328 19.866666666666664 3.427879 18.599999999999998 0.2253495 1.2 0.65 0.1548435 0.65 3.0 3.0 7.0 3.0 3.0 3.0 2.0 2.0 4.0 2.0 2.0 2.0 2.0 2.0 4.0 2.0 2.0 2.0 CA Riverside 2017 0.005121 0.015 0.015 0.003032 0.014 17.986095 50.11428571428571 41.8 9.269774571428572 43.857142857142854 0.0603519090909091 0.11436363636363635 0.10454545454545455 0.017974090909090912 0.11163636363636363 null null null null null 12.455024749999998 46.15 40.6 7.090440500000001 40.87500000000001 0.617355 2.5 1.9 0.414118 2.3 3.0 3.0 7.0 3.0 3.0 3.0 2.0 2.0 4.0 2.0 2.0 2.0 2.0 2.0 4.0 2.0 2.0 2.0 CA Orange 2016 null null null null null 26.712885999999997 64.925 58.6 13.15272775 61.525000000000006 0.0510245 0.10449999999999998 0.08925 0.01382375 0.09674999999999999 null null null null null 8.3535625 34.550000000000004 22.95 4.102276000000001 26.3 0.465903 3.3 2.1 0.496436 3.2 3.0 3.0 7.0 3.0 3.0 3.0 2.0 2.

County

In [0]:
display(countyStateDF)

STATE_ID COUNTY_ID COUNTY_NAME STATE_ABBR STATE_NAME 1 3109 Big Horn MT Montana 1 2975 Petroleum MT Montana 1 2953 Granite MT Montana 1 2924 Carter MT Montana 1 2832 Rosebud MT Montana 1 2770 Flathead MT Montana 1 2639 Daniels MT Montana 1 2568 Deer Lodge MT Montana 1 2498 Ravalli MT Montana 1 2497 McCone MT Montana 1 2409 Valley MT Montana 1 2378 Blaine MT Montana 1 2363 Beaverhead MT Montana 1 2307 Sanders MT Montana 1 2306 Dawson MT Montana 1 2287 Richland MT Montana 1 2272 Lake MT Montana 1 2158 Musselshell MT Montana 1 2126 Fallon MT Montana 1 2094 Judith Basin MT Montana 1 2074 Gallatin MT Montana 1 2014 Meagher MT Montana 1 1978 Madison MT Montana 1 1812 Cascade MT Montana 1 1707 Yellowstone MT Montana 1 1689 Toole MT Montana 1 1582 Prairie MT Montana 1 1557 Pondera MT Montana 1 1533 Custer MT Montana 1 1456 Jefferson MT Montana 1 1398 Liberty MT Montana 1 1374 Powder River MT Montana 1 1279 Chouteau MT Montana 1 1171 Broadwater MT Montana 1 1133 Sweet Grass MT Montana 1 1008 Powell MT Montana 1 951 Wheatland MT Montana 1 806 Phillips MT Montana 1 678 Golden Valley MT Montana 1 644 Glacier MT Montana 1 627 Fergus MT Montana 1 610 Missoula MT Montana 1 559 Mineral MT Montana 1 487 Lincoln MT Montana 1 467 Roosevelt MT Montana 1 359 Garfield MT Montana 1 357 Treasure MT Montana 1 323 Wibaux MT Montana 1 230 Park MT Montana 1 211 Stillwater MT Montana 1 182 Lewis and Clark MT Montana 1 167 Sheridan MT Montana 1 142 Carbon MT Montana 1 141 Hill MT Montana 1 116 Teton MT Montana 1 37 Silver Bow MT Montana 2 3092 Currituck NC North Carolina 2 2999 Mitchell NC North Carolina 2 2998 Durham NC North Carolina 2 2974 Beaufort NC North Carolina 2 2925 Duplin NC North Carolina 2 2908 Davidson NC North Carolina 2 2810 Greene NC North Carolina 2 2785 Alleghany NC North Carolina 2 2769 Guilford NC North Carolina 2 2731 Yancey NC North Carolina 2 2714 McDowell NC North Carolina 2 2692 Caswell NC North Carolina 2 2691 Columbus NC North Carolina 2 2672 Transylvania NC North Carolina 2 2671 Madison NC North Carolina 2 2638 Hertford NC North Carolina 2 2597 Cherokee NC North Carolina 2 2587 Randolph NC North Carolina 2 2585 Northampton NC North Carolina 2 2520 Franklin NC North Carolina 2 2501 Stanly NC North Carolina 2 2482 Wilson NC North Carolina 2 2448 Graham NC North Carolina 2 2408 Orange NC North Carolina 2 2377 Gaston NC North Carolina 2 2285 Hyde NC North Carolina 2 2193 Burke NC North Carolina 2 2110 Pender NC North Carolina 2 2092 Clay NC North Carolina 2 2041 Scotland NC North Carolina 2 2003 Alamance NC North Carolina 2 1980 Montgomery NC North Carolina 2 1979 Cumberland NC North Carolina 2 1964 Onslow NC North Carolina 2 1934 Forsyth NC North Carolina 2 1849 Warren NC North Carolina 2 1811 Catawba NC North Carolina 2 1784 Carteret NC North Carolina 2 1730 Lincoln NC North Carolina 2 1712 Vance NC North Carolina 2 1708 Moore NC North Carolina 2 1688 Bladen NC North Carolina 2 1687 Gates NC North Carolina 2 1670 Martin NC North Carolina 2 1649 Harnett NC North Carolina 2 1635 Caldwell NC North Carolina 2 1634 Alexander NC North Carolina 2 1568 Davie NC North Carolina 2 1545 Person NC North Carolina 2 1519 Perquimans NC North Carolina 2 1505 Surry NC North Carolina 2 1479 New Hanover NC North Carolina 2 1438 Camden NC North Carolina 2 1390 Mecklenburg NC North Carolina 2 1246 Pasquotank NC North Carolina 2 1104 Yadkin NC North Carolina 2 1089 Lenoir NC North Carolina 2 1069 Wayne NC North Carolina 2 1057 Lee NC North Carolina 2 1045 Dare NC North Carolina 2 994 Pitt NC North Carolina 2 960 Edgecombe NC North Carolina 2 917 Chatham NC North Carolina 2 904 Stokes NC North Carolina 2 901 Swain NC North Carolina 2 851 Avery NC North Carolina 2 836 Rutherford NC North Carolina 2 818 Wake NC North Carolina 2 816 Macon NC North Carolina 2 792 Washington NC North Carolina 2 790 Rockingham NC North Carolina 2 788 Chowan NC North Carolina 2 746 Buncombe NC North Carolina 2 732 Haywood NC North Carolina 2 698 Tyrrell NC North Carolina 2 676

In [0]:
import pandas as pd
# Add in an ID to the table 
AQIDFAgg2 = AQIDFAgg2.withColumn('AQ_ID',F.monotonically_increasing_id()+1)

matched = pd.DataFrame([])
noMatchFound = False
display(AQIDFAgg2)
display(countyStateDF)
# If there are current countyies in the database, look through them for a match
if(countyStateDF.count() > 0):
    for countyAQ in AQIDFAgg2.toLocalIterator():
        matchedCol = countyStateDF.filter((countyStateDF.COUNTY_NAME == countyAQ.county) & (countyStateDF.STATE_ABBR == countyAQ.state)).select('COUNTY_ID')  
        # There are conditions where there isn't a match like if the county isn't loaded in the in the table, yet, or we have statewide data.
        if(matchedCol.count() >0):
            matched = matched.append({'AQ_ID': countyAQ.AQ_ID, 
                                      'COUNTY_ID': matchedCol.collect()[0][0]},
                                     ignore_index=True)
        else: noMatchFound = True
    if(len(matched)>0):    
        matched = spark.createDataFrame(matched)
        display(matched)
        # if everything went ok, then join the matched tabled of county ID's to the asthma dataframe
        AQIDFAgg2 = AQIDFAgg2.join(matched, on='AQ_ID', how='left_outer')
        display(AQIDFAgg2)
    else:
        print("NOTHING MATCHED")
        AQIDFAgg2 = AQIDFAgg2.withColumn('COUNTY_ID', lit(None))

display(AQIDFAgg2)
print(noMatchFound)

state county year LEAD_MEAN LEAD_1STMAX LEAD_99PERC LEAD_STD LEAD_2NDMAX NO2_MEAN NO2_1STMAX NO2_99PERC NO2_STD NO2_2NDMAX OZONE_MEAN OZONE_1STMAX OZONE_99PERC OZONE_STD OZONE_2NDMAX PM10_MEAN PM10_1STMAX PM10_99PERC PM10_STD PM10_2NDMAX PM25_MEAN PM25_1STMAX PM25_99PERC PM25_STD PM25_2NDMAX SO2_MEAN SO2_1STMAX SO2_99PERC SO2_STD SO2_2NDMAX LEAD_METHOD_ID NO2_METHOD_ID OZONE_METHOD_ID PM10_METHOD_ID PM25_METHOD_ID SO2_METHOD_ID LEAD_METRIC_ID NO2_METRIC_ID OZONE_METRIC_ID PM10_METRIC_ID PM25_METRIC_ID SO2_METRIC_ID LEAD_UNITS_ID NO2_UNITS_ID OZONE_UNITS_ID PM10_UNITS_ID PM25_UNITS_ID SO2_UNITS_ID AQ_ID CA Sonoma 2018 null null null null null 10.831921 65.1 45.0 8.739281 56.4 0.0379805 0.073 0.0615 0.009461500000000001 0.0675 null null null null null null null null null null null null null null null 3.0 4.0 6.0 3.0 3.0 3.0 2.0 3.0 4.0 2.0 2.0 2.0 2.0 3.0 4.0 2.0 2.0 2.0 1 CA Stanislaus 2015 null null null null null 18.95788 42.0 38.0 8.758836 38.0 0.051584 0.112 0.0955 0.018962 0.1 32.051724 76.0 76.0 15.31359 64.0 null null null null null null null null null null 3.0 4.0 6.0 3.0 3.0 3.0 2.0 3.0 4.0 2.0 2.0 2.0 2.0 3.0 4.0 2.0 2.0 2.0 2 CA Calaveras 2017 null null null null null null null null null null 0.052957 0.109 0.089 0.015065 0.091 null null null null null null null null null null null null null null null 3.0 4.0 6.0 3.0 3.0 3.0 2.0 3.0 4.0 2.0 2.0 2.0 2.0 3.0 4.0 2.0 2.0 2.0 3 CA Contra Costa 2019 null null null null null 12.650939249999999 39.325 33.325 7.3735775 35.825 0.04185325 0.093 0.07650000000000001 0.0117075 0.08625 null null null null null 6.133333 25.5 25.5 3.794034 17.2 null null null null null 3.0 4.0 6.0 3.0 3.0 3.0 2.0 3.0 4.0 2.0 2.0 2.0 2.0 3.0 4.0 2.0 2.0 2.0 4 CA Lake 2016 null null null null null null null null null null 0.041474 0.068 0.065 0.008504 0.068 null null null null null null null null null null null null null null null 3.0 4.0 6.0 3.0 3.0 3.0 2.0 3.0 4.0 2.0 2.0 2.0 2.0 3.0 4.0 2.0 2.0 2.0 5 CA Santa Clara 2016 null null null null null 23.385278 51.650000000000006 46.0 9.6735115 50.25 0.04473725 0.08825000000000001 0.07775 0.01179375 0.08275 null null null null null 8.045263 22.7 22.7 3.8341620000000005 20.3 0.537047 1.8 1.6 0.381402 1.7 3.0 3.0 7.0 3.0 3.0 3.0 2.0 2.0 4.0 2.0 2.0 2.0 2.0 2.0 4.0 2.0 2.0 2.0 6 CA Los Angeles 2015 0.012373857142857143 0.036357142857142866 0.03450000000000001 0.006707142857142857 0.029857142857142863 29.4755605 73.84285714285714 62.38571428571429 12.8423125 67.30714285714286 0.05485715384615385 0.1123076923076923 0.09992307692307692 0.017254538461538464 0.1053846153846154 null null null null null 10.92832075 51.410000000000046 40.33500000000003 6.861900049999998 42.68500000000003 1.8496146666666669 21.666666666666668 8.3 1.8388513333333334 9.7 3.0 3.0 7.0 3.0 3.0 3.0 2.0 2.0 4.0 2.0 2.0 2.0 2.0 2.0 4.0 2.0 2.0 2.0 7 CA San Diego 2016 null null null null null 19.314231777777778 57.666666666666664 46.666666666666664 10.879725888888888 50.55555555555556 0.050642363636363645 0.08572727272727271 0.08072727272727272 0.01088409090909091 0.08281818181818179 null null null null null 8.451768666666668 23.533333333333328 19.866666666666664 3.427879 18.599999999999998 0.2253495 1.2 0.65 0.1548435 0.65 3.0 3.0 7.0 3.0 3.0 3.0 2.0 2.0 4.0 2.0 2.0 2.0 2.0 2.0 4.0 2.0 2.0 2.0 8 CA Riverside 2017 0.005121 0.015 0.015 0.003032 0.014 17.986095 50.11428571428571 41.8 9.269774571428572 43.857142857142854 0.0603519090909091 0.11436363636363635 0.10454545454545455 0.017974090909090912 0.11163636363636363 null null null null null 12.455024749999998 46.15 40.6 7.090440500000001 40.87500000000001 0.617355 2.5 1.9 0.414118 2.3 3.0 3.0 7.0 3.0 3.0 3.0 2.0 2.0 4.0 2.0 2.0 2.0 2.0 2.0 4.0 2.0 2.0 2.0 9 CA Orange 2016 null null null null null 26.712885999999997 64.925 58.6 13.15272775 61.525000000000006 0.0510245 0.10449999999999998 0.08925 0.01382375 0.09674999999999999 null null null null null 8.3535625 34.550000000000004 22.95 4.102276000000001 26.3 0.465903 3.3 2.1 0.496436 3.2 3.0 3.

STATE_ID COUNTY_ID COUNTY_NAME STATE_ABBR STATE_NAME 1 3109 Big Horn MT Montana 1 2975 Petroleum MT Montana 1 2953 Granite MT Montana 1 2924 Carter MT Montana 1 2832 Rosebud MT Montana 1 2770 Flathead MT Montana 1 2639 Daniels MT Montana 1 2568 Deer Lodge MT Montana 1 2498 Ravalli MT Montana 1 2497 McCone MT Montana 1 2409 Valley MT Montana 1 2378 Blaine MT Montana 1 2363 Beaverhead MT Montana 1 2307 Sanders MT Montana 1 2306 Dawson MT Montana 1 2287 Richland MT Montana 1 2272 Lake MT Montana 1 2158 Musselshell MT Montana 1 2126 Fallon MT Montana 1 2094 Judith Basin MT Montana 1 2074 Gallatin MT Montana 1 2014 Meagher MT Montana 1 1978 Madison MT Montana 1 1812 Cascade MT Montana 1 1707 Yellowstone MT Montana 1 1689 Toole MT Montana 1 1582 Prairie MT Montana 1 1557 Pondera MT Montana 1 1533 Custer MT Montana 1 1456 Jefferson MT Montana 1 1398 Liberty MT Montana 1 1374 Powder River MT Montana 1 1279 Chouteau MT Montana 1 1171 Broadwater MT Montana 1 1133 Sweet Grass MT Montana 1 1008 Powell MT Montana 1 951 Wheatland MT Montana 1 806 Phillips MT Montana 1 678 Golden Valley MT Montana 1 644 Glacier MT Montana 1 627 Fergus MT Montana 1 610 Missoula MT Montana 1 559 Mineral MT Montana 1 487 Lincoln MT Montana 1 467 Roosevelt MT Montana 1 359 Garfield MT Montana 1 357 Treasure MT Montana 1 323 Wibaux MT Montana 1 230 Park MT Montana 1 211 Stillwater MT Montana 1 182 Lewis and Clark MT Montana 1 167 Sheridan MT Montana 1 142 Carbon MT Montana 1 141 Hill MT Montana 1 116 Teton MT Montana 1 37 Silver Bow MT Montana 2 3092 Currituck NC North Carolina 2 2999 Mitchell NC North Carolina 2 2998 Durham NC North Carolina 2 2974 Beaufort NC North Carolina 2 2925 Duplin NC North Carolina 2 2908 Davidson NC North Carolina 2 2810 Greene NC North Carolina 2 2785 Alleghany NC North Carolina 2 2769 Guilford NC North Carolina 2 2731 Yancey NC North Carolina 2 2714 McDowell NC North Carolina 2 2692 Caswell NC North Carolina 2 2691 Columbus NC North Carolina 2 2672 Transylvania NC North Carolina 2 2671 Madison NC North Carolina 2 2638 Hertford NC North Carolina 2 2597 Cherokee NC North Carolina 2 2587 Randolph NC North Carolina 2 2585 Northampton NC North Carolina 2 2520 Franklin NC North Carolina 2 2501 Stanly NC North Carolina 2 2482 Wilson NC North Carolina 2 2448 Graham NC North Carolina 2 2408 Orange NC North Carolina 2 2377 Gaston NC North Carolina 2 2285 Hyde NC North Carolina 2 2193 Burke NC North Carolina 2 2110 Pender NC North Carolina 2 2092 Clay NC North Carolina 2 2041 Scotland NC North Carolina 2 2003 Alamance NC North Carolina 2 1980 Montgomery NC North Carolina 2 1979 Cumberland NC North Carolina 2 1964 Onslow NC North Carolina 2 1934 Forsyth NC North Carolina 2 1849 Warren NC North Carolina 2 1811 Catawba NC North Carolina 2 1784 Carteret NC North Carolina 2 1730 Lincoln NC North Carolina 2 1712 Vance NC North Carolina 2 1708 Moore NC North Carolina 2 1688 Bladen NC North Carolina 2 1687 Gates NC North Carolina 2 1670 Martin NC North Carolina 2 1649 Harnett NC North Carolina 2 1635 Caldwell NC North Carolina 2 1634 Alexander NC North Carolina 2 1568 Davie NC North Carolina 2 1545 Person NC North Carolina 2 1519 Perquimans NC North Carolina 2 1505 Surry NC North Carolina 2 1479 New Hanover NC North Carolina 2 1438 Camden NC North Carolina 2 1390 Mecklenburg NC North Carolina 2 1246 Pasquotank NC North Carolina 2 1104 Yadkin NC North Carolina 2 1089 Lenoir NC North Carolina 2 1069 Wayne NC North Carolina 2 1057 Lee NC North Carolina 2 1045 Dare NC North Carolina 2 994 Pitt NC North Carolina 2 960 Edgecombe NC North Carolina 2 917 Chatham NC North Carolina 2 904 Stokes NC North Carolina 2 901 Swain NC North Carolina 2 851 Avery NC North Carolina 2 836 Rutherford NC North Carolina 2 818 Wake NC North Carolina 2 816 Macon NC North Carolina 2 792 Washington NC North Carolina 2 790 Rockingham NC North Carolina 2 788 Chowan NC North Carolina 2 746 Buncombe NC North Carolina 2 732 Haywood NC North Carolina 2 698 Tyrrell NC North Carolina 2 676

AQ_ID COUNTY_ID 1.0 862.0 2.0 809.0 3.0 65.0 4.0 46.0 5.0 603.0 6.0 1737.0 7.0 3118.0 8.0 2343.0 9.0 586.0 10.0 2491.0 11.0 603.0 12.0 224.0 13.0 2664.0 14.0 2816.0 15.0 318.0 16.0 3118.0 17.0 2778.0 18.0 2457.0 19.0 1720.0 20.0 1971.0 21.0 2490.0 22.0 1994.0 23.0 1796.0 24.0 2816.0 25.0 2457.0 26.0 2492.0 27.0 222.0 28.0 2548.0 29.0 2929.0 30.0 222.0 31.0 1797.0 32.0 152.0 33.0 134.0 34.0 1697.0 35.0 152.0 36.0 46.0 37.0 605.0 38.0 2633.0 39.0 1252.0 40.0 2548.0 41.0 2664.0 42.0 545.0 43.0 2778.0 44.0 536.0 45.0 1720.0 46.0 65.0 47.0 1349.0 48.0 1144.0 49.0 318.0 50.0 2490.0 51.0 3118.0 52.0 1737.0 53.0 318.0 54.0 1144.0 55.0 1371.0 56.0 2548.0 57.0 3048.0 58.0 822.0 59.0 1751.0 60.0 534.0 61.0 2492.0 62.0 605.0 63.0 2508.0 64.0 2491.0 65.0 224.0 66.0 1973.0 67.0 3005.0 68.0 1973.0 69.0 1751.0 70.0 1371.0 71.0 152.0 72.0 1371.0 73.0 843.0 74.0 1697.0 75.0 134.0 76.0 2929.0 77.0 2491.0 78.0 2490.0 79.0 2816.0 80.0 318.0 81.0 2490.0 82.0 1971.0 83.0 536.0 84.0 2548.0 85.0 603.0 86.0 1144.0 87.0 1971.0 88.0 534.0 89.0 2590.0 90.0 2343.0 91.0 2778.0 92.0 2929.0 93.0 2492.0 94.0 822.0 95.0 2492.0 96.0 1751.0 97.0 2590.0 98.0 822.0 99.0 1737.0 100.0 2590.0 101.0 318.0 102.0 1775.0 103.0 3048.0 104.0 1994.0 105.0 1252.0 106.0 545.0 107.0 586.0 108.0 2816.0 109.0 1252.0 110.0 1797.0 111.0 1796.0 112.0 1737.0 113.0 224.0 114.0 2343.0 115.0 1971.0 116.0 65.0 117.0 1797.0 118.0 809.0 119.0 2490.0 120.0 152.0 121.0 134.0 122.0 809.0 123.0 1751.0 124.0 1144.0 125.0 1697.0 126.0 222.0 127.0 605.0 128.0 2778.0 129.0 3118.0 130.0 2508.0 131.0 2633.0 132.0 586.0 133.0 1973.0 134.0 862.0 135.0 1406.0 136.0 2457.0 137.0 3085.0 138.0 603.0 139.0 1751.0 140.0 545.0 141.0 1113.0 142.0 65.0 143.0 222.0 144.0 843.0 145.0 1349.0 146.0 2343.0 147.0 1144.0 148.0 1973.0 149.0 2457.0 150.0 862.0 151.0 2633.0 152.0 2457.0 153.0 1349.0 154.0 536.0 155.0 822.0 156.0 1720.0 157.0 1971.0 158.0 1252.0 159.0 2590.0 160.0 534.0 161.0 1697.0 162.0 603.0 163.0 1349.0 164.0 822.0 165.0 1796.0 166.0 1994.0 167.0 586.0 168.0 534.0 169.0 134.0 170.0 809.0 171.0 1994.0 172.0 2492.0 173.0 224.0 174.0 1775.0 175.0 224.0 176.0 1720.0 177.0 46.0 178.0 1775.0 179.0 1113.0 180.0 843.0 181.0 2816.0 182.0 3005.0 183.0 534.0 184.0 2508.0 185.0 1113.0 186.0 843.0 187.0 2664.0 188.0 1775.0 189.0 862.0 190.0 1994.0 191.0 843.0 192.0 586.0 193.0 1406.0 194.0 1796.0 195.0 134.0 196.0 1252.0 197.0 1796.0 198.0 46.0 199.0 2664.0 200.0 2633.0 201.0 2929.0 202.0 2508.0 203.0 3005.0 204.0 2491.0 205.0 545.0 206.0 1797.0 207.0 809.0 208.0 65.0 209.0 1406.0 210.0 545.0 211.0 2508.0 212.0 3085.0 213.0 1720.0 214.0 1371.0 215.0 222.0 216.0 3085.0 217.0 536.0 218.0 46.0 219.0 3118.0 220.0 1371.0 221.0 3005.0 222.0 3005.0 223.0 3085.0 224.0 2929.0 225.0 1697.0 226.0 2548.0 227.0 536.0 228.0 3085.0 229.0 1406.0 230.0 1737.0 231.0 2633.0 232.0 605.0 233.0 862.0 234.0 1406.0 235.0 2343.0 236.0 605.0 237.0 1349.0 238.0 2491.0 239.0 2664.0 240.0 2590.0 241.0 1113.0 242.0 2778.0 243.0 1775.0 244.0 1113.0 245.0 1797.0 246.0 152.0 247.0 1973.0

AQ_ID state county year LEAD_MEAN LEAD_1STMAX LEAD_99PERC LEAD_STD LEAD_2NDMAX NO2_MEAN NO2_1STMAX NO2_99PERC NO2_STD NO2_2NDMAX OZONE_MEAN OZONE_1STMAX OZONE_99PERC OZONE_STD OZONE_2NDMAX PM10_MEAN PM10_1STMAX PM10_99PERC PM10_STD PM10_2NDMAX PM25_MEAN PM25_1STMAX PM25_99PERC PM25_STD PM25_2NDMAX SO2_MEAN SO2_1STMAX SO2_99PERC SO2_STD SO2_2NDMAX LEAD_METHOD_ID NO2_METHOD_ID OZONE_METHOD_ID PM10_METHOD_ID PM25_METHOD_ID SO2_METHOD_ID LEAD_METRIC_ID NO2_METRIC_ID OZONE_METRIC_ID PM10_METRIC_ID PM25_METRIC_ID SO2_METRIC_ID LEAD_UNITS_ID NO2_UNITS_ID OZONE_UNITS_ID PM10_UNITS_ID PM25_UNITS_ID SO2_UNITS_ID COUNTY_ID 1 CA Sonoma 2018 null null null null null 10.831921 65.1 45.0 8.739281 56.4 0.0379805 0.073 0.0615 0.009461500000000001 0.0675 null null null null null null null null null null null null null null null 3.0 4.0 6.0 3.0 3.0 3.0 2.0 3.0 4.0 2.0 2.0 2.0 2.0 3.0 4.0 2.0 2.0 2.0 862.0 2 CA Stanislaus 2015 null null null null null 18.95788 42.0 38.0 8.758836 38.0 0.051584 0.112 0.0955 0.018962 0.1 32.051724 76.0 76.0 15.31359 64.0 null null null null null null null null null null 3.0 4.0 6.0 3.0 3.0 3.0 2.0 3.0 4.0 2.0 2.0 2.0 2.0 3.0 4.0 2.0 2.0 2.0 809.0 3 CA Calaveras 2017 null null null null null null null null null null 0.052957 0.109 0.089 0.015065 0.091 null null null null null null null null null null null null null null null 3.0 4.0 6.0 3.0 3.0 3.0 2.0 3.0 4.0 2.0 2.0 2.0 2.0 3.0 4.0 2.0 2.0 2.0 65.0 4 CA Contra Costa 2019 null null null null null 12.650939249999999 39.325 33.325 7.3735775 35.825 0.04185325 0.093 0.07650000000000001 0.0117075 0.08625 null null null null null 6.133333 25.5 25.5 3.794034 17.2 null null null null null 3.0 4.0 6.0 3.0 3.0 3.0 2.0 3.0 4.0 2.0 2.0 2.0 2.0 3.0 4.0 2.0 2.0 2.0 46.0 5 CA Lake 2016 null null null null null null null null null null 0.041474 0.068 0.065 0.008504 0.068 null null null null null null null null null null null null null null null 3.0 4.0 6.0 3.0 3.0 3.0 2.0 3.0 4.0 2.0 2.0 2.0 2.0 3.0 4.0 2.0 2.0 2.0 603.0 6 CA Santa Clara 2016 null null null null null 23.385278 51.650000000000006 46.0 9.6735115 50.25 0.04473725 0.08825000000000001 0.07775 0.01179375 0.08275 null null null null null 8.045263 22.7 22.7 3.8341620000000005 20.3 0.537047 1.8 1.6 0.381402 1.7 3.0 3.0 7.0 3.0 3.0 3.0 2.0 2.0 4.0 2.0 2.0 2.0 2.0 2.0 4.0 2.0 2.0 2.0 1737.0 7 CA Los Angeles 2015 0.012373857142857143 0.036357142857142866 0.03450000000000001 0.006707142857142857 0.029857142857142863 29.4755605 73.84285714285714 62.38571428571429 12.8423125 67.30714285714286 0.05485715384615385 0.1123076923076923 0.09992307692307692 0.017254538461538464 0.1053846153846154 null null null null null 10.92832075 51.410000000000046 40.33500000000003 6.861900049999998 42.68500000000003 1.8496146666666669 21.666666666666668 8.3 1.8388513333333334 9.7 3.0 3.0 7.0 3.0 3.0 3.0 2.0 2.0 4.0 2.0 2.0 2.0 2.0 2.0 4.0 2.0 2.0 2.0 3118.0 8 CA San Diego 2016 null null null null null 19.314231777777778 57.666666666666664 46.666666666666664 10.879725888888888 50.55555555555556 0.050642363636363645 0.08572727272727271 0.08072727272727272 0.01088409090909091 0.08281818181818179 null null null null null 8.451768666666668 23.533333333333328 19.866666666666664 3.427879 18.599999999999998 0.2253495 1.2 0.65 0.1548435 0.65 3.0 3.0 7.0 3.0 3.0 3.0 2.0 2.0 4.0 2.0 2.0 2.0 2.0 2.0 4.0 2.0 2.0 2.0 2343.0 9 CA Riverside 2017 0.005121 0.015 0.015 0.003032 0.014 17.986095 50.11428571428571 41.8 9.269774571428572 43.857142857142854 0.0603519090909091 0.11436363636363635 0.10454545454545455 0.017974090909090912 0.11163636363636363 null null null null null 12.455024749999998 46.15 40.6 7.090440500000001 40.87500000000001 0.617355 2.5 1.9 0.414118 2.3 3.0 3.0 7.0 3.0 3.0 3.0 2.0 2.0 4.0 2.0 2.0 2.0 2.0 2.0 4.0 2.0 2.0 2.0 586.0 10 CA Orange 2016 null null null null null 26.712885999999997 64.925 58.6 13.15272775 61.525000000000006 0.0510245 0.10449999999999998 0.08925 0.01382375 0.09674999999999999 null null null null null 8.3535625 34.5500000000000

AQ_ID state county year LEAD_MEAN LEAD_1STMAX LEAD_99PERC LEAD_STD LEAD_2NDMAX NO2_MEAN NO2_1STMAX NO2_99PERC NO2_STD NO2_2NDMAX OZONE_MEAN OZONE_1STMAX OZONE_99PERC OZONE_STD OZONE_2NDMAX PM10_MEAN PM10_1STMAX PM10_99PERC PM10_STD PM10_2NDMAX PM25_MEAN PM25_1STMAX PM25_99PERC PM25_STD PM25_2NDMAX SO2_MEAN SO2_1STMAX SO2_99PERC SO2_STD SO2_2NDMAX LEAD_METHOD_ID NO2_METHOD_ID OZONE_METHOD_ID PM10_METHOD_ID PM25_METHOD_ID SO2_METHOD_ID LEAD_METRIC_ID NO2_METRIC_ID OZONE_METRIC_ID PM10_METRIC_ID PM25_METRIC_ID SO2_METRIC_ID LEAD_UNITS_ID NO2_UNITS_ID OZONE_UNITS_ID PM10_UNITS_ID PM25_UNITS_ID SO2_UNITS_ID COUNTY_ID 1 CA Sonoma 2018 null null null null null 10.831921 65.1 45.0 8.739281 56.4 0.0379805 0.073 0.0615 0.009461500000000001 0.0675 null null null null null null null null null null null null null null null 3.0 4.0 6.0 3.0 3.0 3.0 2.0 3.0 4.0 2.0 2.0 2.0 2.0 3.0 4.0 2.0 2.0 2.0 862.0 2 CA Stanislaus 2015 null null null null null 18.95788 42.0 38.0 8.758836 38.0 0.051584 0.112 0.0955 0.018962 0.1 32.051724 76.0 76.0 15.31359 64.0 null null null null null null null null null null 3.0 4.0 6.0 3.0 3.0 3.0 2.0 3.0 4.0 2.0 2.0 2.0 2.0 3.0 4.0 2.0 2.0 2.0 809.0 3 CA Calaveras 2017 null null null null null null null null null null 0.052957 0.109 0.089 0.015065 0.091 null null null null null null null null null null null null null null null 3.0 4.0 6.0 3.0 3.0 3.0 2.0 3.0 4.0 2.0 2.0 2.0 2.0 3.0 4.0 2.0 2.0 2.0 65.0 4 CA Contra Costa 2019 null null null null null 12.650939249999999 39.325 33.325 7.3735775 35.825 0.04185325 0.093 0.07650000000000001 0.0117075 0.08625 null null null null null 6.133333 25.5 25.5 3.794034 17.2 null null null null null 3.0 4.0 6.0 3.0 3.0 3.0 2.0 3.0 4.0 2.0 2.0 2.0 2.0 3.0 4.0 2.0 2.0 2.0 46.0 5 CA Lake 2016 null null null null null null null null null null 0.041474 0.068 0.065 0.008504 0.068 null null null null null null null null null null null null null null null 3.0 4.0 6.0 3.0 3.0 3.0 2.0 3.0 4.0 2.0 2.0 2.0 2.0 3.0 4.0 2.0 2.0 2.0 603.0 6 CA Santa Clara 2016 null null null null null 23.385278 51.650000000000006 46.0 9.6735115 50.25 0.04473725 0.08825000000000001 0.07775 0.01179375 0.08275 null null null null null 8.045263 22.7 22.7 3.8341620000000005 20.3 0.537047 1.8 1.6 0.381402 1.7 3.0 3.0 7.0 3.0 3.0 3.0 2.0 2.0 4.0 2.0 2.0 2.0 2.0 2.0 4.0 2.0 2.0 2.0 1737.0 7 CA Los Angeles 2015 0.012373857142857143 0.036357142857142866 0.03450000000000001 0.006707142857142857 0.029857142857142863 29.4755605 73.84285714285714 62.38571428571429 12.8423125 67.30714285714286 0.05485715384615385 0.1123076923076923 0.09992307692307692 0.017254538461538464 0.1053846153846154 null null null null null 10.92832075 51.410000000000046 40.33500000000003 6.861900049999998 42.68500000000003 1.8496146666666669 21.666666666666668 8.3 1.8388513333333334 9.7 3.0 3.0 7.0 3.0 3.0 3.0 2.0 2.0 4.0 2.0 2.0 2.0 2.0 2.0 4.0 2.0 2.0 2.0 3118.0 8 CA San Diego 2016 null null null null null 19.314231777777778 57.666666666666664 46.666666666666664 10.879725888888888 50.55555555555556 0.050642363636363645 0.08572727272727271 0.08072727272727272 0.01088409090909091 0.08281818181818179 null null null null null 8.451768666666668 23.533333333333328 19.866666666666664 3.427879 18.599999999999998 0.2253495 1.2 0.65 0.1548435 0.65 3.0 3.0 7.0 3.0 3.0 3.0 2.0 2.0 4.0 2.0 2.0 2.0 2.0 2.0 4.0 2.0 2.0 2.0 2343.0 9 CA Riverside 2017 0.005121 0.015 0.015 0.003032 0.014 17.986095 50.11428571428571 41.8 9.269774571428572 43.857142857142854 0.0603519090909091 0.11436363636363635 0.10454545454545455 0.017974090909090912 0.11163636363636363 null null null null null 12.455024749999998 46.15 40.6 7.090440500000001 40.87500000000001 0.617355 2.5 1.9 0.414118 2.3 3.0 3.0 7.0 3.0 3.0 3.0 2.0 2.0 4.0 2.0 2.0 2.0 2.0 2.0 4.0 2.0 2.0 2.0 586.0 10 CA Orange 2016 null null null null null 26.712885999999997 64.925 58.6 13.15272775 61.525000000000006 0.0510245 0.10449999999999998 0.08925 0.01382375 0.09674999999999999 null null null null null 8.3535625 34.5500000000000

False

In [0]:
AQIDFAgg2 = AQIDFAgg2.drop('state','county', 'AQ_ID')

Write the AQ data to the SQL database

In [0]:
print(AQIDFAgg2.printSchema())
from pyspark.sql.types import LongType
AQIDFAgg3 = AQIDFAgg2.withColumn("COUNTY_ID", AQIDFAgg2["COUNTY_ID"].cast(LongType()))
print(AQIDFAgg3.printSchema())

root
-- year: long (nullable = true)
-- LEAD_MEAN: double (nullable = true)
-- LEAD_1STMAX: double (nullable = true)
-- LEAD_99PERC: double (nullable = true)
-- LEAD_STD: double (nullable = true)
-- LEAD_2NDMAX: double (nullable = true)
-- NO2_MEAN: double (nullable = true)
-- NO2_1STMAX: double (nullable = true)
-- NO2_99PERC: double (nullable = true)
-- NO2_STD: double (nullable = true)
-- NO2_2NDMAX: double (nullable = true)
-- OZONE_MEAN: double (nullable = true)
-- OZONE_1STMAX: double (nullable = true)
-- OZONE_99PERC: double (nullable = true)
-- OZONE_STD: double (nullable = true)
-- OZONE_2NDMAX: double (nullable = true)
-- PM10_MEAN: double (nullable = true)
-- PM10_1STMAX: double (nullable = true)
-- PM10_99PERC: double (nullable = true)
-- PM10_STD: double (nullable = true)
-- PM10_2NDMAX: double (nullable = true)
-- PM25_MEAN: double (nullable = true)
-- PM25_1STMAX: double (nullable = true)
-- PM25_99PERC: double (nullable = true)
-- PM25_STD: double (nullable = true)
-- PM25_2NDMAX: double (nullable = true)
-- SO2_MEAN: double (nullable = true)
-- SO2_1STMAX: double (nullable = true)
-- SO2_99PERC: double (nullable = true)
-- SO2_STD: double (nullable = true)
-- SO2_2NDMAX: double (nullable = true)
-- LEAD_METHOD_ID: double (nullable = true)
-- NO2_METHOD_ID: double (nullable = true)
-- OZONE_METHOD_ID: double (nullable = true)
-- PM10_METHOD_ID: double (nullable = true)
-- PM25_METHOD_ID: double (nullable = true)
-- SO2_METHOD_ID: double (nullable = true)
-- LEAD_METRIC_ID: double (nullable = true)
-- NO2_METRIC_ID: double (nullable = true)
-- OZONE_METRIC_ID: double (nullable = true)
-- PM10_METRIC_ID: double (nullable = true)
-- PM25_METRIC_ID: double (nullable = true)
-- SO2_METRIC_ID: double (nullable = true)
-- LEAD_UNITS_ID: double (nullable = true)
-- NO2_UNITS_ID: double (nullable = true)
-- OZONE_UNITS_ID: double (nullable = true)
-- PM10_UNITS_ID: double (nullable = true)
-- PM25_UNITS_ID: double (nullable = true)
-- SO2_UNITS_ID: double (nullable = true)
-- COUNTY_ID: double (nullable = true)

None
root
-- year: long (nullable = true)
-- LEAD_MEAN: double (nullable = true)
-- LEAD_1STMAX: double (nullable = true)
-- LEAD_99PERC: double (nullable = true)
-- LEAD_STD: double (nullable = true)
-- LEAD_2NDMAX: double (nullable = true)
-- NO2_MEAN: double (nullable = true)
-- NO2_1STMAX: double (nullable = true)
-- NO2_99PERC: double (nullable = true)
-- NO2_STD: double (nullable = true)
-- NO2_2NDMAX: double (nullable = true)
-- OZONE_MEAN: double (nullable = true)
-- OZONE_1STMAX: double (nullable = true)
-- OZONE_99PERC: double (nullable = true)
-- OZONE_STD: double (nullable = true)
-- OZONE_2NDMAX: double (nullable = true)
-- PM10_MEAN: double (nullable = true)
-- PM10_1STMAX: double (nullable = true)
-- PM10_99PERC: double (nullable = true)
-- PM10_STD: double (nullable = true)
-- PM10_2NDMAX: double (nullable = true)
-- PM25_MEAN: double (nullable = true)
-- PM25_1STMAX: double (nullable = true)
-- PM25_99PERC: double (nullable = true)
-- PM25_STD: double (nullable = true)
-- PM25_2NDMAX: double (nullable = true)
-- SO2_MEAN: double (nullable = true)
-- SO2_1STMAX: double (nullable = true)
-- SO2_99PERC: double (nullable = true)
-- SO2_STD: double (nullable = true)
-- SO2_2NDMAX: double (nullable = true)
-- LEAD_METHOD_ID: double (nullable = true)
-- NO2_METHOD_ID: double (nullable = true)
-- OZONE_METHOD_ID: double (nullable = true)
-- PM10_METHOD_ID: double (nullable = true)
-- PM25_METHOD_ID: double (nullable = true)
-- SO2_METHOD_ID: double (nullable = true)
-- LEAD_METRIC_ID: double (nullable = true)
-- NO2_METRIC_ID: double (nullable = true)
-- OZONE_METRIC_ID: double (nullable = true)
-- PM10_METRIC_ID: double (nullable = true)
-- PM25_METRIC_ID: double (nullable = true)
-- SO2_METRIC_ID: double (nullable = true)
-- LEAD_UNITS_ID: double (nullable = true)
-- NO2_UNITS_ID: double (nullable = true)
-- OZONE_UNITS_ID: double (nullable = true)
-- PM10_UNITS_ID: double (nullable = true)
-- PM25_UN

In [0]:
# Copy schema from database and make DataFrame with that schema

# Load in database
df_loaded = spark.read.format("jdbc") \
    .option("url", url) \
    .option("dbtable", "AirQualityDataCounty") \
    .option("user", user) \
    .option("password", password) \
    .option("driver", "com.microsoft.sqlserver.jdbc.SQLServerDriver") \
    .load()
df_loaded = df_loaded.drop("AQ_ID") # We don't need the IDs

print(df_loaded.printSchema())
print(AQIDFAgg2.printSchema())
# Reorder columns to match order from database
AQIDFAgg2 = AQIDFAgg2.select("COUNTY_ID", "year",
                             "LEAD_MEAN", "LEAD_1STMAX", "LEAD_99PERC", "LEAD_STD",
                             "LEAD_2NDMAX","LEAD_METHOD_ID","LEAD_METRIC_ID","LEAD_UNITS_ID",
                             "NO2_MEAN", "NO2_1STMAX", "NO2_99PERC", "NO2_STD",
                             "NO2_2NDMAX", "NO2_METHOD_ID","NO2_METRIC_ID","NO2_UNITS_ID",
                             "OZONE_MEAN", "OZONE_1STMAX", "OZONE_99PERC", "OZONE_STD",
                             "OZONE_2NDMAX", "OZONE_METHOD_ID","OZONE_METRIC_ID","OZONE_UNITS_ID", 
                             "PM10_MEAN", "PM10_1STMAX", "PM10_99PERC", "PM10_STD",
                             "PM10_2NDMAX", "PM10_METHOD_ID","PM10_METRIC_ID","PM10_UNITS_ID",
                             "PM25_MEAN", "PM25_1STMAX", "PM25_99PERC", "PM25_STD", 
                             "PM25_2NDMAX", "PM25_METHOD_ID","PM25_METRIC_ID","PM25_UNITS_ID",
                             "SO2_MEAN", "SO2_1STMAX", "SO2_99PERC", "SO2_STD",
                             "SO2_2NDMAX", "SO2_METHOD_ID","SO2_METRIC_ID","SO2_UNITS_ID")

AQIDFAgg2 = AQIDFAgg2.withColumnRenamed("year","YEAR")
AQIDFAgg2 = AQIDFAgg2.withColumn("COUNTY_ID", AQIDFAgg2.COUNTY_ID.cast("integer"))   

AQIDFAgg2 = AQIDFAgg2.withColumn("LEAD_METHOD_ID", AQIDFAgg2.LEAD_METHOD_ID.cast("integer"))   
AQIDFAgg2 = AQIDFAgg2.withColumn("NO2_METHOD_ID", AQIDFAgg2.NO2_METHOD_ID.cast("integer"))    
AQIDFAgg2 = AQIDFAgg2.withColumn("OZONE_METHOD_ID", AQIDFAgg2.OZONE_METHOD_ID.cast("integer"))    
AQIDFAgg2 = AQIDFAgg2.withColumn("PM10_METHOD_ID", AQIDFAgg2.PM10_METHOD_ID.cast("integer"))    
AQIDFAgg2 = AQIDFAgg2.withColumn("PM25_METHOD_ID", AQIDFAgg2.PM25_METHOD_ID.cast("integer"))    
AQIDFAgg2 = AQIDFAgg2.withColumn("SO2_METHOD_ID", AQIDFAgg2.SO2_METHOD_ID.cast("integer")) 

AQIDFAgg2 = AQIDFAgg2.withColumn("LEAD_METRIC_ID", AQIDFAgg2.LEAD_METRIC_ID.cast("integer"))   
AQIDFAgg2 = AQIDFAgg2.withColumn("NO2_METRIC_ID", AQIDFAgg2.NO2_METRIC_ID.cast("integer"))    
AQIDFAgg2 = AQIDFAgg2.withColumn("OZONE_METRIC_ID", AQIDFAgg2.OZONE_METRIC_ID.cast("integer"))    
AQIDFAgg2 = AQIDFAgg2.withColumn("PM10_METRIC_ID", AQIDFAgg2.PM10_METRIC_ID.cast("integer"))    
AQIDFAgg2 = AQIDFAgg2.withColumn("PM25_METRIC_ID", AQIDFAgg2.PM25_METRIC_ID.cast("integer"))    
AQIDFAgg2 = AQIDFAgg2.withColumn("SO2_METRIC_ID", AQIDFAgg2.SO2_METRIC_ID.cast("integer")) 

AQIDFAgg2 = AQIDFAgg2.withColumn("LEAD_UNITS_ID", AQIDFAgg2.LEAD_UNITS_ID.cast("integer"))   
AQIDFAgg2 = AQIDFAgg2.withColumn("NO2_UNITS_ID", AQIDFAgg2.NO2_UNITS_ID.cast("integer"))    
AQIDFAgg2 = AQIDFAgg2.withColumn("OZONE_UNITS_ID", AQIDFAgg2.OZONE_UNITS_ID.cast("integer"))    
AQIDFAgg2 = AQIDFAgg2.withColumn("PM10_UNITS_ID", AQIDFAgg2.PM10_UNITS_ID.cast("integer"))    
AQIDFAgg2 = AQIDFAgg2.withColumn("PM25_UNITS_ID", AQIDFAgg2.PM25_UNITS_ID.cast("integer"))    
AQIDFAgg2 = AQIDFAgg2.withColumn("SO2_UNITS_ID", AQIDFAgg2.SO2_UNITS_ID.cast("integer")) 

try:
    AQIDFAgg3 = sqlContext.createDataFrame(AQIDFAgg2.rdd, df_loaded.schema)
    display(AQIDFAgg3)
except Exception as e:
    print(f"SCHEMA: {e}")

root
-- COUNTY_ID: integer (nullable = true)
-- YEAR: integer (nullable = true)
-- LEAD_MEAN: double (nullable = true)
-- LEAD_1STMAX: double (nullable = true)
-- LEAD_99PERC: double (nullable = true)
-- LEAD_STD: double (nullable = true)
-- LEAD_2NDMAX: double (nullable = true)
-- LEAD_METHOD_ID: integer (nullable = true)
-- LEAD_METRIC_ID: integer (nullable = true)
-- LEAD_UNITS_ID: integer (nullable = true)
-- NO2_MEAN: double (nullable = true)
-- NO2_1STMAX: double (nullable = true)
-- NO2_99PERC: double (nullable = true)
-- NO2_STD: double (nullable = true)
-- NO2_2NDMAX: double (nullable = true)
-- NO2_METHOD_ID: integer (nullable = true)
-- NO2_METRIC_ID: integer (nullable = true)
-- NO2_UNITS_ID: integer (nullable = true)
-- OZONE_MEAN: double (nullable = true)
-- OZONE_1STMAX: double (nullable = true)
-- OZONE_99PERC: double (nullable = true)
-- OZONE_STD: double (nullable = true)
-- OZONE_2NDMAX: double (nullable = true)
-- OZONE_METHOD_ID: integer (nullable = true)
-- OZONE_METRIC_ID: integer (nullable = true)
-- OZONE_UNITS_ID: integer (nullable = true)
-- PM10_MEAN: double (nullable = true)
-- PM10_1STMAX: double (nullable = true)
-- PM10_99PERC: double (nullable = true)
-- PM10_STD: double (nullable = true)
-- PM10_2NDMAX: double (nullable = true)
-- PM10_METHOD_ID: integer (nullable = true)
-- PM10_METRIC_ID: integer (nullable = true)
-- PM10_UNITS_ID: integer (nullable = true)
-- PM25_MEAN: double (nullable = true)
-- PM25_1STMAX: double (nullable = true)
-- PM25_99PERC: double (nullable = true)
-- PM25_STD: double (nullable = true)
-- PM25_2NDMAX: double (nullable = true)
-- PM25_METHOD_ID: integer (nullable = true)
-- PM25_METRIC_ID: integer (nullable = true)
-- PM25_UNITS_ID: integer (nullable = true)
-- SO2_MEAN: double (nullable = true)
-- SO2_1STMAX: double (nullable = true)
-- SO2_99PERC: double (nullable = true)
-- SO2_STD: double (nullable = true)
-- SO2_2NDMAX: double (nullable = true)
-- SO2_METHOD_ID: integer (nullable = true)
-- SO2_METRIC_ID: integer (nullable = true)
-- SO2_UNITS_ID: integer (nullable = true)

None
root
-- year: long (nullable = true)
-- LEAD_MEAN: double (nullable = true)
-- LEAD_1STMAX: double (nullable = true)
-- LEAD_99PERC: double (nullable = true)
-- LEAD_STD: double (nullable = true)
-- LEAD_2NDMAX: double (nullable = true)
-- NO2_MEAN: double (nullable = true)
-- NO2_1STMAX: double (nullable = true)
-- NO2_99PERC: double (nullable = true)
-- NO2_STD: double (nullable = true)
-- NO2_2NDMAX: double (nullable = true)
-- OZONE_MEAN: double (nullable = true)
-- OZONE_1STMAX: double (nullable = true)
-- OZONE_99PERC: double (nullable = true)
-- OZONE_STD: double (nullable = true)
-- OZONE_2NDMAX: double (nullable = true)
-- PM10_MEAN: double (nullable = true)
-- PM10_1STMAX: double (nullable = true)
-- PM10_99PERC: double (nullable = true)
-- PM10_STD: double (nullable = true)
-- PM10_2NDMAX: double (nullable = true)
-- PM25_MEAN: double (nullable = true)
-- PM25_1STMAX: double (nullable = true)
-- PM25_99PERC: double (nullable = true)
-- PM25_STD: double (nullable = true)
-- PM25_2NDMAX: double (nullable = true)
-- SO2_MEAN: double (nullable = true)
-- SO2_1STMAX: double (nullable = true)
-- SO2_99PERC: double (nullable = true)
-- SO2_STD: double (nullable = true)
-- SO2_2NDMAX: double (nullable = true)
-- LEAD_METHOD_ID: double (nullable = true)
-- NO2_METHOD_ID: double (nullable = true)
-- OZONE_METHOD_ID: double (nullable = true)
-- PM10_METHOD_ID: double (nullable = true)
-- PM25_METHOD_ID: double (nullable = true)
-- SO2_METHOD_ID: double (nullable = true)
-- LEAD_METRIC_ID: double (nullable = true)
-- NO2_METRIC_ID: double (nullable = true)
-- OZONE_METRIC_ID: double (nullable = true)
-- PM10_METRIC_ID: double (nullable = true)
-- PM25_METRIC_ID: double (nullable = true)
-- SO2_METRIC_ID: double (nullable = true)
-- LEAD_UNITS_ID: double (nullable = true)
-- NO2_UNITS_ID: double (nullable = true)
-- OZONE_UNITS_ID: double (nullable = true)
-- PM10_UNITS_ID: double (nulla

COUNTY_ID YEAR LEAD_MEAN LEAD_1STMAX LEAD_99PERC LEAD_STD LEAD_2NDMAX LEAD_METHOD_ID LEAD_METRIC_ID LEAD_UNITS_ID NO2_MEAN NO2_1STMAX NO2_99PERC NO2_STD NO2_2NDMAX NO2_METHOD_ID NO2_METRIC_ID NO2_UNITS_ID OZONE_MEAN OZONE_1STMAX OZONE_99PERC OZONE_STD OZONE_2NDMAX OZONE_METHOD_ID OZONE_METRIC_ID OZONE_UNITS_ID PM10_MEAN PM10_1STMAX PM10_99PERC PM10_STD PM10_2NDMAX PM10_METHOD_ID PM10_METRIC_ID PM10_UNITS_ID PM25_MEAN PM25_1STMAX PM25_99PERC PM25_STD PM25_2NDMAX PM25_METHOD_ID PM25_METRIC_ID PM25_UNITS_ID SO2_MEAN SO2_1STMAX SO2_99PERC SO2_STD SO2_2NDMAX SO2_METHOD_ID SO2_METRIC_ID SO2_UNITS_ID 862 2018 null null null null null 3 2 2 10.831921 65.1 45.0 8.739281 56.4 4 3 3 0.0379805 0.073 0.0615 0.009461500000000001 0.0675 6 4 4 null null null null null 3 2 2 null null null null null 3 2 2 null null null null null 3 2 2 809 2015 null null null null null 3 2 2 18.95788 42.0 38.0 8.758836 38.0 4 3 3 0.051584 0.112 0.0955 0.018962 0.1 6 4 4 32.051724 76.0 76.0 15.31359 64.0 3 2 2 null null null null null 3 2 2 null null null null null 3 2 2 65 2017 null null null null null 3 2 2 null null null null null 4 3 3 0.052957 0.109 0.089 0.015065 0.091 6 4 4 null null null null null 3 2 2 null null null null null 3 2 2 null null null null null 3 2 2 46 2019 null null null null null 3 2 2 12.650939249999999 39.325 33.325 7.3735775 35.825 4 3 3 0.04185325 0.093 0.07650000000000001 0.0117075 0.08625 6 4 4 null null null null null 3 2 2 6.133333 25.5 25.5 3.794034 17.2 3 2 2 null null null null null 3 2 2 603 2016 null null null null null 3 2 2 null null null null null 4 3 3 0.041474 0.068 0.065 0.008504 0.068 6 4 4 null null null null null 3 2 2 null null null null null 3 2 2 null null null null null 3 2 2 1737 2016 null null null null null 3 2 2 23.385278 51.650000000000006 46.0 9.6735115 50.25 3 2 2 0.04473725 0.08825000000000001 0.07775 0.01179375 0.08275 7 4 4 null null null null null 3 2 2 8.045263 22.7 22.7 3.8341620000000005 20.3 3 2 2 0.537047 1.8 1.6 0.381402 1.7 3 2 2 3118 2015 0.012373857142857143 0.036357142857142866 0.03450000000000001 0.006707142857142857 0.029857142857142863 3 2 2 29.4755605 73.84285714285714 62.38571428571429 12.8423125 67.30714285714286 3 2 2 0.05485715384615385 0.1123076923076923 0.09992307692307692 0.017254538461538464 0.1053846153846154 7 4 4 null null null null null 3 2 2 10.92832075 51.410000000000046 40.33500000000003 6.861900049999998 42.68500000000003 3 2 2 1.8496146666666669 21.666666666666668 8.3 1.8388513333333334 9.7 3 2 2 2343 2016 null null null null null 3 2 2 19.314231777777778 57.666666666666664 46.666666666666664 10.879725888888888 50.55555555555556 3 2 2 0.050642363636363645 0.08572727272727271 0.08072727272727272 0.01088409090909091 0.08281818181818179 7 4 4 null null null null null 3 2 2 8.451768666666668 23.533333333333328 19.866666666666664 3.427879 18.599999999999998 3 2 2 0.2253495 1.2 0.65 0.1548435 0.65 3 2 2 586 2017 0.005121 0.015 0.015 0.003032 0.014 3 2 2 17.986095 50.11428571428571 41.8 9.269774571428572 43.857142857142854 3 2 2 0.0603519090909091 0.11436363636363635 0.10454545454545455 0.017974090909090912 0.11163636363636363 7 4 4 null null null null null 3 2 2 12.455024749999998 46.15 40.6 7.090440500000001 40.87500000000001 3 2 2 0.617355 2.5 1.9 0.414118 2.3 3 2 2 2491 2016 null null null null null 3 2 2 26.712885999999997 64.925 58.6 13.15272775 61.525000000000006 3 2 2 0.0510245 0.10449999999999998 0.08925 0.01382375 0.09674999999999999 7 4 4 null null null null null 3 2 2 8.3535625 34.550000000000004 22.95 4.102276000000001 26.3 3 2 2 0.465903 3.3 2.1 0.496436 3.2 3 2 2 603 2018 null null null null null 3 2 2 null null null null null 5 3 3 0.041084 0.08 0.064 0.009467 0.072 7 4 4 null null null null null 3 2 2 null null null null null 8 5 1 null null null null null 3 2 2 224 2018 null null null null null 3 2 2 4.3386425 34.55 15.75 3.566809 21.5 5 3 3 0.031964 0.0495 0.0465 0.006933 0.0475 7 4 4 null null null null null 3 2 2 null null null null null 8 5 1 null null nu

In [0]:
print(AQIDFAgg3.printSchema())


root
-- COUNTY_ID: integer (nullable = true)
-- YEAR: integer (nullable = true)
-- LEAD_MEAN: double (nullable = true)
-- LEAD_1STMAX: double (nullable = true)
-- LEAD_99PERC: double (nullable = true)
-- LEAD_STD: double (nullable = true)
-- LEAD_2NDMAX: double (nullable = true)
-- LEAD_METHOD_ID: integer (nullable = true)
-- LEAD_METRIC_ID: integer (nullable = true)
-- LEAD_UNITS_ID: integer (nullable = true)
-- NO2_MEAN: double (nullable = true)
-- NO2_1STMAX: double (nullable = true)
-- NO2_99PERC: double (nullable = true)
-- NO2_STD: double (nullable = true)
-- NO2_2NDMAX: double (nullable = true)
-- NO2_METHOD_ID: integer (nullable = true)
-- NO2_METRIC_ID: integer (nullable = true)
-- NO2_UNITS_ID: integer (nullable = true)
-- OZONE_MEAN: double (nullable = true)
-- OZONE_1STMAX: double (nullable = true)
-- OZONE_99PERC: double (nullable = true)
-- OZONE_STD: double (nullable = true)
-- OZONE_2NDMAX: double (nullable = true)
-- OZONE_METHOD_ID: integer (nullable = true)
-- OZONE_METRIC_ID: integer (nullable = true)
-- OZONE_UNITS_ID: integer (nullable = true)
-- PM10_MEAN: double (nullable = true)
-- PM10_1STMAX: double (nullable = true)
-- PM10_99PERC: double (nullable = true)
-- PM10_STD: double (nullable = true)
-- PM10_2NDMAX: double (nullable = true)
-- PM10_METHOD_ID: integer (nullable = true)
-- PM10_METRIC_ID: integer (nullable = true)
-- PM10_UNITS_ID: integer (nullable = true)
-- PM25_MEAN: double (nullable = true)
-- PM25_1STMAX: double (nullable = true)
-- PM25_99PERC: double (nullable = true)
-- PM25_STD: double (nullable = true)
-- PM25_2NDMAX: double (nullable = true)
-- PM25_METHOD_ID: integer (nullable = true)
-- PM25_METRIC_ID: integer (nullable = true)
-- PM25_UNITS_ID: integer (nullable = true)
-- SO2_MEAN: double (nullable = true)
-- SO2_1STMAX: double (nullable = true)
-- SO2_99PERC: double (nullable = true)
-- SO2_STD: double (nullable = true)
-- SO2_2NDMAX: double (nullable = true)
-- SO2_METHOD_ID: integer (nullable = true)
-- SO2_METRIC_ID: integer (nullable = true)
-- SO2_UNITS_ID: integer (nullable = true)

None

In [0]:
try:
    writer = AQIDFAgg3.write.format("jdbc").option("url", url) \
        .mode("append") \
        .option("dbtable", 'AirQualityDataCounty') \
        .option("user", user) \
        .option("password", password) \
        .option("driver", "com.microsoft.sqlserver.jdbc.SQLServerDriver")
    writer.save()
except Exception as e:
    print(e)

    df_loaded = spark.read.format("jdbc") \
        .option("url", url) \
        .option("dbtable", "AirQualityDataCounty") \
        .option("user", user) \
        .option("password", password) \
        .option("driver", "com.microsoft.sqlserver.jdbc.SQLServerDriver") \
        .load()
    print('df_loaded')
    display(df_loaded)   
        
    # Subtract the two to only leave what is not in the database
    # remove the index column of the loaded dataframe
    df_loaded = df_loaded.drop('AQ_ID')
    df_toload = AQIDFAgg3.subtract(df_loaded)
    print('df_toload')
    display(df_toload)
    
    if(df_toload.count() > 0):
        # Upload all the data that wasn't already in the database
        df_toload.write.format("jdbc")  \
            .option("url", url) \
            .mode("append") \
            .option("dbtable", "AirQualityDataCounty") \
            .option("user", user) \
            .option("password", password) \
            .option("driver", "com.microsoft.sqlserver.jdbc.SQLServerDriver") \
            .save()
    
AQIDFAggDF = spark.read.format("jdbc") \
    .option("url", url) \
    .option("dbtable", "AirQualityDataCounty") \
    .option("user", user) \
    .option("password", password) \
    .option("driver", "com.microsoft.sqlserver.jdbc.SQLServerDriver") \
    .load()
display(AQIDFAggDF) 

An error occurred while calling o61205.save.
: org.apache.spark.SparkException: Job aborted due to stage failure: Task 0 in stage 122464.0 failed 4 times, most recent failure: Lost task 0.3 in stage 122464.0 (TID 99007) (10.139.64.5 executor driver): java.sql.BatchUpdateException: Violation of UNIQUE KEY constraint 'uq_AirQualityDataCounty_CountyID_YEAR'. Cannot insert duplicate key in object 'dbo.AirQualityDataCounty'. The duplicate key value is (862, 2018).
	at com.microsoft.sqlserver.jdbc.SQLServerPreparedStatement.executeBatch(SQLServerPreparedStatement.java:2085)
	at org.apache.spark.sql.execution.datasources.jdbc.JdbcUtils$.savePartition(JdbcUtils.scala:731)
	at org.apache.spark.sql.execution.datasources.jdbc.JdbcUtils$.$anonfun$saveTable$1(JdbcUtils.scala:888)
	at org.apache.spark.sql.execution.datasources.jdbc.JdbcUtils$.$anonfun$saveTable$1$adapted(JdbcUtils.scala:886)
	at org.apache.spark.rdd.RDD.$anonfun$foreachPartition$2(RDD.scala:1025)
	at org.apache.spark.rdd.RDD.$anonfun$foreachPartition$2$adapted(RDD.scala:1025)
	at org.apache.spark.SparkContext.$anonfun$runJob$2(SparkContext.scala:2576)
	at org.apache.spark.scheduler.ResultTask.$anonfun$runTask$3(ResultTask.scala:75)
	at com.databricks.spark.util.ExecutorFrameProfiler$.record(ExecutorFrameProfiler.scala:110)
	at org.apache.spark.scheduler.ResultTask.$anonfun$runTask$1(ResultTask.scala:75)
	at com.databricks.spark.util.ExecutorFrameProfiler$.record(ExecutorFrameProfiler.scala:110)
	at org.apache.spark.scheduler.ResultTask.runTask(ResultTask.scala:55)
	at org.apache.spark.scheduler.Task.doRunTask(Task.scala:153)
	at org.apache.spark.scheduler.Task.$anonfun$run$1(Task.scala:122)
	at com.databricks.spark.util.ExecutorFrameProfiler$.record(ExecutorFrameProfiler.scala:110)
	at org.apache.spark.scheduler.Task.run(Task.scala:93)
	at org.apache.spark.executor.Executor$TaskRunner.$anonfun$run$13(Executor.scala:824)
	at org.apache.spark.util.Utils$.tryWithSafeFinally(Utils.scala:1621)
	at org.apache.spark.executor.Executor$TaskRunner.$anonfun$run$4(Executor.scala:827)
	at scala.runtime.java8.JFunction0$mcV$sp.apply(JFunction0$mcV$sp.java:23)
	at com.databricks.spark.util.ExecutorFrameProfiler$.record(ExecutorFrameProfiler.scala:110)
	at org.apache.spark.executor.Executor$TaskRunner.run(Executor.scala:683)
	at java.util.concurrent.ThreadPoolExecutor.runWorker(ThreadPoolExecutor.java:1149)
	at java.util.concurrent.ThreadPoolExecutor$Worker.run(ThreadPoolExecutor.java:624)
	at java.lang.Thread.run(Thread.java:748)

Driver stacktrace:
	at org.apache.spark.scheduler.DAGScheduler.failJobAndIndependentStages(DAGScheduler.scala:2973)
	at org.apache.spark.scheduler.DAGScheduler.$anonfun$abortStage$2(DAGScheduler.scala:2920)
	at org.apache.spark.scheduler.DAGScheduler.$anonfun$abortStage$2$adapted(DAGScheduler.scala:2914)
	at scala.collection.mutable.ResizableArray.foreach(ResizableArray.scala:62)
	at scala.collection.mutable.ResizableArray.foreach$(ResizableArray.scala:55)
	at scala.collection.mutable.ArrayBuffer.foreach(ArrayBuffer.scala:49)
	at org.apache.spark.scheduler.DAGScheduler.abortStage(DAGScheduler.scala:2914)
	at org.apache.spark.scheduler.DAGScheduler.$anonfun$handleTaskSetFailed$1(DAGScheduler.scala:1334)
	at org.apache.spark.scheduler.DAGScheduler.$anonfun$handleTaskSetFailed$1$adapted(DAGScheduler.scala:1334)
	at scala.Option.foreach(Option.scala:407)
	at org.apache.spark.scheduler.DAGScheduler.handleTaskSetFailed(DAGScheduler.scala:1334)
	at org.apache.spark.scheduler.DAGSchedulerEventProcessLoop.doOnReceive(DAGScheduler.scala:3182)
	at org.apache.spark.scheduler.DAGSchedulerEventProcessLoop.onReceive(DAGScheduler.scala:3123)
	at org.apache.spark.scheduler.DAGSchedulerEventProcessLoop.onReceive(DAGScheduler.scala:3111)
	at org.apache.spark.util.EventLoop$$anon$1.run(EventLoop.scala:49)
	at org.apache.spark.scheduler.DAGScheduler.runJob(DAGScheduler.scala:1096)
	at org.apache.spark.SparkContext.runJobInternal(SparkContext.scala:2536)
	at org.apache.spark.SparkCon

AQ_ID COUNTY_ID YEAR LEAD_MEAN LEAD_1STMAX LEAD_99PERC LEAD_STD LEAD_2NDMAX LEAD_METHOD_ID LEAD_METRIC_ID LEAD_UNITS_ID NO2_MEAN NO2_1STMAX NO2_99PERC NO2_STD NO2_2NDMAX NO2_METHOD_ID NO2_METRIC_ID NO2_UNITS_ID OZONE_MEAN OZONE_1STMAX OZONE_99PERC OZONE_STD OZONE_2NDMAX OZONE_METHOD_ID OZONE_METRIC_ID OZONE_UNITS_ID PM10_MEAN PM10_1STMAX PM10_99PERC PM10_STD PM10_2NDMAX PM10_METHOD_ID PM10_METRIC_ID PM10_UNITS_ID PM25_MEAN PM25_1STMAX PM25_99PERC PM25_STD PM25_2NDMAX PM25_METHOD_ID PM25_METRIC_ID PM25_UNITS_ID SO2_MEAN SO2_1STMAX SO2_99PERC SO2_STD SO2_2NDMAX SO2_METHOD_ID SO2_METRIC_ID SO2_UNITS_ID 1 1371 2021 null null null null null 3 2 2 null null null null null 3 2 2 0.054537 0.095 0.088 0.01188 0.093 6 4 4 null null null null null 3 2 2 null null null null null 3 2 2 null null null null null 3 2 2 2 714 2021 null null null null null 3 2 2 null null null null null 3 2 2 0.041595 0.089 0.0825 0.012210499999999999 0.0825 6 4 4 null null null null null 3 2 2 null null null null null 3 2 2 null null null null null 3 2 2 3 1286 2021 null null null null null 3 2 2 null null null null null 3 2 2 0.047252 0.079 0.076 0.009666 0.078 7 4 4 null null null null null 3 2 2 null null null null null 3 2 2 null null null null null 3 2 2 4 1796 2021 null null null null null 3 2 2 4.42316 13.833333333333334 11.333333333333334 2.5284210000000003 11.466666666666667 4 3 3 0.03858088888888889 0.06544444444444444 0.06122222222222221 0.006700777777777778 0.06099999999999999 6 4 4 null null null null null 3 2 2 null null null null null 3 2 2 null null null null null 3 2 2 5 1303 2021 null null null null null 3 2 2 null null null null null 3 2 2 null null null null null 3 2 2 null null null null null 3 2 2 null null null null null 3 2 2 1.8907759999999998 30.5 19.0 2.9063369999999997 19.5 9 6 3 6 3126 2021 null null null null null 3 2 2 null null null null null 3 2 2 0.0464555 0.107 0.092 0.0147595 0.0955 7 4 4 null null null null null 3 2 2 7.237862 24.95 24.0 4.3267165 24.0 8 5 1 0.9241094999999999 4.6 3.45 0.7187600000000001 4.05 9 6 3 7 2422 2021 null null null null null 3 2 2 null null null null null 3 2 2 0.043206 0.071 0.065 0.01211 0.066 7 4 4 null null null null null 3 2 2 null null null null null 3 2 2 null null null null null 3 2 2 8 921 2021 null null null null null 3 2 2 null null null null null 3 2 2 0.041337 0.07433333333333332 0.06966666666666667 0.011780333333333332 0.07133333333333335 7 4 4 null null null null null 3 2 2 null null null null null 3 2 2 null null null null null 3 2 2 9 2073 2021 null null null null null 3 2 2 9.670071400000001 29.4 23.2 4.461328399999999 24.759999999999998 4 3 3 0.051210200000000004 0.0806 0.0754 0.0098608 0.07880000000000001 6 4 4 null null null null null 3 2 2 null null null null null 3 2 2 null null null null null 3 2 2 10 1379 2021 null null null null null 3 2 2 null null null null null 3 2 2 0.05092325 0.121 0.1105 0.017247000000000002 0.116 7 4 4 null null null null null 3 2 2 7.42 25.75 25.75 5.3271945 20.3 8 5 1 0.602247 3.4 2.9 0.618568 2.9 9 6 3 11 751 2021 null null null null null 3 2 2 9.9369 40.0 33.3 6.04502 37.1 5 3 3 0.039563 0.087 0.077 0.013636 0.086 7 4 4 null null null null null 3 2 2 null null null null null 3 2 2 null null null null null 3 2 2 12 1031 2021 null null null null null 3 2 2 null null null null null 3 2 2 0.040121 0.067 0.064 0.011877 0.067 6 4 4 null null null null null 3 2 2 6.5563495 15.35 15.35 2.5102005 11.5 8 5 1 null null null null null 3 2 2 13 1363 2021 null null null null null 3 2 2 null null null null null 3 2 2 0.0444835 0.07675 0.07150000000000001 0.011167749999999999 0.07350000000000001 6 4 4 null null null null null 3 2 2 10.601328833333334 32.85 29.216666666666665 5.773344666666667 27.299999999999997 8 5 1 0.658242 6.6 2.8 0.639872 4.3 9 6 3 14 399 2021 null null null null null 3 2 2 null null null null null 3 2 2 0.04893 0.076 0.075 0.00995 0.075 6 4 4 null null null null null 3 2 2 null null null null null 3 2 2 null null null null null 3 2 2 15 3

df_toload

COUNTY_ID YEAR LEAD_MEAN LEAD_1STMAX LEAD_99PERC LEAD_STD LEAD_2NDMAX LEAD_METHOD_ID LEAD_METRIC_ID LEAD_UNITS_ID NO2_MEAN NO2_1STMAX NO2_99PERC NO2_STD NO2_2NDMAX NO2_METHOD_ID NO2_METRIC_ID NO2_UNITS_ID OZONE_MEAN OZONE_1STMAX OZONE_99PERC OZONE_STD OZONE_2NDMAX OZONE_METHOD_ID OZONE_METRIC_ID OZONE_UNITS_ID PM10_MEAN PM10_1STMAX PM10_99PERC PM10_STD PM10_2NDMAX PM10_METHOD_ID PM10_METRIC_ID PM10_UNITS_ID PM25_MEAN PM25_1STMAX PM25_99PERC PM25_STD PM25_2NDMAX PM25_METHOD_ID PM25_METRIC_ID PM25_UNITS_ID SO2_MEAN SO2_1STMAX SO2_99PERC SO2_STD SO2_2NDMAX SO2_METHOD_ID SO2_METRIC_ID SO2_UNITS_ID

AQ_ID COUNTY_ID YEAR LEAD_MEAN LEAD_1STMAX LEAD_99PERC LEAD_STD LEAD_2NDMAX LEAD_METHOD_ID LEAD_METRIC_ID LEAD_UNITS_ID NO2_MEAN NO2_1STMAX NO2_99PERC NO2_STD NO2_2NDMAX NO2_METHOD_ID NO2_METRIC_ID NO2_UNITS_ID OZONE_MEAN OZONE_1STMAX OZONE_99PERC OZONE_STD OZONE_2NDMAX OZONE_METHOD_ID OZONE_METRIC_ID OZONE_UNITS_ID PM10_MEAN PM10_1STMAX PM10_99PERC PM10_STD PM10_2NDMAX PM10_METHOD_ID PM10_METRIC_ID PM10_UNITS_ID PM25_MEAN PM25_1STMAX PM25_99PERC PM25_STD PM25_2NDMAX PM25_METHOD_ID PM25_METRIC_ID PM25_UNITS_ID SO2_MEAN SO2_1STMAX SO2_99PERC SO2_STD SO2_2NDMAX SO2_METHOD_ID SO2_METRIC_ID SO2_UNITS_ID 1 1371 2021 null null null null null 3 2 2 null null null null null 3 2 2 0.054537 0.095 0.088 0.01188 0.093 6 4 4 null null null null null 3 2 2 null null null null null 3 2 2 null null null null null 3 2 2 2 714 2021 null null null null null 3 2 2 null null null null null 3 2 2 0.041595 0.089 0.0825 0.012210499999999999 0.0825 6 4 4 null null null null null 3 2 2 null null null null null 3 2 2 null null null null null 3 2 2 3 1286 2021 null null null null null 3 2 2 null null null null null 3 2 2 0.047252 0.079 0.076 0.009666 0.078 7 4 4 null null null null null 3 2 2 null null null null null 3 2 2 null null null null null 3 2 2 4 1796 2021 null null null null null 3 2 2 4.42316 13.833333333333334 11.333333333333334 2.5284210000000003 11.466666666666667 4 3 3 0.03858088888888889 0.06544444444444444 0.06122222222222221 0.006700777777777778 0.06099999999999999 6 4 4 null null null null null 3 2 2 null null null null null 3 2 2 null null null null null 3 2 2 5 1303 2021 null null null null null 3 2 2 null null null null null 3 2 2 null null null null null 3 2 2 null null null null null 3 2 2 null null null null null 3 2 2 1.8907759999999998 30.5 19.0 2.9063369999999997 19.5 9 6 3 6 3126 2021 null null null null null 3 2 2 null null null null null 3 2 2 0.0464555 0.107 0.092 0.0147595 0.0955 7 4 4 null null null null null 3 2 2 7.237862 24.95 24.0 4.3267165 24.0 8 5 1 0.9241094999999999 4.6 3.45 0.7187600000000001 4.05 9 6 3 7 2422 2021 null null null null null 3 2 2 null null null null null 3 2 2 0.043206 0.071 0.065 0.01211 0.066 7 4 4 null null null null null 3 2 2 null null null null null 3 2 2 null null null null null 3 2 2 8 921 2021 null null null null null 3 2 2 null null null null null 3 2 2 0.041337 0.07433333333333332 0.06966666666666667 0.011780333333333332 0.07133333333333335 7 4 4 null null null null null 3 2 2 null null null null null 3 2 2 null null null null null 3 2 2 9 2073 2021 null null null null null 3 2 2 9.670071400000001 29.4 23.2 4.461328399999999 24.759999999999998 4 3 3 0.051210200000000004 0.0806 0.0754 0.0098608 0.07880000000000001 6 4 4 null null null null null 3 2 2 null null null null null 3 2 2 null null null null null 3 2 2 10 1379 2021 null null null null null 3 2 2 null null null null null 3 2 2 0.05092325 0.121 0.1105 0.017247000000000002 0.116 7 4 4 null null null null null 3 2 2 7.42 25.75 25.75 5.3271945 20.3 8 5 1 0.602247 3.4 2.9 0.618568 2.9 9 6 3 11 751 2021 null null null null null 3 2 2 9.9369 40.0 33.3 6.04502 37.1 5 3 3 0.039563 0.087 0.077 0.013636 0.086 7 4 4 null null null null null 3 2 2 null null null null null 3 2 2 null null null null null 3 2 2 12 1031 2021 null null null null null 3 2 2 null null null null null 3 2 2 0.040121 0.067 0.064 0.011877 0.067 6 4 4 null null null null null 3 2 2 6.5563495 15.35 15.35 2.5102005 11.5 8 5 1 null null null null null 3 2 2 13 1363 2021 null null null null null 3 2 2 null null null null null 3 2 2 0.0444835 0.07675 0.07150000000000001 0.011167749999999999 0.07350000000000001 6 4 4 null null null null null 3 2 2 10.601328833333334 32.85 29.216666666666665 5.773344666666667 27.299999999999997 8 5 1 0.658242 6.6 2.8 0.639872 4.3 9 6 3 14 399 2021 null null null null null 3 2 2 null null null null null 3 2 2 0.04893 0.076 0.075 0.00995 0.075 6 4 4 null null null null null 3 2 2 null null null null null 3 2 2 null null null null null 3 2 2 15 3

### 4. Add an index in the asthma dataframe referencing the matching data from the air quality dataframe

In [0]:
display(AQIDFAggDF)
display(asthmaTotalDF)

AQ_ID COUNTY_ID YEAR LEAD_MEAN LEAD_1STMAX LEAD_99PERC LEAD_STD LEAD_2NDMAX LEAD_METHOD_ID LEAD_METRIC_ID LEAD_UNITS_ID NO2_MEAN NO2_1STMAX NO2_99PERC NO2_STD NO2_2NDMAX NO2_METHOD_ID NO2_METRIC_ID NO2_UNITS_ID OZONE_MEAN OZONE_1STMAX OZONE_99PERC OZONE_STD OZONE_2NDMAX OZONE_METHOD_ID OZONE_METRIC_ID OZONE_UNITS_ID PM10_MEAN PM10_1STMAX PM10_99PERC PM10_STD PM10_2NDMAX PM10_METHOD_ID PM10_METRIC_ID PM10_UNITS_ID PM25_MEAN PM25_1STMAX PM25_99PERC PM25_STD PM25_2NDMAX PM25_METHOD_ID PM25_METRIC_ID PM25_UNITS_ID SO2_MEAN SO2_1STMAX SO2_99PERC SO2_STD SO2_2NDMAX SO2_METHOD_ID SO2_METRIC_ID SO2_UNITS_ID 1 1371 2021 null null null null null 3 2 2 null null null null null 3 2 2 0.054537 0.095 0.088 0.01188 0.093 6 4 4 null null null null null 3 2 2 null null null null null 3 2 2 null null null null null 3 2 2 2 714 2021 null null null null null 3 2 2 null null null null null 3 2 2 0.041595 0.089 0.0825 0.012210499999999999 0.0825 6 4 4 null null null null null 3 2 2 null null null null null 3 2 2 null null null null null 3 2 2 3 1286 2021 null null null null null 3 2 2 null null null null null 3 2 2 0.047252 0.079 0.076 0.009666 0.078 7 4 4 null null null null null 3 2 2 null null null null null 3 2 2 null null null null null 3 2 2 4 1796 2021 null null null null null 3 2 2 4.42316 13.833333333333334 11.333333333333334 2.5284210000000003 11.466666666666667 4 3 3 0.03858088888888889 0.06544444444444444 0.06122222222222221 0.006700777777777778 0.06099999999999999 6 4 4 null null null null null 3 2 2 null null null null null 3 2 2 null null null null null 3 2 2 5 1303 2021 null null null null null 3 2 2 null null null null null 3 2 2 null null null null null 3 2 2 null null null null null 3 2 2 null null null null null 3 2 2 1.8907759999999998 30.5 19.0 2.9063369999999997 19.5 9 6 3 6 3126 2021 null null null null null 3 2 2 null null null null null 3 2 2 0.0464555 0.107 0.092 0.0147595 0.0955 7 4 4 null null null null null 3 2 2 7.237862 24.95 24.0 4.3267165 24.0 8 5 1 0.9241094999999999 4.6 3.45 0.7187600000000001 4.05 9 6 3 7 2422 2021 null null null null null 3 2 2 null null null null null 3 2 2 0.043206 0.071 0.065 0.01211 0.066 7 4 4 null null null null null 3 2 2 null null null null null 3 2 2 null null null null null 3 2 2 8 921 2021 null null null null null 3 2 2 null null null null null 3 2 2 0.041337 0.07433333333333332 0.06966666666666667 0.011780333333333332 0.07133333333333335 7 4 4 null null null null null 3 2 2 null null null null null 3 2 2 null null null null null 3 2 2 9 2073 2021 null null null null null 3 2 2 9.670071400000001 29.4 23.2 4.461328399999999 24.759999999999998 4 3 3 0.051210200000000004 0.0806 0.0754 0.0098608 0.07880000000000001 6 4 4 null null null null null 3 2 2 null null null null null 3 2 2 null null null null null 3 2 2 10 1379 2021 null null null null null 3 2 2 null null null null null 3 2 2 0.05092325 0.121 0.1105 0.017247000000000002 0.116 7 4 4 null null null null null 3 2 2 7.42 25.75 25.75 5.3271945 20.3 8 5 1 0.602247 3.4 2.9 0.618568 2.9 9 6 3 11 751 2021 null null null null null 3 2 2 9.9369 40.0 33.3 6.04502 37.1 5 3 3 0.039563 0.087 0.077 0.013636 0.086 7 4 4 null null null null null 3 2 2 null null null null null 3 2 2 null null null null null 3 2 2 12 1031 2021 null null null null null 3 2 2 null null null null null 3 2 2 0.040121 0.067 0.064 0.011877 0.067 6 4 4 null null null null null 3 2 2 6.5563495 15.35 15.35 2.5102005 11.5 8 5 1 null null null null null 3 2 2 13 1363 2021 null null null null null 3 2 2 null null null null null 3 2 2 0.0444835 0.07675 0.07150000000000001 0.011167749999999999 0.07350000000000001 6 4 4 null null null null null 3 2 2 10.601328833333334 32.85 29.216666666666665 5.773344666666667 27.299999999999997 8 5 1 0.658242 6.6 2.8 0.639872 4.3 9 6 3 14 399 2021 null null null null null 3 2 2 null null null null null 3 2 2 0.04893 0.076 0.075 0.00995 0.075 6 4 4 null null null null null 3 2 2 null null null null null 3 2 2 null null null null null 3 2 2 15 3

AsthmaID YEAR NUMBER OF ED VISITS AGE-ADJUSTED ED VISIT RATE COUNTY_ID 1 2015 191904 50.4 null 2 2015 9939 64.3 3085.0 3 2015 196 58.4 843.0 4 2015 1044 50.2 152.0 5 2015 185 48.0 65.0 6 2015 97 41.4 545.0 7 2015 6858 65.2 46.0 8 2015 140 53.0 2947.0 9 2015 592 36.4 1751.0 10 2015 7936 77.0 2778.0 11 2015 122 42.6 2490.0 12 2015 835 63.4 224.0 13 2015 1388 71.2 1113.0 14 2015 88 53.5 1797.0 15 2015 5859 62.3 1697.0 16 2015 1250 78.6 1973.0 17 2015 478 80.4 603.0 18 2015 148 45.3 29.0 19 2015 52227 53.1 3118.0 20 2015 1031 62.3 2633.0 21 2015 541 22.2 2492.0 22 2015 79 47.4 1371.0 23 2015 479 57.4 568.0 24 2015 2425 87.4 318.0 25 2015 53 67.9 2173.0 26 2015 43 32.0 3048.0 27 2015 2194 50.2 2548.0 28 2015 572 41.9 1252.0 29 2015 351 42.8 134.0 30 2015 10275 33.9 2491.0 31 2015 1125 31.4 605.0 32 2015 99 56.3 1349.0 33 2015 10111 43.2 586.0 34 2015 10109 69.2 536.0 35 2015 285 50.1 2508.0 36 2015 12761 59.3 2590.0 37 2015 11646 37.0 2343.0 38 2015 3141 41.3 2816.0 39 2015 4802 66.2 2664.0 40 2015 950 40.1 2457.0 41 2015 2695 36.4 822.0 42 2015 1734 40.7 1796.0 43 2015 6521 35.1 1737.0 44 2015 910 36.5 222.0 45 2015 1015 60.5 3005.0 46 2015 176 47.0 534.0 47 2015 3415 83.2 1775.0 48 2015 1936 40.2 862.0 49 2015 3281 60.7 809.0 50 2015 337 34.1 2929.0 51 2015 323 52.7 1971.0 52 2015 67 60.5 2966.0 53 2015 2542 51.3 1720.0 54 2015 257 53.1 1144.0 55 2015 2933 35.3 1406.0 56 2015 852 44.1 1994.0 57 2015 346 45.4 782.0 58 2016 174733 45.8 null 59 2016 9086 57.8 3085.0 60 2016 187 61.8 843.0 61 2016 770 38.1 152.0 62 2016 171 45.3 65.0 63 2016 67 29.6 545.0 64 2016 6021 56.8 46.0 65 2016 172 71.1 2947.0 66 2016 564 35.5 1751.0 67 2016 6930 67.4 2778.0 68 2016 103 36.3 2490.0 69 2016 815 64.5 224.0 70 2016 1287 66.3 1113.0 71 2016 90 53.7 1797.0 72 2016 5008 54.5 1697.0 73 2016 1027 65.0 1973.0 74 2016 487 79.4 603.0 75 2016 118 40.7 29.0 76 2016 50778 51.5 3118.0 77 2016 956 60.2 2633.0 78 2016 543 23.1 2492.0 79 2016 66 45.3 1371.0 80 2016 451 56.4 568.0 81 2016 2211 79.2 318.0 82 2016 59 80.1 2173.0 83 2016 33 28.1 3048.0 84 2016 1959 44.3 2548.0 85 2016 439 33.5 1252.0 86 2016 267 33.6 134.0 87 2016 8878 29.2 2491.0 88 2016 968 28.3 605.0 89 2016 99 61.4 1349.0 90 2016 9596 41.5 586.0 91 2016 8953 60.7 536.0 92 2016 268 48.7 2508.0 93 2016 11335 51.9 2590.0 94 2016 10068 30.9 2343.0 95 2016 2997 38.5 2816.0 96 2016 4245 57.5 2664.0 97 2016 926 38.1 2457.0 98 2016 2382 32.5 822.0 99 2016 1641 37.7 1796.0 100 2016 5534 29.1 1737.0 101 2016 864 34.4 222.0 102 2016 726 46.4 3005.0 103 2016 128 33.7 534.0 104 2016 3349 80.8 1775.0 105 2016 1682 36.6 862.0 106 2016 2763 51.3 809.0 107 2016 324 33.7 2929.0 108 2016 335 55.9 1971.0 109 2016 55 52.7 2966.0 110 2016 1980 40.5 1720.0 111 2016 224 46.9 1144.0 112 2016 2619 32.4 1406.0 113 2016 774 38.4 1994.0 114 2016 297 39.2 782.0 115 2017 180053 46.9 null 116 2017 8942 56.3 3085.0 117 2017 176 56.8 843.0 118 2017 936 45.3 152.0 119 2017 198 55.1 65.0 120 2017 62 28.4 545.0 121 2017 6706 62.6 46.0 122 2017 150 61.2 2947.0 123 2017 650 40.5 1751.0 124 2017 7783 75.4 2778.0 125 2017 129 45.6 2490.0 126 2017 851 67.1 224.0 127 2017 1291 65.7 1113.0 128 2017 110 70.7 1797.0 129 2017 4853 52.2 1697.0 130 2017 1074 67.9 1973.0 131 2017 482 80.1 603.0 132 2017 131 44.0 29.0 133 2017 49504 50.0 3118.0 134 2017 979 61.7 2633.0 135 2017 564 23.5 2492.0 136 2017 63 46.5 1371.0 137 2017 567 70.9 568.0 138 2017 2067 73.9 318.0 139 2017 77 106.0 2173.0 140 2017 40 32.0 3048.0 141 2017 1916 43.1 2548.0 142 2017 537 40.2 1252.0 143 2017 306 38.5 134.0 144 2017 9084 29.7 2491.0 145 2017 1193 34.7 605.0 146 2017 86 63.2 1349.0 147 2017 10076 43.2 586.0 148 2017 10129 68.6 536.0 149 2017 340 61.2 2508.0 150 2017 11204 51.4 2590.0 151 2017 10339 31.7 2343.0 152 2017 3247 41.7 2816.0 153 2017 4881 65.9 2664.0 154 2017 800 33.3 2457.0 155 2017 2346 31.8 822.0 156 2017 1471 33.5 1796.0 157 2017 5865 30.7 1737.0 158 2017 772 29.8 222.0 159 2017 722 45.3 3005.0 160 2017 159 42.1 534.0 161 2017 3850 91.7 1775.0 162 20

In [0]:
# Create a table relating the asthma indices matched to AQ indices by county and year. 
# There is no more than one match for each but not always a match for all of them
import pandas as pd
matched = pd.DataFrame([])
count = 0
for countyAsthma in asthmaTotalDF.toLocalIterator():
    matchedCol = AQIDFAggDF.filter((AQIDFAggDF.COUNTY_ID == countyAsthma.COUNTY_ID) & (AQIDFAggDF.YEAR == countyAsthma.YEAR)).select('AQ_ID')  
    if(matchedCol.count() >0):
        matched = matched.append({'AsthmaID': countyAsthma.AsthmaID, 
                                  'AQ_ID': matchedCol.collect()[0][0]},
                                 ignore_index=True)
matched = spark.createDataFrame(matched)
display(matched)

AQ_ID AsthmaID 989.0 2.0 910.0 3.0 886.0 4.0 812.0 5.0 808.0 6.0 802.0 7.0 889.0 9.0 857.0 10.0 816.0 11.0 939.0 12.0 945.0 13.0 972.0 14.0 927.0 15.0 899.0 16.0 928.0 17.0 773.0 19.0 997.0 20.0 827.0 21.0 836.0 22.0 846.0 24.0 992.0 27.0 871.0 28.0 887.0 29.0 1004.0 30.0 1002.0 31.0 911.0 32.0 898.0 33.0 810.0 34.0 829.0 35.0 866.0 36.0 880.0 37.0 790.0 38.0 965.0 39.0 915.0 40.0 860.0 41.0 877.0 42.0 996.0 43.0 796.0 44.0 987.0 45.0 926.0 46.0 940.0 47.0 955.0 48.0 768.0 49.0 967.0 50.0 853.0 51.0 979.0 53.0 852.0 54.0 975.0 55.0 932.0 56.0 903.0 59.0 839.0 60.0 801.0 61.0 974.0 62.0 906.0 63.0 943.0 64.0 825.0 66.0 783.0 67.0 885.0 68.0 941.0 69.0 907.0 70.0 797.0 71.0 840.0 72.0 1013.0 73.0 771.0 74.0 985.0 76.0 917.0 77.0 861.0 78.0 986.0 79.0 781.0 81.0 822.0 84.0 962.0 85.0 841.0 86.0 776.0 87.0 803.0 88.0 929.0 89.0 933.0 90.0 983.0 91.0 950.0 92.0 863.0 93.0 774.0 94.0 874.0 95.0 1005.0 96.0 784.0 97.0 921.0 98.0 963.0 99.0 772.0 100.0 981.0 101.0 988.0 102.0 854.0 103.0 944.0 104.0 916.0 105.0 973.0 106.0 842.0 107.0 881.0 108.0 922.0 110.0 890.0 111.0 1000.0 112.0 956.0 113.0 982.0 116.0 946.0 117.0 837.0 118.0 769.0 119.0 872.0 120.0 964.0 121.0 862.0 123.0 894.0 124.0 847.0 125.0 879.0 126.0 1007.0 127.0 1011.0 128.0 800.0 129.0 834.0 130.0 904.0 131.0 895.0 133.0 804.0 134.0 792.0 135.0 838.0 136.0 819.0 138.0 850.0 141.0 805.0 142.0 961.0 143.0 843.0 144.0 828.0 145.0 1003.0 146.0 775.0 147.0 993.0 148.0 977.0 149.0 855.0 150.0 912.0 151.0 947.0 152.0 953.0 153.0 918.0 154.0 930.0 155.0 960.0 156.0 818.0 157.0 793.0 158.0 969.0 159.0 934.0 160.0 1009.0 161.0 900.0 162.0 936.0 163.0 858.0 164.0 848.0 165.0 942.0 167.0 913.0 168.0 959.0 169.0 870.0 170.0 978.0 173.0 952.0 174.0 1012.0 175.0 882.0 176.0 976.0 177.0 984.0 178.0 835.0 180.0 1008.0 181.0 787.0 182.0 778.0 183.0 951.0 184.0 883.0 185.0 891.0 186.0 914.0 187.0 777.0 188.0 817.0 190.0 966.0 191.0 859.0 192.0 980.0 193.0 815.0 195.0 869.0 197.0 794.0 198.0 924.0 199.0 935.0 200.0 830.0 201.0 998.0 202.0 919.0 203.0 873.0 204.0 920.0 205.0 896.0 206.0 925.0 207.0 856.0 208.0 845.0 209.0 779.0 210.0 791.0 211.0 864.0 212.0 931.0 213.0 878.0 214.0 909.0 215.0 948.0 216.0 949.0 218.0 868.0 219.0 767.0 220.0 888.0 221.0 990.0 222.0 923.0 223.0 785.0 225.0 820.0 226.0 995.0 227.0 788.0 228.0 994.0 231.0 957.0 232.0 798.0 233.0 908.0 234.0 971.0 235.0 770.0 236.0 905.0 238.0 809.0 239.0 844.0 240.0 831.0 241.0 1010.0 242.0 876.0 243.0 991.0 244.0 832.0 245.0 851.0 246.0 782.0 248.0 897.0 249.0 938.0 250.0 821.0 251.0 867.0 253.0 823.0 255.0 806.0 256.0 875.0 257.0 799.0 258.0 970.0 259.0 893.0 260.0 813.0 261.0 958.0 262.0 849.0 263.0 968.0 264.0 1006.0 265.0 1001.0 266.0 780.0 267.0 807.0 268.0 902.0 269.0 824.0 270.0 789.0 271.0 865.0 272.0 892.0 273.0 833.0 274.0 826.0 275.0 954.0 276.0 999.0 277.0 884.0 278.0 795.0 279.0 786.0 280.0 811.0 282.0 814.0 283.0 901.0 284.0 937.0 285.0

In [0]:
# Use a left outer join then
asthmaTotalDFjoined = asthmaTotalDF.join(matched, on='AsthmaID', how='left_outer')
display(asthmaTotalDFjoined)

AsthmaID YEAR NUMBER OF ED VISITS AGE-ADJUSTED ED VISIT RATE COUNTY_ID AQ_ID 1 2015 191904 50.4 null null 2 2015 9939 64.3 3085.0 989.0 3 2015 196 58.4 843.0 910.0 4 2015 1044 50.2 152.0 886.0 5 2015 185 48.0 65.0 812.0 6 2015 97 41.4 545.0 808.0 7 2015 6858 65.2 46.0 802.0 8 2015 140 53.0 2947.0 null 9 2015 592 36.4 1751.0 889.0 10 2015 7936 77.0 2778.0 857.0 11 2015 122 42.6 2490.0 816.0 12 2015 835 63.4 224.0 939.0 13 2015 1388 71.2 1113.0 945.0 14 2015 88 53.5 1797.0 972.0 15 2015 5859 62.3 1697.0 927.0 16 2015 1250 78.6 1973.0 899.0 17 2015 478 80.4 603.0 928.0 18 2015 148 45.3 29.0 null 19 2015 52227 53.1 3118.0 773.0 20 2015 1031 62.3 2633.0 997.0 21 2015 541 22.2 2492.0 827.0 22 2015 79 47.4 1371.0 836.0 23 2015 479 57.4 568.0 null 24 2015 2425 87.4 318.0 846.0 25 2015 53 67.9 2173.0 null 26 2015 43 32.0 3048.0 null 27 2015 2194 50.2 2548.0 992.0 28 2015 572 41.9 1252.0 871.0 29 2015 351 42.8 134.0 887.0 30 2015 10275 33.9 2491.0 1004.0 31 2015 1125 31.4 605.0 1002.0 32 2015 99 56.3 1349.0 911.0 33 2015 10111 43.2 586.0 898.0 34 2015 10109 69.2 536.0 810.0 35 2015 285 50.1 2508.0 829.0 36 2015 12761 59.3 2590.0 866.0 37 2015 11646 37.0 2343.0 880.0 38 2015 3141 41.3 2816.0 790.0 39 2015 4802 66.2 2664.0 965.0 40 2015 950 40.1 2457.0 915.0 41 2015 2695 36.4 822.0 860.0 42 2015 1734 40.7 1796.0 877.0 43 2015 6521 35.1 1737.0 996.0 44 2015 910 36.5 222.0 796.0 45 2015 1015 60.5 3005.0 987.0 46 2015 176 47.0 534.0 926.0 47 2015 3415 83.2 1775.0 940.0 48 2015 1936 40.2 862.0 955.0 49 2015 3281 60.7 809.0 768.0 50 2015 337 34.1 2929.0 967.0 51 2015 323 52.7 1971.0 853.0 52 2015 67 60.5 2966.0 null 53 2015 2542 51.3 1720.0 979.0 54 2015 257 53.1 1144.0 852.0 55 2015 2933 35.3 1406.0 975.0 56 2015 852 44.1 1994.0 932.0 57 2015 346 45.4 782.0 null 58 2016 174733 45.8 null null 59 2016 9086 57.8 3085.0 903.0 60 2016 187 61.8 843.0 839.0 61 2016 770 38.1 152.0 801.0 62 2016 171 45.3 65.0 974.0 63 2016 67 29.6 545.0 906.0 64 2016 6021 56.8 46.0 943.0 65 2016 172 71.1 2947.0 null 66 2016 564 35.5 1751.0 825.0 67 2016 6930 67.4 2778.0 783.0 68 2016 103 36.3 2490.0 885.0 69 2016 815 64.5 224.0 941.0 70 2016 1287 66.3 1113.0 907.0 71 2016 90 53.7 1797.0 797.0 72 2016 5008 54.5 1697.0 840.0 73 2016 1027 65.0 1973.0 1013.0 74 2016 487 79.4 603.0 771.0 75 2016 118 40.7 29.0 null 76 2016 50778 51.5 3118.0 985.0 77 2016 956 60.2 2633.0 917.0 78 2016 543 23.1 2492.0 861.0 79 2016 66 45.3 1371.0 986.0 80 2016 451 56.4 568.0 null 81 2016 2211 79.2 318.0 781.0 82 2016 59 80.1 2173.0 null 83 2016 33 28.1 3048.0 null 84 2016 1959 44.3 2548.0 822.0 85 2016 439 33.5 1252.0 962.0 86 2016 267 33.6 134.0 841.0 87 2016 8878 29.2 2491.0 776.0 88 2016 968 28.3 605.0 803.0 89 2016 99 61.4 1349.0 929.0 90 2016 9596 41.5 586.0 933.0 91 2016 8953 60.7 536.0 983.0 92 2016 268 48.7 2508.0 950.0 93 2016 11335 51.9 2590.0 863.0 94 2016 10068 30.9 2343.0 774.0 95 2016 2997 38.5 2816.0 874.0 96 2016 4245 57.5 2664.0 1005.0 97 2016 926 38.1 2457.0 784.0 98 2016 2382 32.5 822.0 921.0 99 2016 1641 37.7 1796.0 963.0 100 2016 5534 29.1 1737.0 772.0 101 2016 864 34.4 222.0 981.0 102 2016 726 46.4 3005.0 988.0 103 2016 128 33.7 534.0 854.0 104 2016 3349 80.8 1775.0 944.0 105 2016 1682 36.6 862.0 916.0 106 2016 2763 51.3 809.0 973.0 107 2016 324 33.7 2929.0 842.0 108 2016 335 55.9 1971.0 881.0 109 2016 55 52.7 2966.0 null 110 2016 1980 40.5 1720.0 922.0 111 2016 224 46.9 1144.0 890.0 112 2016 2619 32.4 1406.0 1000.0 113 2016 774 38.4 1994.0 956.0 114 2016 297 39.2 782.0 null 115 2017 180053 46.9 null null 116 2017 8942 56.3 3085.0 982.0 117 2017 176 56.8 843.0 946.0 118 2017 936 45.3 152.0 837.0 119 2017 198 55.1 65.0 769.0 120 2017 62 28.4 545.0 872.0 121 2017 6706 62.6 46.0 964.0 122 2017 150 61.2 2947.0 null 123 2017 650 40.5 1751.0 862.0 124 2017 7783 75.4 2778.0 894.0 125 2017 129 45.6 2490.0 847.0 126 2017 851 67.1 224.0 879.0 127 2017 1291 65.7 1113.0 1007.0 128 2017 110 70.7 1797.0 1011.0 129 2017 4853 52.2 1697.0 800.0 130 2017 1074 67.9 1973.0 834.0 131 2017 48

Look at the counties with missing air quality data. Let's see if there are missmatched spellings or other issues causing problems.

In [0]:
display(asthmaTotalDFjoined.filter((asthmaTotalDFjoined.AQ_ID.isNull())))

AsthmaID YEAR NUMBER OF ED VISITS AGE-ADJUSTED ED VISIT RATE COUNTY_ID AQ_ID 1 2015 191904 50.4 null null 8 2015 140 53.0 2947.0 null 18 2015 148 45.3 29.0 null 23 2015 479 57.4 568.0 null 25 2015 53 67.9 2173.0 null 26 2015 43 32.0 3048.0 null 52 2015 67 60.5 2966.0 null 57 2015 346 45.4 782.0 null 58 2016 174733 45.8 null null 65 2016 172 71.1 2947.0 null 75 2016 118 40.7 29.0 null 80 2016 451 56.4 568.0 null 82 2016 59 80.1 2173.0 null 83 2016 33 28.1 3048.0 null 109 2016 55 52.7 2966.0 null 114 2016 297 39.2 782.0 null 115 2017 180053 46.9 null null 122 2017 150 61.2 2947.0 null 132 2017 131 44.0 29.0 null 137 2017 567 70.9 568.0 null 139 2017 77 106.0 2173.0 null 140 2017 40 32.0 3048.0 null 166 2017 55 50.1 2966.0 null 171 2017 366 47.9 782.0 null 172 2018 163807 42.4 null null 179 2018 132 53.6 2947.0 null 189 2018 112 37.9 29.0 null 194 2018 507 62.4 568.0 null 196 2018 86 109.3 2173.0 null 217 2018 12 52.5 2547.0 null 224 2018 57 60.1 2966.0 null 229 2018 333 43.0 782.0 null 230 2019 165449 42.6 null null 237 2019 117 48.9 2947.0 null 247 2019 102 35.2 29.0 null 252 2019 489 60.0 568.0 null 254 2019 67 90.8 2173.0 null 281 2019 48 43.0 2966.0 null 286 2019 328 42.3 782.0 null

California is the statewide average. We can leave that in case we want to display that. The others don't appear to have any obvious mismatches in spelling. Some are missing for all years, while some are missing AQ data for one or two years. We will keep all of this is the dataset for now and handle it later before doing the model.

### 5. Move the data to a SQL database in our datalake

We need to first reorder the dataframe columns to match the schema in the database

Load in the air quality data first since the asthma data is linked to it

In [0]:
jdbcDF = spark.read.format("jdbc") \
    .option("url", url) \
    .option("dbtable", "CAAsthmaData") \
    .option("user", user) \
    .option("password", password) \
    .option("driver", "com.microsoft.sqlserver.jdbc.SQLServerDriver") \
    .load()
display(jdbcDF)
print(jdbcDF.printSchema())
asthmaTotalDFjoined = asthmaTotalDFjoined.select('AsthmaID', 'COUNTY_ID', 
                                                 'YEAR', 'NUMBER OF ED VISITS', 'AGE-ADJUSTED ED VISIT RATE', 'AQ_ID')

asthmaTotalDFjoined = asthmaTotalDFjoined.withColumn("AQ_ID", asthmaTotalDFjoined["AQ_ID"].cast('int'))
asthmaTotalDFjoined = asthmaTotalDFjoined.withColumn("COUNTY_ID", asthmaTotalDFjoined["COUNTY_ID"].cast('int'))
print(asthmaTotalDFjoined.printSchema())
try:
    asthmaTotalDFjoined = sqlContext.createDataFrame(asthmaTotalDFjoined.rdd, jdbcDF.schema)
except Exception as e:
    print(f"SCHEMA: {e}")
    



ASTHMA_ID COUNTY_ID YEAR NUM_ED_VISITS AGE_ADJ_ED_VISITS AQ_ID 1 null 2015 191904 50.4 null 2 3085 2015 9939 64.3 989 3 843 2015 196 58.4 910 4 152 2015 1044 50.2 886 5 65 2015 185 48.0 812 6 545 2015 97 41.4 808 7 46 2015 6858 65.2 802 8 2947 2015 140 53.0 null 9 1751 2015 592 36.4 889 10 2778 2015 7936 77.0 857 11 2490 2015 122 42.6 816 12 224 2015 835 63.4 939 13 1113 2015 1388 71.2 945 14 1797 2015 88 53.5 972 15 1697 2015 5859 62.3 927 16 1973 2015 1250 78.6 899 17 603 2015 478 80.4 928 18 29 2015 148 45.3 null 19 3118 2015 52227 53.1 773 20 2633 2015 1031 62.3 997 21 2492 2015 541 22.2 827 22 1371 2015 79 47.4 836 23 568 2015 479 57.4 null 24 318 2015 2425 87.4 846 25 2173 2015 53 67.9 null 26 3048 2015 43 32.0 null 27 2548 2015 2194 50.2 992 28 1252 2015 572 41.9 871 29 134 2015 351 42.8 887 30 2491 2015 10275 33.9 1004 31 605 2015 1125 31.4 1002 32 1349 2015 99 56.3 911 33 586 2015 10111 43.2 898 34 536 2015 10109 69.2 810 35 2508 2015 285 50.1 829 36 2590 2015 12761 59.3 866 37 2343 2015 11646 37.0 880 38 2816 2015 3141 41.3 790 39 2664 2015 4802 66.2 965 40 2457 2015 950 40.1 915 41 822 2015 2695 36.4 860 42 1796 2015 1734 40.7 877 43 1737 2015 6521 35.1 996 44 222 2015 910 36.5 796 45 3005 2015 1015 60.5 987 46 534 2015 176 47.0 926 47 1775 2015 3415 83.2 940 48 862 2015 1936 40.2 955 49 809 2015 3281 60.7 768 50 2929 2015 337 34.1 967 51 1971 2015 323 52.7 853 52 2966 2015 67 60.5 null 53 1720 2015 2542 51.3 979 54 1144 2015 257 53.1 852 55 1406 2015 2933 35.3 975 56 1994 2015 852 44.1 932 57 782 2015 346 45.4 null 58 null 2016 174733 45.8 null 59 3085 2016 9086 57.8 903 60 843 2016 187 61.8 839 61 152 2016 770 38.1 801 62 65 2016 171 45.3 974 63 545 2016 67 29.6 906 64 46 2016 6021 56.8 943 65 2947 2016 172 71.1 null 66 1751 2016 564 35.5 825 67 2778 2016 6930 67.4 783 68 2490 2016 103 36.3 885 69 224 2016 815 64.5 941 70 1113 2016 1287 66.3 907 71 1797 2016 90 53.7 797 72 1697 2016 5008 54.5 840 73 1973 2016 1027 65.0 1013 74 603 2016 487 79.4 771 75 29 2016 118 40.7 null 76 3118 2016 50778 51.5 985 77 2633 2016 956 60.2 917 78 2492 2016 543 23.1 861 79 1371 2016 66 45.3 986 80 568 2016 451 56.4 null 81 318 2016 2211 79.2 781 82 2173 2016 59 80.1 null 83 3048 2016 33 28.1 null 84 2548 2016 1959 44.3 822 85 1252 2016 439 33.5 962 86 134 2016 267 33.6 841 87 2491 2016 8878 29.2 776 88 605 2016 968 28.3 803 89 1349 2016 99 61.4 929 90 586 2016 9596 41.5 933 91 536 2016 8953 60.7 983 92 2508 2016 268 48.7 950 93 2590 2016 11335 51.9 863 94 2343 2016 10068 30.9 774 95 2816 2016 2997 38.5 874 96 2664 2016 4245 57.5 1005 97 2457 2016 926 38.1 784 98 822 2016 2382 32.5 921 99 1796 2016 1641 37.7 963 100 1737 2016 5534 29.1 772 101 222 2016 864 34.4 981 102 3005 2016 726 46.4 988 103 534 2016 128 33.7 854 104 1775 2016 3349 80.8 944 105 862 2016 1682 36.6 916 106 809 2016 2763 51.3 973 107 2929 2016 324 33.7 842 108 1971 2016 335 55.9 881 109 2966 2016 55 52.7 null 110 1720 2016 1980 40.5 922 111 1144 2016 224 46.9 890 112 1406 2016 2619 32.4 1000 113 1994 2016 774 38.4 956 114 782 2016 297 39.2 null 115 null 2017 180053 46.9 null 116 3085 2017 8942 56.3 982 117 843 2017 176 56.8 946 118 152 2017 936 45.3 837 119 65 2017 198 55.1 769 120 545 2017 62 28.4 872 121 46 2017 6706 62.6 964 122 2947 2017 150 61.2 null 123 1751 2017 650 40.5 862 124 2778 2017 7783 75.4 894 125 2490 2017 129 45.6 847 126 224 2017 851 67.1 879 127 1113 2017 1291 65.7 1007 128 1797 2017 110 70.7 1011 129 1697 2017 4853 52.2 800 130 1973 2017 1074 67.9 834 131 603 2017 482 80.1 904 132 29 2017 131 44.0 null 133 3118 2017 49504 50.0 895 134 2633 2017 979 61.7 804 135 2492 2017 564 23.5 792 136 1371 2017 63 46.5 838 137 568 2017 567 70.9 null 138 318 2017 2067 73.9 819 139 2173 2017 77 106.0 null 140 3048 2017 40 32.0 null 141 2548 2017 1916 43.1 850 142 1252 2017 537 40.2 805 143 134 2017 306 38.5 961 144 2491 2017 9084 29.7 843 145 605 2017 1193 34.7 828 146 1349 2017 86 63.2 1003 147 586 2017 10076 43.2 775 148 536 2017 10129 68.6 993 149 2508 2017 

root
-- ASTHMA_ID: integer (nullable = true)
-- COUNTY_ID: integer (nullable = true)
-- YEAR: integer (nullable = true)
-- NUM_ED_VISITS: integer (nullable = true)
-- AGE_ADJ_ED_VISITS: double (nullable = true)
-- AQ_ID: integer (nullable = true)

None
root
-- AsthmaID: long (nullable = false)
-- COUNTY_ID: integer (nullable = true)
-- YEAR: integer (nullable = true)
-- NUMBER OF ED VISITS: integer (nullable = true)
-- AGE-ADJUSTED ED VISIT RATE: double (nullable = true)
-- AQ_ID: integer (nullable = true)

None

In [0]:
asthmaTotalDFjoined = asthmaTotalDFjoined.drop("ASTHMA_ID")

In [0]:
try:
    writer = asthmaTotalDFjoined.write.format("jdbc").option("url", url) \
        .mode("append") \
        .option("dbtable", 'CAAsthmaData') \
        .option("user", user) \
        .option("password", password) \
        .option("driver", "com.microsoft.sqlserver.jdbc.SQLServerDriver")
    writer.save()
except Exception as e:
    print(e)

    df_loaded = spark.read.format("jdbc") \
        .option("url", url) \
        .option("dbtable", "CAAsthmaData") \
        .option("user", user) \
        .option("password", password) \
        .option("driver", "com.microsoft.sqlserver.jdbc.SQLServerDriver") \
        .load()
    print('df_loaded')
    display(df_loaded)   
        
    # Subtract the two to only leave what is not in the database
    # remove the index column of the loaded dataframe
    df_loaded = df_loaded.drop('ASTHMA_ID')
    df_toload = asthmaTotalDFjoined.subtract(df_loaded)
    print('df_toload')
    display(df_toload)
    
    if(df_toload.count() > 0):
        # Upload all the data that wasn't already in the database
        df_toload.write.format("jdbc")  \
            .option("url", url) \
            .mode("append") \
            .option("dbtable", "CAAsthmaData") \
            .option("user", user) \
            .option("password", password) \
            .option("driver", "com.microsoft.sqlserver.jdbc.SQLServerDriver") \
            .save()
    
asthmaTotalDF = spark.read.format("jdbc") \
    .option("url", url) \
    .option("dbtable", "CAAsthmaData") \
    .option("user", user) \
    .option("password", password) \
    .option("driver", "com.microsoft.sqlserver.jdbc.SQLServerDriver") \
    .load()
display(asthmaTotalDF) 

An error occurred while calling o65208.save.
: org.apache.spark.SparkException: Job aborted due to stage failure: Task 0 in stage 123648.0 failed 4 times, most recent failure: Lost task 0.3 in stage 123648.0 (TID 100043) (10.139.64.5 executor driver): java.sql.BatchUpdateException: Violation of UNIQUE KEY constraint 'uq_CAAsthmaData_CountyID_YEAR'. Cannot insert duplicate key in object 'dbo.CAAsthmaData'. The duplicate key value is (586, 2017).
	at com.microsoft.sqlserver.jdbc.SQLServerPreparedStatement.executeBatch(SQLServerPreparedStatement.java:2085)
	at org.apache.spark.sql.execution.datasources.jdbc.JdbcUtils$.savePartition(JdbcUtils.scala:731)
	at org.apache.spark.sql.execution.datasources.jdbc.JdbcUtils$.$anonfun$saveTable$1(JdbcUtils.scala:888)
	at org.apache.spark.sql.execution.datasources.jdbc.JdbcUtils$.$anonfun$saveTable$1$adapted(JdbcUtils.scala:886)
	at org.apache.spark.rdd.RDD.$anonfun$foreachPartition$2(RDD.scala:1025)
	at org.apache.spark.rdd.RDD.$anonfun$foreachPartition$2$adapted(RDD.scala:1025)
	at org.apache.spark.SparkContext.$anonfun$runJob$2(SparkContext.scala:2576)
	at org.apache.spark.scheduler.ResultTask.$anonfun$runTask$3(ResultTask.scala:75)
	at com.databricks.spark.util.ExecutorFrameProfiler$.record(ExecutorFrameProfiler.scala:110)
	at org.apache.spark.scheduler.ResultTask.$anonfun$runTask$1(ResultTask.scala:75)
	at com.databricks.spark.util.ExecutorFrameProfiler$.record(ExecutorFrameProfiler.scala:110)
	at org.apache.spark.scheduler.ResultTask.runTask(ResultTask.scala:55)
	at org.apache.spark.scheduler.Task.doRunTask(Task.scala:153)
	at org.apache.spark.scheduler.Task.$anonfun$run$1(Task.scala:122)
	at com.databricks.spark.util.ExecutorFrameProfiler$.record(ExecutorFrameProfiler.scala:110)
	at org.apache.spark.scheduler.Task.run(Task.scala:93)
	at org.apache.spark.executor.Executor$TaskRunner.$anonfun$run$13(Executor.scala:824)
	at org.apache.spark.util.Utils$.tryWithSafeFinally(Utils.scala:1621)
	at org.apache.spark.executor.Executor$TaskRunner.$anonfun$run$4(Executor.scala:827)
	at scala.runtime.java8.JFunction0$mcV$sp.apply(JFunction0$mcV$sp.java:23)
	at com.databricks.spark.util.ExecutorFrameProfiler$.record(ExecutorFrameProfiler.scala:110)
	at org.apache.spark.executor.Executor$TaskRunner.run(Executor.scala:683)
	at java.util.concurrent.ThreadPoolExecutor.runWorker(ThreadPoolExecutor.java:1149)
	at java.util.concurrent.ThreadPoolExecutor$Worker.run(ThreadPoolExecutor.java:624)
	at java.lang.Thread.run(Thread.java:748)

Driver stacktrace:
	at org.apache.spark.scheduler.DAGScheduler.failJobAndIndependentStages(DAGScheduler.scala:2973)
	at org.apache.spark.scheduler.DAGScheduler.$anonfun$abortStage$2(DAGScheduler.scala:2920)
	at org.apache.spark.scheduler.DAGScheduler.$anonfun$abortStage$2$adapted(DAGScheduler.scala:2914)
	at scala.collection.mutable.ResizableArray.foreach(ResizableArray.scala:62)
	at scala.collection.mutable.ResizableArray.foreach$(ResizableArray.scala:55)
	at scala.collection.mutable.ArrayBuffer.foreach(ArrayBuffer.scala:49)
	at org.apache.spark.scheduler.DAGScheduler.abortStage(DAGScheduler.scala:2914)
	at org.apache.spark.scheduler.DAGScheduler.$anonfun$handleTaskSetFailed$1(DAGScheduler.scala:1334)
	at org.apache.spark.scheduler.DAGScheduler.$anonfun$handleTaskSetFailed$1$adapted(DAGScheduler.scala:1334)
	at scala.Option.foreach(Option.scala:407)
	at org.apache.spark.scheduler.DAGScheduler.handleTaskSetFailed(DAGScheduler.scala:1334)
	at org.apache.spark.scheduler.DAGSchedulerEventProcessLoop.doOnReceive(DAGScheduler.scala:3182)
	at org.apache.spark.scheduler.DAGSchedulerEventProcessLoop.onReceive(DAGScheduler.scala:3123)
	at org.apache.spark.scheduler.DAGSchedulerEventProcessLoop.onReceive(DAGScheduler.scala:3111)
	at org.apache.spark.util.EventLoop$$anon$1.run(EventLoop.scala:49)
	at org.apache.spark.scheduler.DAGScheduler.runJob(DAGScheduler.scala:1096)
	at org.apache.spark.SparkContext.runJobInternal(SparkContext.scala:2536)
	at org.apache.spark.SparkContext.runJob(Spa

ASTHMA_ID COUNTY_ID YEAR NUM_ED_VISITS AGE_ADJ_ED_VISITS AQ_ID 1 null 2015 191904 50.4 null 2 3085 2015 9939 64.3 989 3 843 2015 196 58.4 910 4 152 2015 1044 50.2 886 5 65 2015 185 48.0 812 6 545 2015 97 41.4 808 7 46 2015 6858 65.2 802 8 2947 2015 140 53.0 null 9 1751 2015 592 36.4 889 10 2778 2015 7936 77.0 857 11 2490 2015 122 42.6 816 12 224 2015 835 63.4 939 13 1113 2015 1388 71.2 945 14 1797 2015 88 53.5 972 15 1697 2015 5859 62.3 927 16 1973 2015 1250 78.6 899 17 603 2015 478 80.4 928 18 29 2015 148 45.3 null 19 3118 2015 52227 53.1 773 20 2633 2015 1031 62.3 997 21 2492 2015 541 22.2 827 22 1371 2015 79 47.4 836 23 568 2015 479 57.4 null 24 318 2015 2425 87.4 846 25 2173 2015 53 67.9 null 26 3048 2015 43 32.0 null 27 2548 2015 2194 50.2 992 28 1252 2015 572 41.9 871 29 134 2015 351 42.8 887 30 2491 2015 10275 33.9 1004 31 605 2015 1125 31.4 1002 32 1349 2015 99 56.3 911 33 586 2015 10111 43.2 898 34 536 2015 10109 69.2 810 35 2508 2015 285 50.1 829 36 2590 2015 12761 59.3 866 37 2343 2015 11646 37.0 880 38 2816 2015 3141 41.3 790 39 2664 2015 4802 66.2 965 40 2457 2015 950 40.1 915 41 822 2015 2695 36.4 860 42 1796 2015 1734 40.7 877 43 1737 2015 6521 35.1 996 44 222 2015 910 36.5 796 45 3005 2015 1015 60.5 987 46 534 2015 176 47.0 926 47 1775 2015 3415 83.2 940 48 862 2015 1936 40.2 955 49 809 2015 3281 60.7 768 50 2929 2015 337 34.1 967 51 1971 2015 323 52.7 853 52 2966 2015 67 60.5 null 53 1720 2015 2542 51.3 979 54 1144 2015 257 53.1 852 55 1406 2015 2933 35.3 975 56 1994 2015 852 44.1 932 57 782 2015 346 45.4 null 58 null 2016 174733 45.8 null 59 3085 2016 9086 57.8 903 60 843 2016 187 61.8 839 61 152 2016 770 38.1 801 62 65 2016 171 45.3 974 63 545 2016 67 29.6 906 64 46 2016 6021 56.8 943 65 2947 2016 172 71.1 null 66 1751 2016 564 35.5 825 67 2778 2016 6930 67.4 783 68 2490 2016 103 36.3 885 69 224 2016 815 64.5 941 70 1113 2016 1287 66.3 907 71 1797 2016 90 53.7 797 72 1697 2016 5008 54.5 840 73 1973 2016 1027 65.0 1013 74 603 2016 487 79.4 771 75 29 2016 118 40.7 null 76 3118 2016 50778 51.5 985 77 2633 2016 956 60.2 917 78 2492 2016 543 23.1 861 79 1371 2016 66 45.3 986 80 568 2016 451 56.4 null 81 318 2016 2211 79.2 781 82 2173 2016 59 80.1 null 83 3048 2016 33 28.1 null 84 2548 2016 1959 44.3 822 85 1252 2016 439 33.5 962 86 134 2016 267 33.6 841 87 2491 2016 8878 29.2 776 88 605 2016 968 28.3 803 89 1349 2016 99 61.4 929 90 586 2016 9596 41.5 933 91 536 2016 8953 60.7 983 92 2508 2016 268 48.7 950 93 2590 2016 11335 51.9 863 94 2343 2016 10068 30.9 774 95 2816 2016 2997 38.5 874 96 2664 2016 4245 57.5 1005 97 2457 2016 926 38.1 784 98 822 2016 2382 32.5 921 99 1796 2016 1641 37.7 963 100 1737 2016 5534 29.1 772 101 222 2016 864 34.4 981 102 3005 2016 726 46.4 988 103 534 2016 128 33.7 854 104 1775 2016 3349 80.8 944 105 862 2016 1682 36.6 916 106 809 2016 2763 51.3 973 107 2929 2016 324 33.7 842 108 1971 2016 335 55.9 881 109 2966 2016 55 52.7 null 110 1720 2016 1980 40.5 922 111 1144 2016 224 46.9 890 112 1406 2016 2619 32.4 1000 113 1994 2016 774 38.4 956 114 782 2016 297 39.2 null 115 null 2017 180053 46.9 null 116 3085 2017 8942 56.3 982 117 843 2017 176 56.8 946 118 152 2017 936 45.3 837 119 65 2017 198 55.1 769 120 545 2017 62 28.4 872 121 46 2017 6706 62.6 964 122 2947 2017 150 61.2 null 123 1751 2017 650 40.5 862 124 2778 2017 7783 75.4 894 125 2490 2017 129 45.6 847 126 224 2017 851 67.1 879 127 1113 2017 1291 65.7 1007 128 1797 2017 110 70.7 1011 129 1697 2017 4853 52.2 800 130 1973 2017 1074 67.9 834 131 603 2017 482 80.1 904 132 29 2017 131 44.0 null 133 3118 2017 49504 50.0 895 134 2633 2017 979 61.7 804 135 2492 2017 564 23.5 792 136 1371 2017 63 46.5 838 137 568 2017 567 70.9 null 138 318 2017 2067 73.9 819 139 2173 2017 77 106.0 null 140 3048 2017 40 32.0 null 141 2548 2017 1916 43.1 850 142 1252 2017 537 40.2 805 143 134 2017 306 38.5 961 144 2491 2017 9084 29.7 843 145 605 2017 1193 34.7 828 146 1349 2017 86 63.2 1003 147 586 2017 10076 43.2 775 148 536 2017 10129 68.6 993 149 2508 2017 

df_toload

COUNTY_ID YEAR NUM_ED_VISITS AGE_ADJ_ED_VISITS AQ_ID

ASTHMA_ID COUNTY_ID YEAR NUM_ED_VISITS AGE_ADJ_ED_VISITS AQ_ID 1 null 2015 191904 50.4 null 2 3085 2015 9939 64.3 989 3 843 2015 196 58.4 910 4 152 2015 1044 50.2 886 5 65 2015 185 48.0 812 6 545 2015 97 41.4 808 7 46 2015 6858 65.2 802 8 2947 2015 140 53.0 null 9 1751 2015 592 36.4 889 10 2778 2015 7936 77.0 857 11 2490 2015 122 42.6 816 12 224 2015 835 63.4 939 13 1113 2015 1388 71.2 945 14 1797 2015 88 53.5 972 15 1697 2015 5859 62.3 927 16 1973 2015 1250 78.6 899 17 603 2015 478 80.4 928 18 29 2015 148 45.3 null 19 3118 2015 52227 53.1 773 20 2633 2015 1031 62.3 997 21 2492 2015 541 22.2 827 22 1371 2015 79 47.4 836 23 568 2015 479 57.4 null 24 318 2015 2425 87.4 846 25 2173 2015 53 67.9 null 26 3048 2015 43 32.0 null 27 2548 2015 2194 50.2 992 28 1252 2015 572 41.9 871 29 134 2015 351 42.8 887 30 2491 2015 10275 33.9 1004 31 605 2015 1125 31.4 1002 32 1349 2015 99 56.3 911 33 586 2015 10111 43.2 898 34 536 2015 10109 69.2 810 35 2508 2015 285 50.1 829 36 2590 2015 12761 59.3 866 37 2343 2015 11646 37.0 880 38 2816 2015 3141 41.3 790 39 2664 2015 4802 66.2 965 40 2457 2015 950 40.1 915 41 822 2015 2695 36.4 860 42 1796 2015 1734 40.7 877 43 1737 2015 6521 35.1 996 44 222 2015 910 36.5 796 45 3005 2015 1015 60.5 987 46 534 2015 176 47.0 926 47 1775 2015 3415 83.2 940 48 862 2015 1936 40.2 955 49 809 2015 3281 60.7 768 50 2929 2015 337 34.1 967 51 1971 2015 323 52.7 853 52 2966 2015 67 60.5 null 53 1720 2015 2542 51.3 979 54 1144 2015 257 53.1 852 55 1406 2015 2933 35.3 975 56 1994 2015 852 44.1 932 57 782 2015 346 45.4 null 58 null 2016 174733 45.8 null 59 3085 2016 9086 57.8 903 60 843 2016 187 61.8 839 61 152 2016 770 38.1 801 62 65 2016 171 45.3 974 63 545 2016 67 29.6 906 64 46 2016 6021 56.8 943 65 2947 2016 172 71.1 null 66 1751 2016 564 35.5 825 67 2778 2016 6930 67.4 783 68 2490 2016 103 36.3 885 69 224 2016 815 64.5 941 70 1113 2016 1287 66.3 907 71 1797 2016 90 53.7 797 72 1697 2016 5008 54.5 840 73 1973 2016 1027 65.0 1013 74 603 2016 487 79.4 771 75 29 2016 118 40.7 null 76 3118 2016 50778 51.5 985 77 2633 2016 956 60.2 917 78 2492 2016 543 23.1 861 79 1371 2016 66 45.3 986 80 568 2016 451 56.4 null 81 318 2016 2211 79.2 781 82 2173 2016 59 80.1 null 83 3048 2016 33 28.1 null 84 2548 2016 1959 44.3 822 85 1252 2016 439 33.5 962 86 134 2016 267 33.6 841 87 2491 2016 8878 29.2 776 88 605 2016 968 28.3 803 89 1349 2016 99 61.4 929 90 586 2016 9596 41.5 933 91 536 2016 8953 60.7 983 92 2508 2016 268 48.7 950 93 2590 2016 11335 51.9 863 94 2343 2016 10068 30.9 774 95 2816 2016 2997 38.5 874 96 2664 2016 4245 57.5 1005 97 2457 2016 926 38.1 784 98 822 2016 2382 32.5 921 99 1796 2016 1641 37.7 963 100 1737 2016 5534 29.1 772 101 222 2016 864 34.4 981 102 3005 2016 726 46.4 988 103 534 2016 128 33.7 854 104 1775 2016 3349 80.8 944 105 862 2016 1682 36.6 916 106 809 2016 2763 51.3 973 107 2929 2016 324 33.7 842 108 1971 2016 335 55.9 881 109 2966 2016 55 52.7 null 110 1720 2016 1980 40.5 922 111 1144 2016 224 46.9 890 112 1406 2016 2619 32.4 1000 113 1994 2016 774 38.4 956 114 782 2016 297 39.2 null 115 null 2017 180053 46.9 null 116 3085 2017 8942 56.3 982 117 843 2017 176 56.8 946 118 152 2017 936 45.3 837 119 65 2017 198 55.1 769 120 545 2017 62 28.4 872 121 46 2017 6706 62.6 964 122 2947 2017 150 61.2 null 123 1751 2017 650 40.5 862 124 2778 2017 7783 75.4 894 125 2490 2017 129 45.6 847 126 224 2017 851 67.1 879 127 1113 2017 1291 65.7 1007 128 1797 2017 110 70.7 1011 129 1697 2017 4853 52.2 800 130 1973 2017 1074 67.9 834 131 603 2017 482 80.1 904 132 29 2017 131 44.0 null 133 3118 2017 49504 50.0 895 134 2633 2017 979 61.7 804 135 2492 2017 564 23.5 792 136 1371 2017 63 46.5 838 137 568 2017 567 70.9 null 138 318 2017 2067 73.9 819 139 2173 2017 77 106.0 null 140 3048 2017 40 32.0 null 141 2548 2017 1916 43.1 850 142 1252 2017 537 40.2 805 143 134 2017 306 38.5 961 144 2491 2017 9084 29.7 843 145 605 2017 1193 34.7 828 146 1349 2017 86 63.2 1003 147 586 2017 10076 43.2 775 148 536 2017 10129 68.6 993 149 2508 2017 